#### El objetivo de este notebook es poder realizar una exploracion de terms, tablas, queries y otras informaciones sobre el subdominio de prestamos para nutrir un modelo de chat GPT 3.5 y obtener tiempos reducidos en iteraciones

In [9]:
# Traigo dependencias
import requests
from requests.auth import HTTPBasicAuth
import os
import json
from pyhive import hive
import pandas as pd
import sys
from datetime import datetime
import re
import sqlparse

In [72]:
def _find_valid_atlas_instance(atlas_instances_list, port, credentials):
    for instance in atlas_instances_list:
        full_instance = f"http://{instance}:{port}/api/atlas"
        try:
            if requests.get(url=f"{full_instance}/v2/types/typedefs/headers",auth=credentials).status_code == 200:
                return full_instance
        except:
            pass
    raise Exception("No valid instance for Apache Atlas in {}".format(atlas_instances_list))
class AtlasHandler:
    def __init__(self, hosts, port, credentials):
        self.atlas_instance = _find_valid_atlas_instance(hosts, port, credentials)
        self.credentials = credentials
        self.headers = {"Content-Type" : "application/json",
                        "Accept" : "application/json"}
        
    def find_atlas_term_by_guid(self, term_guid):
        found_atlas_term = requests.get(url="{instance}/v2/glossary/term/{termGuid}".format(instance=self.atlas_instance, termGuid=term_guid),auth=self.credentials)
        return json.loads(found_atlas_term.text)
        
    def entity_search(self, type, name):
        def _get_right_entity(entities, searched_entity_name):
            for entity in entities:
                if entity["attributes"]["name"] == searched_entity_name:
                    return entity   
        search_results = requests.get(url="{instance}/v2/search/dsl?query=from%20{entity_type}%20where%20name%20%3D%20'{entity_name}'&typeName={entity_type}".format(instance=self.atlas_instance,entity_type=type, entity_name=name),
                                    auth=self.credentials).text
        search_results = json.loads(search_results)
        if not search_results.get('entities'):
            raise Exception("No entity of type '{type}' and name '{name}' exists in environment ({instance}).".format(type=type,name=name,instance=self.atlas_instance))
        atlas_term_entity = _get_right_entity(search_results["entities"], name)
        return atlas_term_entity
    
    def find_classification_ids(self, classification_name):
        found_classification = requests.get(url="{instance}/v2/types/classificationdef/name/{name}".format(instance=self.atlas_instance, name=classification_name),auth=self.credentials).text
        return found_classification
    
    def create_glossary(self, glossary_name):
        # Define the glossary information
        glossary_payload = {
            "name": glossary_name
        }
        
        # Make the POST request with authentication
        response = requests.post(url="{instance}/v2/glossary".format(instance=self.atlas_instance), 
                                 json=glossary_payload, 
                                 headers=self.headers,
                                 auth=self.credentials)
        if response.status_code == 200:
            print("Glossary created successfully.")
            #self.logger.log("Created glossary", response.text, self.atlas_instance)
            return json.loads(response.text)["guid"]
        else:
            raise Exception(f"Error creating glossary: {response.status_code} - {response.text}")
    
    def adapt_term_to_env(self, term_to_deploy, force):
        def _find_glossary_guid(glossary_term):
            glossary_entity=self.entity_search("AtlasGlossary", glossary_term)
            return glossary_entity["guid"]
        def _fetch_classifications(term_to_deploy):
            classifications = []
            for classification in term_to_deploy["classifications"]:
                resulting_classification = {}
                resulting_classification["typeName"] = classification["typeName"]
                resulting_classification["attributes"] = classification["attributes"]
                classifications.append(resulting_classification)
            return classifications
            
        # Define the glossary term payload      
        glossary_name = term_to_deploy["attributes"]["qualifiedName"].split('@')[1]
        try:
            glossary_guid = _find_glossary_guid(glossary_name)
        except:
            if not force:
                # Ask the user if they want to create the glossary
                create_glossary = ""
                while create_glossary not in ('y','n'):
                    create_glossary = input("Glossary '{glossary}' does not exists in the destination env. Do you want to create it? (y/n): ".format(glossary=glossary_name)).lower()
                    if create_glossary == 'y':
                        glossary_guid = self.create_glossary(glossary_name)
                        time.sleep(8)
                    elif create_glossary == 'n':
                        sys.exit()
            else:
                glossary_guid = self.create_glossary(glossary_name)
                time.sleep(8)
        term_name = term_to_deploy["attributes"]["name"]
        term_payload = {
            "glossaryName": glossary_name,
            "name": term_name,
            "qualifiedName": term_name+"@"+glossary_name,
            "anchor": {"glossaryGuid": glossary_guid}
        }
        term_payload["classifications"] = _fetch_classifications(term_to_deploy)        
        return term_payload
                    
    def delete_term(self, term_payload):
        def _find_term_guid(term_name):
            glossary_entity=self.entity_search("AtlasGlossaryTerm", term_name)
            return glossary_entity["guid"]
        # Make the POST request with authentication
        term_name = term_payload['name']
        term_qualifiedName = term_payload["qualifiedName"]
        term_guid = _find_term_guid(term_name)
        
        response = requests.delete(url="{instance}/v2/glossary/term/{term_id}".format(instance=self.atlas_instance,term_id=term_guid), 
                                 headers=self.headers,
                                 auth=self.credentials)
        if response.status_code == 204:
            print("Glossary term '{name}' ({guid}) deleted successfully.".format(name=term_qualifiedName, guid=term_guid))
            #self.logger.log("Deleted term", {"msg":"Glossary term '{name}' ({guid}) deleted successfully.".format(name=term_qualifiedName, guid=term_guid)}, self.atlas_instance)
            return response
        else:
            print(f"Error deleting atlas glossary term: {response.status_code} - {response.text}")
            return response
    
    def create_glossary_term(self, term_payload, force):
        # Make the POST request with authentication
        response = requests.post(url="{instance}/v2/glossary/term".format(instance=self.atlas_instance), 
                                 json=term_payload, 
                                 headers=self.headers,
                                 auth=self.credentials)
        if response.status_code == 200:
            print("Glossary term created successfully.")
            #self.logger.log("Created glossary term", term_payload, self.atlas_instance)
            return response
        elif response.status_code == 409:
            if not force:
                update_term = ""
                while update_term not in ('y','n'):
                    update_term = input("Atlas term with qualified name '{qualifiedName}' already exists in the destination env. Do you want to delete and re-create it? (y/n): ".format(qualifiedName=term_payload["qualifiedName"])).lower()
                    if update_term == 'y':
                        self.delete_term(term_payload)
                        self.create_glossary_term(term_payload, force)
                    elif update_term == 'n':
                        exit
                    else:
                        pass
                return response
            else:
                self.delete_term(term_payload)
                self.create_glossary_term(term_payload, force)
        else:
            print(f"Error creating glossary term: {response.status_code} - {response.text}")
            return response
        
    def get_glossaries(self):
        search_results = requests.get(url=f"{self.atlas_instance}/v2/glossary",auth=self.credentials).text
        search_results = json.loads(search_results)
        return search_results


In [73]:
'''Variables'''
## Atlas dev
headers = {
    "Content-Type": "application/json",
    "Accept": "application/json"
}
credentials = HTTPBasicAuth('atlasadmin', 'xNB8lZ!Dut')
atlas_urls = ["172.30.213.141","172.30.213.142"]
atlas_port = 31000

## Hive dev
hive_host = 'edh-master-01d.root.corp'
hive_port = 10000
hive_user = 'admin'

In [74]:
atlas_handler = AtlasHandler(atlas_urls, atlas_port, credentials)
#atlas_handler.get_glossaries()

In [60]:
from concurrent.futures import ThreadPoolExecutor, as_completed

In [119]:
'''Scripts para scanear todo el atlas y listar por cada tabla mencionada a que termino esta asociado
para hacer la busqueda invertida en tiempo real a posterior
WARNING: Tarda aprox 30/40 minutos en correr'''

def download_tables_per_term(target_path, handler):
    table_term_mapping = {}
    glossaries = handler.get_glossaries()
    for glossary in glossaries:    #por cada glosario encontrado
        glossary_name = glossary.get('qualifiedName')
        found_terms = glossary.get("terms")
        if found_terms:                            #me fijo si terms esta vacio o no, si no esta sigo
            for term in found_terms:               #por cada term en la lista de terms encontrados
                term_name = term.get('displayText')
                term_guid = term.get('termGuid')
                term_json = handler.find_atlas_term_by_guid(term_guid)
                term_classifications = term_json.get('classifications')
                if term_classifications:
                    for classification in term_classifications:
                        if classification.get('attributes'):
                            for k,v in classification['attributes'].items():
                                if 'Tabla' in k:
                                    mapping = {"term_name": term_name,
                                                "term_guid": term_guid,
                                                "term_glossary": glossary_name,
                                                "table_key": k}
                                    if table_term_mapping.get(v):
                                        table_term_mapping[v] = table_term_mapping[v] + [mapping]
                                    else:
                                        table_term_mapping[v] = [mapping]
    try:
        with open(f'{target_path}/table_term_mapping.json', 'w+') as f:
            final_obj = {
                "table_info": table_term_mapping,
                "last_updated": str(datetime.now().strftime('%Y-%m-%d %H:%M:%S'))
            }
            str_object = json.dumps(final_obj, indent=2)
            f.write(str_object)
    except:
        print(json.dumps(table_term_mapping, indent=2))

In [61]:
from concurrent.futures import ThreadPoolExecutor, as_completed

def process_glossary(glossary, handler, table_term_mapping):
    glossary_name = glossary.get('qualifiedName')
    found_terms = glossary.get("terms")
    if found_terms:
        for term in found_terms:
            term_name = term.get('displayText')
            term_guid = term.get('termGuid')
            term_json = handler.find_atlas_term_by_guid(term_guid)
            term_classifications = term_json.get('classifications')
            if term_classifications:
                for classification in term_classifications:
                    if classification.get('attributes'):
                        for k, v in classification['attributes'].items():
                            if 'Tabla' in k:
                                mapping = {"term_name": term_name,
                                           "term_guid": term_guid,
                                           "term_glossary": glossary_name,
                                           "table_key": k}
                                if table_term_mapping.get(v):
                                    table_term_mapping[v] = table_term_mapping[v] + [mapping]
                                else:
                                    table_term_mapping[v] = [mapping]

def download_tables_per_term(target_path, handler):
    table_term_mapping = {}
    glossaries = handler.get_glossaries()

    with ThreadPoolExecutor(max_workers=5) as executor:
        futures = [executor.submit(process_glossary, glossary, handler, table_term_mapping) for glossary in glossaries]

        for future in as_completed(futures):
            try:
                future.result()
            except Exception as e:
                print(f"Error processing glossary: {e}")

    try:
        with open(f'{target_path}/table_term_mapping.json', 'w+') as f:
            final_obj = {
                "table_info": table_term_mapping,
                "last_updated": str(datetime.now().strftime('%Y-%m-%d %H:%M:%S'))
            }
            str_object = json.dumps(final_obj, indent=2)
            f.write(str_object)
    except Exception as e:
        print(f"Error writing to file: {e}")


In [64]:
path = '/home/lautaroperezcarmona/Desktop/atlas_downloads'
download_tables_per_term(path, atlas_handler)

#### ¿que ocurre de acá en adelante?

In [65]:
# Cargo el diccionario de tablas-terminos en memoria
f = open(f'{path}/table_term_mapping.json', 'r+')
table_term_mapping = json.load(f)
f.close()
table_term_mapping = table_term_mapping.get('table_info')


In [67]:
## Defino tablas afectadas por subdominio de prestamos
tablas_prestamos = ["productos_parametria_dim_productos",
                    "productos_prestamos_dim_maestro",
                    "can_ges_parametria_dim_sucursales",
                    "productos_parametria_dim_moneda",
                    "productos_parametria_dim_periodocpa",
                    "productos_parametria_dim_origen_fondos",
                    "productos_parametria_dim_sist_amort",
                    "productos_parametria_dim_tipo_tasa",
                    "productos_parametria_dim_codigos_tasa",
                    "productos_parametria_dim_toma_disp_fondo",
                    "productos_parametria_dim_punto_vta",
                    "productos_parametria_dim_atrib_cont_bcra",
                    "productos_parametria_dim_destino_econom",
                    "productos_parametria_dim_acordante",
                    "productos_parametria_dim_relacion_titularidad",
                    "clientes_datos_identificatorios_dim",
                    "productos_parametria_ft_calendario_saldo",
                    "productos_parametria_dim_operativa_contable",
                    "productos_contabilidad_dim_maestro_plan_cuentas",
                    "productos_prestamo_transacciones",
                    "productos_cta_corriente_dim_maestro",
                    "productos_ca_dim_tasas_interes",
                    "productos_garantias_dim_maestro",
                    "productos_garantias_rel_operaciones",
                    "productos_prestamos_ft_movimientos_historico",
                    "productos_cta_corriente_ft_maestro_historico",
                    "productos_prestamos_dim_cuotas_generadas",
                    "productos_prestamos_ft_gastos_cuotas",
                    "dt_productos_prestamos_dim_cuotas_procesadas",
                    #"productos_previsiones_dim", no desarrollada aun
                    "productos_lineas_especiales_dim",
                    "productos_prestamos_rel_prefinanciados_productos",
                    "productos_contabilidad_dim_maestro_causales",
                    "productos_prestamos_dim_maestro_vendedores",
                    "productos_prestamos_rel_carpeta_cliente"]

In [68]:
def extract_table_names(query):
    # Match 'FROM' or 'JOIN' followed by optional whitespace and then capture table name
    regex = r'(?:FROM|JOIN)\s+([^\s,]+)'
    matches = re.findall(regex, query, re.IGNORECASE)
    return matches
# se usa esta
def extract_table_names(query):
    # Match 'FROM' or 'JOIN' followed by optional whitespace and then capture table name
    regex = r'(?:FROM|JOIN)\s+([$a-zA-Z_][^\s,]+)'
    matches = re.findall(regex, query, re.IGNORECASE)
    return matches

In [75]:
def get_tables_loading_information(handler, table_list):
    tables_not_found = set()
    searched_terms = set()
    full_analysis = {}
    search_level = 1
    next_level_tables_to_search = []
    while True:
        #print("DEBUG - SEARCH LEVEL:", search_level)
        search_level_found_info = []
        #step 1: fetch tables to search in this level
        if search_level == 1:
            tables_to_search_in_this_level = table_list
        else:
            tables_to_search_in_this_level = next_level_tables_to_search.copy()
            next_level_tables_to_search = []
        if not tables_to_search_in_this_level:
            break
        #step 2: fetch info associated with tables
        for table in tables_to_search_in_this_level:
            #print("INFO - Table searched:", table)
            #if table not in searched_tables:
            table_info_list = table_term_mapping.get(table.lower())
            if not table_info_list:
                tables_not_found.add(table)
            else:
                for table_info in table_info_list:
                    term_guid = table_info.get('term_guid')
                    if term_guid not in searched_terms:
                        #step 3: process table starting from table info
                        term = handler.find_atlas_term_by_guid(table_info.get('term_guid'))
                        #save table as searched
                        searched_terms.add(term_guid)
                        for classification in term['classifications']:
                            findings = {"associated_term": table_info.get('term_name'),
                                        "zone": None,
                                        "table": None,
                                        "query": None,
                                        "affected_tables": None}
                            if classification.get('attributes'):
                                if classification.get('typeName') == 'params pipes ingesta':
                                    findings["zone"] = "RAW"
                                    findings["table"] = classification.get('attributes').get('ING Tabla RAW')
                                    findings_raw = findings.copy()
                                    search_level_found_info.append(findings_raw)

                                    findings["zone"] = "CUR"
                                    findings["table"] = classification.get('attributes').get('ING Tabla CUR')
                                    findings["query"] = classification.get('attributes').get('ING Query CUR')
                                    
                                
                                else:
                                    for k,v in classification['attributes'].items():
                                        if 'tabla' in k.lower():
                                            #print(f"Found table key: {k} with value: {v}\n")
                                            zone_split = k.split(' ')
                                            findings["zone"] = zone_split[0]
                                            findings["table"] = v
                                
                                        if 'query' in k.lower() and not 'motor' in k.lower() and not 'post' in k.lower() and not 'query pre-insert' in k.lower() and v:
                                            #print(f"Found query key: {k} with value: {v}\n")
                                            findings["query"] = v
                                        
                                if findings.get("query"):
                                    # Extract table names from the query
                                    findings['affected_tables'] = list(set(filter(lambda x: '.' in x, map(lambda x: x.replace('(', '').replace(')', ''), extract_table_names(findings.get("query"))))))
                                    affected_tables_without_db = list(map(lambda x: x.split('.')[1],findings['affected_tables']))
                                next_level_tables_to_search.extend(affected_tables_without_db)
                            if findings['table']:
                                if findings["zone"] == "INSERTKUDU":
                                    if list(filter(lambda x: '4con' in x, findings['affected_tables'])):
                                        findings["zone"] = "DATAMART"
                                    else:
                                        findings["zone"] = "CON"
                                search_level_found_info.append(findings)
        full_analysis["level_%d" % search_level] = search_level_found_info
        search_level += 1
    full_analysis['tables_not_found'] = list(tables_not_found)
    return full_analysis

full_analysis = get_tables_loading_information(atlas_handler, tablas_prestamos)
print(json.dumps(full_analysis, indent=2))

{
  "level_1": [
    {
      "associated_term": "productos_parametria_dim_productos_unisys",
      "zone": "CON",
      "table": "productos_parametria_dim_productos",
      "query": "SELECT id_concepto AS id_concepto, cod_producto AS cod_producto, id_moneda AS id_moneda, fecha_proceso AS fecha_proceso, id_producto AS id_producto, marca_sfb AS marca_sfb, marca_producto_cta_comitente AS marca_producto_cta_comitente, cast(fecha_vencimiento_producto as varchar(10)) AS fecha_vencimiento_producto, cast(fecha_vigencia_producto as varchar(10)) AS fecha_vigencia_producto, desc_producto AS desc_producto, nro_campo_c_467 AS nro_campo_c_467, nro_campo_garantia AS nro_campo_garantia, nro_campo_lisol AS nro_campo_lisol, factor_ponderacion AS factor_ponderacion, fecha_vencimiento_producto_rel AS fecha_vencimiento_producto_rel, fecha_vigencia_producto_rel AS fecha_vigencia_producto_rel, estado AS estado, marca_producto_privado AS marca_producto_privado FROM $SUBENTORNO_$ENTIDAD_3ref.productos_parametr

In [76]:
## Flatten tables loading information to same level
def flatten_tables_loading_information(full_analysis):
    flattened_analysis = []
    for level, level_info in full_analysis.items():
        for table_info in level_info:
            flattened_analysis.append(table_info)
    return flattened_analysis

flattened_analysis = flatten_tables_loading_information(full_analysis)
print(json.dumps(flattened_analysis, indent=2))


[
  {
    "associated_term": "productos_parametria_dim_productos_unisys",
    "zone": "CON",
    "table": "productos_parametria_dim_productos",
    "query": "SELECT id_concepto AS id_concepto, cod_producto AS cod_producto, id_moneda AS id_moneda, fecha_proceso AS fecha_proceso, id_producto AS id_producto, marca_sfb AS marca_sfb, marca_producto_cta_comitente AS marca_producto_cta_comitente, cast(fecha_vencimiento_producto as varchar(10)) AS fecha_vencimiento_producto, cast(fecha_vigencia_producto as varchar(10)) AS fecha_vigencia_producto, desc_producto AS desc_producto, nro_campo_c_467 AS nro_campo_c_467, nro_campo_garantia AS nro_campo_garantia, nro_campo_lisol AS nro_campo_lisol, factor_ponderacion AS factor_ponderacion, fecha_vencimiento_producto_rel AS fecha_vencimiento_producto_rel, fecha_vigencia_producto_rel AS fecha_vigencia_producto_rel, estado AS estado, marca_producto_privado AS marca_producto_privado FROM $SUBENTORNO_$ENTIDAD_3ref.productos_parametria_dim_productos WHERE fe

In [77]:
## Create a dict zone-table containing a json with all the information of associated term and query
def create_zone_table_dict(flattened_analysis):
    zone_table_dict = {}
    for flattened_table_info in flattened_analysis:
        try:
            zone = flattened_table_info['zone'].lower()
            table = flattened_table_info.get('table')
            term = flattened_table_info.get('associated_term')
            unisys_bsf = 'bsf' if 'bsf' in term else 'unisys' if 'unisys' in term else 'any'
            zone_table_term = zone+';'+table+';'+unisys_bsf
            zone_table_dict[zone_table_term] = {
                "associated_term": term,
                "query": flattened_table_info.get('query'),
            }
        except:
            pass
    return zone_table_dict

zone_table_dict = create_zone_table_dict(flattened_analysis)
print(json.dumps(zone_table_dict, indent=2))

{
  "con;productos_parametria_dim_productos;unisys": {
    "associated_term": "productos_parametria_dim_productos_unisys",
    "query": "SELECT id_concepto AS id_concepto, cod_producto AS cod_producto, id_moneda AS id_moneda, fecha_proceso AS fecha_proceso, id_producto AS id_producto, marca_sfb AS marca_sfb, marca_producto_cta_comitente AS marca_producto_cta_comitente, cast(fecha_vencimiento_producto as varchar(10)) AS fecha_vencimiento_producto, cast(fecha_vigencia_producto as varchar(10)) AS fecha_vigencia_producto, desc_producto AS desc_producto, nro_campo_c_467 AS nro_campo_c_467, nro_campo_garantia AS nro_campo_garantia, nro_campo_lisol AS nro_campo_lisol, factor_ponderacion AS factor_ponderacion, fecha_vencimiento_producto_rel AS fecha_vencimiento_producto_rel, fecha_vigencia_producto_rel AS fecha_vigencia_producto_rel, estado AS estado, marca_producto_privado AS marca_producto_privado FROM $SUBENTORNO_$ENTIDAD_3ref.productos_parametria_dim_productos WHERE fecha_proceso='$FECHA_P

In [78]:
def generate_adjacency_list(full_analysis):
    adjacency_list = {}
    for level in full_analysis.keys():
        if level != 'tables_not_found':
            for analysed_table in full_analysis[level]:
                if not analysed_table['zone']+'-'+analysed_table['table'] in adjacency_list.keys():
                    adjacency_list[analysed_table['zone']+'-'+analysed_table['table']] = []
                affected_tables = analysed_table['affected_tables']
                if affected_tables:
                    for affected_table in affected_tables:
                        affected_table_db, affected_table_table_name = affected_table.split('.')
                        if 'raw' in affected_table_db.lower():
                            affected_table_zone = 'RAW'
                        if 'cur' in affected_table_db.lower():
                            affected_table_zone = 'CUR'
                        if 'ref' in affected_table_db.lower():
                            affected_table_zone = 'REF'
                        if 'con' in affected_table_db.lower():
                            affected_table_zone = 'CON'
                        if 'datamart' in affected_table_db.lower():
                            affected_table_zone = 'DATAMART'
                        affected_table_full_name = affected_table_zone+'-'+affected_table_table_name.lower()
                        if affected_table_full_name not in adjacency_list.keys():
                            adjacency_list[affected_table_full_name] = []
                        if not analysed_table['zone']+'-'+analysed_table['table'] in adjacency_list[affected_table_full_name]:
                            adjacency_list[affected_table_full_name].append(analysed_table['zone']+'-'+analysed_table['table'])
    return adjacency_list
table_adj_list = generate_adjacency_list(full_analysis)
print(json.dumps(table_adj_list, indent=2))
    

{
  "CON-productos_parametria_dim_productos": [
    "DATAMART-productos_prestamos_dim_maestro"
  ],
  "REF-productos_parametria_dim_productos": [
    "CON-productos_parametria_dim_productos"
  ],
  "CUR-productos_aampr": [
    "REF-productos_parametria_dim_productos",
    "REF-productos_cta_corriente_dim_maestro",
    "REF-productos_garantias_dim_maestro"
  ],
  "REF-productos_prestamos_dim_maestro": [
    "CON-productos_prestamos_dim_maestro"
  ],
  "CUR-productos_pprpc": [
    "REF-productos_prestamos_dim_maestro"
  ],
  "CUR-productos_ppaso": [
    "REF-productos_prestamos_dim_maestro"
  ],
  "CUR-productos_ppmap": [
    "REF-productos_prestamos_dim_maestro",
    "REF-productos_prestamos_ft",
    "REF-productos_prestamos_dim"
  ],
  "CUR-productos_cuotas_duration": [
    "REF-productos_prestamos_dim_maestro"
  ],
  "CUR-productos_ppmpr": [
    "REF-productos_prestamos_dim_maestro"
  ],
  "CON-productos_prestamos_dim_maestro": [
    "DATAMART-productos_prestamos_dim_maestro"
  ],
  "

In [79]:
print(len(table_adj_list.keys()))
print(table_adj_list.keys())

333
dict_keys(['CON-productos_parametria_dim_productos', 'REF-productos_parametria_dim_productos', 'CUR-productos_aampr', 'REF-productos_prestamos_dim_maestro', 'CUR-productos_pprpc', 'CUR-productos_ppaso', 'CUR-productos_ppmap', 'CUR-productos_cuotas_duration', 'CUR-productos_ppmpr', 'CON-productos_prestamos_dim_maestro', 'DATAMART-productos_prestamos_dim_maestro', 'CON-productos_cta_corriente_dim_maestro', 'CON-clientes_datos_identificatorios_dim', 'CON-can_ges_parametria_dim_sucursales', 'CON-productos_parametria_dim_acordante', 'CON-productos_parametria_dim_origen_fondos', 'CON-productos_parametria_dim_punto_vta', 'CON-productos_parametria_dim_codigos_tasa', 'CON-productos_parametria_dim_destino_econom', 'CON-productos_dim_maestro_valores_sesion', 'CON-productos_prestamos_dim_cuotas_generadas', 'CON-productos_parametria_ft_calendario_saldo', 'CON-productos_ca_dim_tasas_interes', 'CON-productos_parametria_dim_moneda', 'CON-productos_parametria_dim_estado_ppmap', 'CON-productos_prest

In [83]:
# Create a Hive connection raw
hive_database_raw = 'de_ber_1raw'
table_name_raw = 'sfb_aamve'
hive_conn_raw = hive.connect(host=hive_host, port=hive_port, username=hive_user, database=hive_database_raw)
# Create a Hive cursor
hive_cursor_raw = hive_conn_raw.cursor()


# List all databases in Hive
hive_cursor_raw.execute('SHOW DATABASES')
databases = list(map(lambda x: x[0], hive_cursor_raw.fetchall()))
databases_dict = {}
grouped_tables_by_zone = {}

# List tables in Hive database
for database in databases:
    if 'raw' in database or 'cur' in database or 'ref' in database or 'con' in database:
        if 'raw' in database:
            zone = 'RAW'
        if 'cur' in database:
            zone = 'CUR'
        if 'ref' in database:
            zone = 'REF'
        if 'con' in database:
            zone = 'CON'
        grouped_tables_by_zone.setdefault(zone, [])
        if 'ber' in database or 'bsf' in database or 'bsj' in database or 'bsc' in database:
            hive_cursor_raw.execute('USE %s' % database)
            hive_cursor_raw.execute('SHOW TABLES')
            tables_in_database = list(map(lambda x: x[0], hive_cursor_raw.fetchall()))
            databases_dict[database] = tables_in_database
            grouped_tables_by_zone[zone] = grouped_tables_by_zone[zone]+list(map(lambda x: database+'.'+x, tables_in_database))
            #print('Tables in database %s: %s' % (database, tables))

def find_create_table_info(table_name):
    hive_conn_raw = hive.connect(host=hive_host, port=hive_port, username=hive_user, database=hive_database_raw)
    # Create a Hive cursor
    hive_cursor_raw = hive_conn_raw.cursor()
    # List all databases in Hive
    hive_cursor_raw.execute('DESCRIBE %s' % table_name)
    create_table = hive_cursor_raw.fetchall()
    none_tuple = ('', None, None)
    #find none_tuple index in create_table
    none_tuple_index = create_table.index(none_tuple)
    create_table = create_table[0: none_tuple_index]
    hive_cursor_raw.close()
    hive_conn_raw.close()
    return create_table

print(find_create_table_info('de_ber_1raw.sfb_aamve'))




[('glb_dtime', 'string', 'Clave identifica el registro como unico'), ('aco_conce', 'string', 'Codigo de concepto'), ('aco_usuar', 'string', 'Usuario de Cuento'), ('acu_ofici', 'string', 'Codigo de sucursal'), ('acunumcue', 'string', 'Numero de Cuenta'), ('acoptovta', 'string', 'Codigo de puesto de venta'), ('acudigver', 'string', 'Digito de Cuenta'), ('estado', 'string', 'Estado'), ('fecha_proceso', 'varchar(8)', '')]


In [84]:
print(json.dumps(grouped_tables_by_zone, indent=2))

{
  "RAW": [
    "de_ber_1raw.acreditaciones_haberes",
    "de_ber_1raw.adelanto_haberes",
    "de_ber_1raw.anses_rud_beneficios",
    "de_ber_1raw.archivo_segmentacion_bersa_1",
    "de_ber_1raw.archivo_segmentacion_bersa_2",
    "de_ber_1raw.archivo_segmentacion_bersa_3",
    "de_ber_1raw.archivo_segmentacion_bersa_4",
    "de_ber_1raw.ber_paq",
    "de_ber_1raw.calificador_limites",
    "de_ber_1raw.calificador_limites_deploy",
    "de_ber_1raw.campania_mail_extrajudicial",
    "de_ber_1raw.cant_atm_x_entidad",
    "de_ber_1raw.captura_trx",
    "de_ber_1raw.captura_trx_test2",
    "de_ber_1raw.captura_trx_test3",
    "de_ber_1raw.captura_trx_test4",
    "de_ber_1raw.captura_trx_test5",
    "de_ber_1raw.captura_trx_test6",
    "de_ber_1raw.cierre_mensual_visa_mc",
    "de_ber_1raw.cierres_tc_cart1_test",
    "de_ber_1raw.cimfdbk_contratacionproducto",
    "de_ber_1raw.cimfdbk_engage",
    "de_ber_1raw.cimfdbk_icommkt",
    "de_ber_1raw.cimfdbk_linkcli",
    "de_ber_1raw.cimfdbk_noti

In [85]:
json_consumo = {
  "CON": [
    "de_ber_4con.abt_persona_perfil_crediticio_clientes",
    "de_ber_4con.beneficios_tienda_clic_ft_compra",
    "de_ber_4con.bsmot_tarjetas_debito",
    "de_ber_4con.can_gen_empleadores_sector_publico",
    "de_ber_4con.can_ges_caja_presencial_dim",
    "de_ber_4con.can_ges_campania_ft_respuesta",
    "de_ber_4con.can_ges_campanias_dim_engage_lista",
    "de_ber_4con.can_ges_campanias_ft_codlista",
    "de_ber_4con.can_ges_campanias_ft_micrositio_4u",
    "de_ber_4con.can_ges_campanias_ft_micrositio_empresa",
    "de_ber_4con.can_ges_campanias_ft_micrositio_misolucion",
    "de_ber_4con.can_ges_campanias_ft_micrositio_tcma",
    "de_ber_4con.can_ges_campanias_ft_respuesta_contratacion_producto",
    "de_ber_4con.can_ges_campanias_ft_respuesta_icommkt",
    "de_ber_4con.can_ges_campanias_ft_respuesta_notificacion_oferta",
    "de_ber_4con.can_ges_contact_center_ft",
    "de_ber_4con.can_ges_hb_empresas_dim_rol",
    "de_ber_4con.can_ges_hb_empresas_parametria_actividades",
    "de_ber_4con.can_ges_hb_ft_auditoria_errores",
    "de_ber_4con.can_ges_hb_ft_login",
    "de_ber_4con.can_ges_hb_ft_transacciones",
    "de_ber_4con.can_ges_hb_parametria_actividades",
    "de_ber_4con.can_ges_homebanking_dim_abt_empresas",
    "de_ber_4con.can_ges_homebanking_ft_auditoria_prueba",
    "de_ber_4con.can_ges_homebanking_ft_transacciones",
    "de_ber_4con.can_ges_parametria_dim_oficiales",
    "de_ber_4con.can_ges_parametria_dim_sucursal_cg",
    "de_ber_4con.can_ges_parametria_dim_sucursal_meta4",
    "de_ber_4con.can_ges_parametria_dim_sucursales",
    "de_ber_4con.can_ges_parametria_ft_metas_grupales",
    "de_ber_4con.can_ges_parametria_ft_metas_individuales",
    "de_ber_4con.can_ges_parametria_ft_uptime_atm",
    "de_ber_4con.can_ges_parametria_rel_carterizacion",
    "de_ber_4con.can_ges_turnero_ft_turnos_engage",
    "de_ber_4con.can_ges_workflow_ft_mesa_entrada",
    "de_ber_4con.can_ges_workflow_rel_soli_relacion_persona",
    "de_ber_4con.clientes_afip_dim",
    "de_ber_4con.clientes_contactabilidad_direccion_dim",
    "de_ber_4con.clientes_contactabilidad_mail_dim",
    "de_ber_4con.clientes_contactabilidad_telefono_dim",
    "de_ber_4con.clientes_datos_adicionales_dim_abt_empresas",
    "de_ber_4con.clientes_datos_identificatorios_dim",
    "de_ber_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "de_ber_4con.clientes_datos_identificatorios_dim_datagp",
    "de_ber_4con.clientes_datos_identificatorios_dim_temp",
    "de_ber_4con.clientes_datos_identificatorios_rel_documentos",
    "de_ber_4con.clientes_datos_impositivos_dim",
    "de_ber_4con.clientes_datos_impositivos_dim_abt_empresas",
    "de_ber_4con.clientes_documentos_dim",
    "de_ber_4con.clientes_legajo_digital_dim_abt_empresas",
    "de_ber_4con.clientes_perfil_comercial_datos_persona",
    "de_ber_4con.clientes_perfil_comercial_dim",
    "de_ber_4con.clientes_perfil_comercial_dim_abt_empresas",
    "de_ber_4con.clientes_perfil_comercial_dim_manual_carterizacion_oficiales",
    "de_ber_4con.clientes_perfil_comercial_dim_manual_segmento_instituciones",
    "de_ber_4con.clientes_productos_dim_activos",
    "de_ber_4con.contabilidad_balance_dim_abt_empresas",
    "de_ber_4con.contabilidad_mov_contables_dim_abt_empresas",
    "de_ber_4con.de_ber_datamart_control_gestion",
    "de_ber_4con.dt_productos_prestamos_dim_cuotas_procesadas",
    "de_ber_4con.exp_cliente_nps_ft_encuesta",
    "de_ber_4con.finanzas_cot_indices_ft_cotizaciones",
    "de_ber_4con.ft_precalificados",
    "de_ber_4con.inventario_acuerdos_cobros",
    "de_ber_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "de_ber_4con.legales_denuncias_dim_abt_empresas",
    "de_ber_4con.legales_mora_judicial_dim_abt_empresas",
    "de_ber_4con.legales_mora_judicial_ft_mail",
    "de_ber_4con.legales_mora_judicial_ft_sms",
    "de_ber_4con.parametria_datos_generales_demograficos",
    "de_ber_4con.parametria_datos_generales_provincias_dim",
    "de_ber_4con.productos_ca_dim",
    "de_ber_4con.productos_ca_dim_tasas_interes",
    "de_ber_4con.productos_ca_ft",
    "de_ber_4con.productos_ca_ft_prueba",
    "de_ber_4con.productos_caja_ahorro_dim_maestro",
    "de_ber_4con.productos_caja_ahorro_dim_maestro_bis",
    "de_ber_4con.productos_caja_ahorro_movimientos_dim",
    "de_ber_4con.productos_caja_de_ahorro_dim_embargos",
    "de_ber_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "de_ber_4con.productos_caja_de_ahorro_transaccion_permitida",
    "de_ber_4con.productos_cajas_seguridad_alta_contratos",
    "de_ber_4con.productos_cajas_seguridad_dim_cotitulares",
    "de_ber_4con.productos_cajas_seguridad_dim_param_estados",
    "de_ber_4con.productos_cajas_seguridad_dim_provincia",
    "de_ber_4con.productos_cajas_seguridad_dim_sucursal",
    "de_ber_4con.productos_cajas_seguridad_dim_tamanio_cajas",
    "de_ber_4con.productos_cajas_seguridad_ft_bajas_alquileres",
    "de_ber_4con.productos_cajas_seguridad_ft_contrato",
    "de_ber_4con.productos_cajas_seguridad_ft_cta_cte",
    "de_ber_4con.productos_cajas_seguridad_ft_estados",
    "de_ber_4con.productos_cajas_seguridad_ft_personas_autorizadas",
    "de_ber_4con.productos_can_ges_parametria_tasas_pasivas",
    "de_ber_4con.productos_cantidad_activos",
    "de_ber_4con.productos_cc_dim",
    "de_ber_4con.productos_cc_ft_movimiento",
    "de_ber_4con.productos_cc_ft_saldo",
    "de_ber_4con.productos_cheques_dim_convenio_cliente",
    "de_ber_4con.productos_cheques_dim_convenios",
    "de_ber_4con.productos_cheques_dim_convenios_depositos",
    "de_ber_4con.productos_cheques_dim_datos_identificatorios_clientes",
    "de_ber_4con.productos_cheques_dim_depositos",
    "de_ber_4con.productos_cheques_dim_echeq_librados",
    "de_ber_4con.productos_cheques_dim_empresas",
    "de_ber_4con.productos_cheques_dim_maestro_bancos",
    "de_ber_4con.productos_cheques_dim_maestro_codigos_postales",
    "de_ber_4con.productos_cheques_dim_maestro_plazas",
    "de_ber_4con.productos_cheques_dim_negociados",
    "de_ber_4con.productos_cheques_dim_usuarios",
    "de_ber_4con.productos_cliente_dim_cuenta",
    "de_ber_4con.productos_contabilidad_dim_comisiones",
    "de_ber_4con.productos_contabilidad_dim_maestro_causales",
    "de_ber_4con.productos_contabilidad_dim_maestro_equivalencias_contables",
    "de_ber_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "de_ber_4con.productos_contabilidad_dim_maestro_tareas_cierre",
    "de_ber_4con.productos_contabilidad_dim_minuta",
    "de_ber_4con.productos_contabilidad_dim_renglon_minuta",
    "de_ber_4con.productos_cta_corriente_dim_embargos",
    "de_ber_4con.productos_cta_corriente_dim_maestro",
    "de_ber_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "de_ber_4con.productos_cta_corriente_ft_maestro_historico",
    "de_ber_4con.productos_cta_corriente_movimientos_dim",
    "de_ber_4con.productos_cta_corriente_param_dim_relacion_titularidad",
    "de_ber_4con.productos_dep_val_cheques_ft_empresa",
    "de_ber_4con.productos_dim_maestro_chequeras",
    "de_ber_4con.productos_dim_maestro_valores_cesion",
    "de_ber_4con.productos_dim_maestro_valores_sesion",
    "de_ber_4con.productos_garantias_dim_maestro",
    "de_ber_4con.productos_garantias_rel_operaciones",
    "de_ber_4con.productos_haberes_cargas_masivas_ft",
    "de_ber_4con.productos_haberes_dim_abt_empresas",
    "de_ber_4con.productos_haberes_dim_convenios",
    "de_ber_4con.productos_haberes_dim_cuenta_sueldo",
    "de_ber_4con.productos_haberes_empresas_clientes_ft",
    "de_ber_4con.productos_haberes_empresas_dim",
    "de_ber_4con.productos_haberes_ft_adelanto",
    "de_ber_4con.productos_haberes_ft_convenios",
    "de_ber_4con.productos_haberes_ft_convenioslkp",
    "de_ber_4con.productos_lineas_especiales_dim",
    "de_ber_4con.productos_maestro_causales",
    "de_ber_4con.productos_monedaextranjera_ft_compraventa",
    "de_ber_4con.productos_paquetes_dim",
    "de_ber_4con.productos_paquetes_dim_abt_empresas",
    "de_ber_4con.productos_paquetes_ft_movimientos_pagos",
    "de_ber_4con.productos_paquetes_rel_paq_cc_ca",
    "de_ber_4con.productos_paquetes_rel_paquete_cuenta",
    "de_ber_4con.productos_paquetes_rel_vinculacion_cuentas",
    "de_ber_4con.productos_parametria_dim_acordante",
    "de_ber_4con.productos_parametria_dim_atrib_cont_bcra",
    "de_ber_4con.productos_parametria_dim_codigos_tasa",
    "de_ber_4con.productos_parametria_dim_condicion_iva",
    "de_ber_4con.productos_parametria_dim_destino_econom",
    "de_ber_4con.productos_parametria_dim_divisas",
    "de_ber_4con.productos_parametria_dim_estado_cuenta",
    "de_ber_4con.productos_parametria_dim_estado_ppmap",
    "de_ber_4con.productos_parametria_dim_general_bancos",
    "de_ber_4con.productos_parametria_dim_lim",
    "de_ber_4con.productos_parametria_dim_manual",
    "de_ber_4con.productos_parametria_dim_moneda",
    "de_ber_4con.productos_parametria_dim_moneda_refactor",
    "de_ber_4con.productos_parametria_dim_motivos_cierres",
    "de_ber_4con.productos_parametria_dim_nivel",
    "de_ber_4con.productos_parametria_dim_operativa_contable",
    "de_ber_4con.productos_parametria_dim_origen_fondos",
    "de_ber_4con.productos_parametria_dim_paquetes",
    "de_ber_4con.productos_parametria_dim_periodocpa",
    "de_ber_4con.productos_parametria_dim_plazo_fijo",
    "de_ber_4con.productos_parametria_dim_productos",
    "de_ber_4con.productos_parametria_dim_punto_vta",
    "de_ber_4con.productos_parametria_dim_rechazo",
    "de_ber_4con.productos_parametria_dim_relacion_cliente_cuenta",
    "de_ber_4con.productos_parametria_dim_relacion_portafolio_cuentas",
    "de_ber_4con.productos_parametria_dim_relacion_titularidad",
    "de_ber_4con.productos_parametria_dim_relacion_titularidad_refactor",
    "de_ber_4con.productos_parametria_dim_sector_residencia",
    "de_ber_4con.productos_parametria_dim_sist_amort",
    "de_ber_4con.productos_parametria_dim_sublim",
    "de_ber_4con.productos_parametria_dim_sucursales_provincia",
    "de_ber_4con.productos_parametria_dim_tipo_boleta",
    "de_ber_4con.productos_parametria_dim_tipo_embargos",
    "de_ber_4con.productos_parametria_dim_tipo_empresa",
    "de_ber_4con.productos_parametria_dim_tipo_servicio",
    "de_ber_4con.productos_parametria_dim_tipo_tasa",
    "de_ber_4con.productos_parametria_dim_toma_disp_fondo",
    "de_ber_4con.productos_parametria_dim_zonas",
    "de_ber_4con.productos_parametria_ft_calendario_saldo",
    "de_ber_4con.productos_parametria_tarjeta_debito",
    "de_ber_4con.productos_parametrias_dim_concepto",
    "de_ber_4con.productos_pf_dim_abt_empresas",
    "de_ber_4con.productos_pf_ft",
    "de_ber_4con.productos_pf_ft_certificados",
    "de_ber_4con.productos_pf_maestro_cuentas_inversoras",
    "de_ber_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "de_ber_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras_refactor",
    "de_ber_4con.productos_plazo_fijo_ft_certificados",
    "de_ber_4con.productos_plazo_fijos_dim_parametros",
    "de_ber_4con.productos_prestamo_transacciones",
    "de_ber_4con.productos_prestamos_dim_abt_empresas",
    "de_ber_4con.productos_prestamos_dim_cuotas_generadas",
    "de_ber_4con.productos_prestamos_dim_maestro",
    "de_ber_4con.productos_prestamos_dim_maestro_cuotas",
    "de_ber_4con.productos_prestamos_dim_maestro_vendedores",
    "de_ber_4con.productos_prestamos_ft",
    "de_ber_4con.productos_prestamos_ft_gastos_cuotas",
    "de_ber_4con.productos_prestamos_ft_movimientos_historico",
    "de_ber_4con.productos_prestamos_ft_residuales_csv",
    "de_ber_4con.productos_prestamos_ft_residuales_nueva",
    "de_ber_4con.productos_prestamos_ft_residuales_nueva2",
    "de_ber_4con.productos_prestamos_rel_carpeta_cliente",
    "de_ber_4con.productos_prestamos_rel_prefinanciados_productos",
    "de_ber_4con.productos_recaudaciones_dim_detalle_comisiones",
    "de_ber_4con.productos_recaudaciones_dim_entes",
    "de_ber_4con.productos_recaudaciones_dim_formula_comision",
    "de_ber_4con.productos_recaudaciones_dim_link_detalle_comisiones_hist",
    "de_ber_4con.productos_recaudaciones_dim_linkentes",
    "de_ber_4con.productos_recaudaciones_dim_maestro_entes",
    "de_ber_4con.productos_recaudaciones_dim_tasas_interes",
    "de_ber_4con.productos_recaudaciones_ft_maestro",
    "de_ber_4con.productos_request_tracking",
    "de_ber_4con.productos_seguros_dim_maestro",
    "de_ber_4con.productos_seguros_dim_qualia",
    "de_ber_4con.productos_seguros_ft",
    "de_ber_4con.productos_seguros_ft_solicitud_baja",
    "de_ber_4con.productos_tarjetas_debito_dim_maestro",
    "de_ber_4con.productos_tarjetas_debito_ft_cierres",
    "de_ber_4con.productos_tarjetas_debito_movimientos",
    "de_ber_4con.productos_tarjetas_promocion_individuos",
    "de_ber_4con.productos_ttcc_dim_abt_empresas",
    "de_ber_4con.productos_ttcc_dim_maestro",
    "de_ber_4con.productos_ttcc_dim_plasticos",
    "de_ber_4con.productos_ttcc_ft_mov_cred",
    "de_ber_4con.productos_ttcc_ft_mov_prisma",
    "de_ber_4con.productos_ttdd_dim",
    "de_ber_4con.productos_ttdd_dim_maestro",
    "de_ber_4con.productos_vendedores_dim_maestro",
    "de_ber_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "de_ber_4con.riesgos_adm_crediticia_balance",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_afip",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "de_ber_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_ber_4con.riesgos_adm_crediticia_datos_adicionales",
    "de_ber_4con.riesgos_adm_crediticia_datos_impositivos",
    "de_ber_4con.riesgos_adm_crediticia_datos_personales",
    "de_ber_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "de_ber_4con.riesgos_adm_crediticia_dim_lim",
    "de_ber_4con.riesgos_adm_crediticia_dim_no_clientes",
    "de_ber_4con.riesgos_adm_crediticia_dim_plafond",
    "de_ber_4con.riesgos_adm_crediticia_dim_sublim",
    "de_ber_4con.riesgos_adm_crediticia_dim_workflow",
    "de_ber_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_ber_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_ber_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "de_ber_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_ber_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_ber_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_ber_4con.riesgos_adm_crediticia_eva_score",
    "de_ber_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "de_ber_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_ber_4con.riesgos_adm_crediticia_eva_script",
    "de_ber_4con.riesgos_adm_crediticia_ft_calificador_lim",
    "de_ber_4con.riesgos_adm_crediticia_ft_link",
    "de_ber_4con.riesgos_adm_crediticia_ft_sin_haberes",
    "de_ber_4con.riesgos_adm_crediticia_home_banking",
    "de_ber_4con.riesgos_adm_crediticia_limites_y_garantias",
    "de_ber_4con.riesgos_adm_crediticia_mora",
    "de_ber_4con.riesgos_adm_crediticia_of_calculosfinales",
    "de_ber_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "de_ber_4con.riesgos_adm_crediticia_of_decisionfinal",
    "de_ber_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "de_ber_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_ber_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "de_ber_4con.riesgos_adm_crediticia_of_niveldefirma",
    "de_ber_4con.riesgos_adm_crediticia_of_postburo",
    "de_ber_4con.riesgos_adm_crediticia_of_reclasificacion",
    "de_ber_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "de_ber_4con.riesgos_adm_crediticia_of_score",
    "de_ber_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "de_ber_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_ber_4con.riesgos_adm_crediticia_of_topedecliente",
    "de_ber_4con.riesgos_adm_crediticia_of_tramites",
    "de_ber_4con.riesgos_adm_crediticia_of_verificaciones",
    "de_ber_4con.riesgos_adm_crediticia_of_vigencias",
    "de_ber_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "de_ber_4con.riesgos_adm_crediticia_perfil_tecnico",
    "de_ber_4con.riesgos_adm_crediticia_prestamos",
    "de_ber_4con.riesgos_adm_crediticia_sucursales",
    "de_ber_4con.riesgos_adm_crediticia_tarjetas",
    "de_ber_4con.riesgos_calificacion_prestamos_tarjetas",
    "de_ber_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_ber_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "de_ber_4con.riesgos_recupero_dim_cartera_diaria_morosa",
    "de_ber_4con.riesgos_recupero_ft_gestiones",
    "de_ber_4con.rrhh_perfil_colaborador_dim_empleado",
    "de_ber_4con.tabla_temporal_con",
    "de_ber_4con.test_ranger",
    "de_ber_4con.vn_productos_parametria_dim_relacion_titularidad",
    "de_ber_4con.vw_caja_ahorro_cuentas_contables",
    "de_ber_4con.vw_caja_ahorro_cuentas_contables_comisiones",
    "de_ber_4con.vw_caja_ahorro_datos_basicos",
    "de_ber_4con.vw_caja_ahorro_embargos",
    "de_ber_4con.vw_caja_ahorro_movimientos",
    "de_ber_4con.vw_caja_ahorro_saldos",
    "de_ber_4con.vw_caja_ahorro_tarjetas_debito",
    "de_ber_4con.vw_caja_ahorro_titularidad_relacion",
    "de_ber_4con.vw_caja_ahorro_transacciones",
    "de_ber_4con.vw_caja_ahorro_transacciones_habilitadas",
    "de_ber_4con.vw_cheques_chequeras",
    "de_ber_4con.vw_cheques_convenios",
    "de_ber_4con.vw_clientes_rel_vn",
    "de_ber_4con.vw_cuenta_corriente_acuerdos",
    "de_ber_4con.vw_cuenta_corriente_cuenta_portafolio",
    "de_ber_4con.vw_cuenta_corriente_datos_basicos",
    "de_ber_4con.vw_cuenta_corriente_embargos",
    "de_ber_4con.vw_cuenta_corriente_garantias",
    "de_ber_4con.vw_cuenta_corriente_maestro_historico",
    "de_ber_4con.vw_cuenta_corriente_titularidad_relacion",
    "de_ber_4con.vw_maestro_vn",
    "de_ber_4con.vw_prestamos_cobranzas_movimientos",
    "de_ber_4con.vw_prod_vn_cheques",
    "de_ber_4con.vw_productos_paquetes_datos_basicos",
    "de_ber_4con.vw_productos_parametria_dim_relacion_titularidad",
    "de_ber_4con.vw_productos_pf_dim_maestro_cuentas_inversoras",
    "de_ber_4con.vw_productos_plazo_fijo_ft_certificados",
    "de_ber_4con.vw_productos_prestamos_dim_maestro",
    "de_ber_4con.vw_riesgos_adm_crediticia_dim_lim",
    "de_ber_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "de_ber_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "de_bsc_4con.adobe_productos_ttcc_ft_mov_cred",
    "de_bsc_4con.beneficios_tienda_clic_ft_compra",
    "de_bsc_4con.can_gen_empleadores_sector_publico",
    "de_bsc_4con.can_ges_caja_presencial_dim",
    "de_bsc_4con.can_ges_campania_ft_respuesta",
    "de_bsc_4con.can_ges_campanias_dim_engage_lista",
    "de_bsc_4con.can_ges_campanias_ft_codlista",
    "de_bsc_4con.can_ges_campanias_ft_micrositio_4u",
    "de_bsc_4con.can_ges_campanias_ft_micrositio_empresa",
    "de_bsc_4con.can_ges_campanias_ft_micrositio_misolucion",
    "de_bsc_4con.can_ges_campanias_ft_micrositio_tcma",
    "de_bsc_4con.can_ges_campanias_ft_respuesta_contratacion_producto",
    "de_bsc_4con.can_ges_campanias_ft_respuesta_icommkt",
    "de_bsc_4con.can_ges_campanias_ft_respuesta_notificacion_oferta",
    "de_bsc_4con.can_ges_contact_center_ft",
    "de_bsc_4con.can_ges_hb_ft_auditoria_errores",
    "de_bsc_4con.can_ges_hb_ft_login",
    "de_bsc_4con.can_ges_hb_ft_transacciones",
    "de_bsc_4con.can_ges_hb_parametria_actividades",
    "de_bsc_4con.can_ges_homebanking_dim_abt_empresas",
    "de_bsc_4con.can_ges_parametria_dim_oficiales",
    "de_bsc_4con.can_ges_parametria_dim_sucursal_cg",
    "de_bsc_4con.can_ges_parametria_dim_sucursal_meta4",
    "de_bsc_4con.can_ges_parametria_dim_sucursales",
    "de_bsc_4con.can_ges_parametria_ft_metas_grupales",
    "de_bsc_4con.can_ges_parametria_ft_metas_individuales",
    "de_bsc_4con.can_ges_parametria_ft_uptime_atm",
    "de_bsc_4con.can_ges_parametria_rel_carterizacion",
    "de_bsc_4con.can_ges_turnero_ft_turnos_engage",
    "de_bsc_4con.can_ges_workflow_ft_mesa_entrada",
    "de_bsc_4con.can_ges_workflow_rel_soli_relacion_persona",
    "de_bsc_4con.clientes_afip_dim",
    "de_bsc_4con.clientes_contactabilidad_direccion_dim",
    "de_bsc_4con.clientes_contactabilidad_mail_dim",
    "de_bsc_4con.clientes_contactabilidad_telefono_dim",
    "de_bsc_4con.clientes_datos_adicionales_dim_abt_empresas",
    "de_bsc_4con.clientes_datos_identificatorios_dim",
    "de_bsc_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "de_bsc_4con.clientes_datos_identificatorios_dim_datagp",
    "de_bsc_4con.clientes_datos_identificatorios_dim_temp",
    "de_bsc_4con.clientes_datos_identificatorios_rel_documentos",
    "de_bsc_4con.clientes_datos_impositivos_dim",
    "de_bsc_4con.clientes_datos_impositivos_dim_abt_empresas",
    "de_bsc_4con.clientes_documentos_dim",
    "de_bsc_4con.clientes_legajo_digital_dim_abt_empresas",
    "de_bsc_4con.clientes_perfil_comercial_dim",
    "de_bsc_4con.clientes_perfil_comercial_dim_abt_empresas",
    "de_bsc_4con.clientes_perfil_comercial_dim_manual_carterizacion_oficiales",
    "de_bsc_4con.clientes_perfil_comercial_dim_manual_segmento_instituciones",
    "de_bsc_4con.clientes_productos_dim_activos",
    "de_bsc_4con.contabilidad_balance_dim_abt_empresas",
    "de_bsc_4con.contabilidad_mov_contables_dim_abt_empresas",
    "de_bsc_4con.dt_productos_prestamos_dim_cuotas_procesadas",
    "de_bsc_4con.exp_cliente_nps_ft_encuesta",
    "de_bsc_4con.finanzas_cot_indices_ft_cotizaciones",
    "de_bsc_4con.ft_precalificados",
    "de_bsc_4con.inventario_acuerdos_cobros",
    "de_bsc_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "de_bsc_4con.legales_denuncias_dim_abt_empresas",
    "de_bsc_4con.legales_mora_judicial_dim_abt_empresas",
    "de_bsc_4con.legales_mora_judicial_ft_mail",
    "de_bsc_4con.legales_mora_judicial_ft_sms",
    "de_bsc_4con.parametria_datos_generales_demograficos",
    "de_bsc_4con.parametria_datos_generales_provincias_dim",
    "de_bsc_4con.productos_ca_dim",
    "de_bsc_4con.productos_ca_dim_tasas_interes",
    "de_bsc_4con.productos_ca_ft",
    "de_bsc_4con.productos_ca_ft_prueba",
    "de_bsc_4con.productos_caja_ahorro_dim_maestro",
    "de_bsc_4con.productos_caja_ahorro_movimientos_dim",
    "de_bsc_4con.productos_caja_de_ahorro_dim_embargos",
    "de_bsc_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "de_bsc_4con.productos_caja_de_ahorro_transaccion_permitida",
    "de_bsc_4con.productos_cajas_seguridad_alta_contratos",
    "de_bsc_4con.productos_cajas_seguridad_dim_cotitulares",
    "de_bsc_4con.productos_cajas_seguridad_dim_param_estados",
    "de_bsc_4con.productos_cajas_seguridad_dim_provincia",
    "de_bsc_4con.productos_cajas_seguridad_dim_sucursal",
    "de_bsc_4con.productos_cajas_seguridad_dim_tamanio_cajas",
    "de_bsc_4con.productos_cajas_seguridad_ft_bajas_alquileres",
    "de_bsc_4con.productos_cajas_seguridad_ft_cta_cte",
    "de_bsc_4con.productos_cajas_seguridad_ft_estados",
    "de_bsc_4con.productos_cajas_seguridad_ft_personas_autorizadas",
    "de_bsc_4con.productos_can_ges_parametria_tasas_pasivas",
    "de_bsc_4con.productos_cantidad_activos",
    "de_bsc_4con.productos_cc_dim",
    "de_bsc_4con.productos_cc_ft_movimiento",
    "de_bsc_4con.productos_cc_ft_saldo",
    "de_bsc_4con.productos_cheques_dim_convenio_cliente",
    "de_bsc_4con.productos_cheques_dim_convenios",
    "de_bsc_4con.productos_cheques_dim_convenios_depositos",
    "de_bsc_4con.productos_cheques_dim_datos_identificatorios_clientes",
    "de_bsc_4con.productos_cheques_dim_depositos",
    "de_bsc_4con.productos_cheques_dim_echeq_librados",
    "de_bsc_4con.productos_cheques_dim_empresas",
    "de_bsc_4con.productos_cheques_dim_maestro_bancos",
    "de_bsc_4con.productos_cheques_dim_maestro_codigos_postales",
    "de_bsc_4con.productos_cheques_dim_maestro_plazas",
    "de_bsc_4con.productos_cheques_dim_negociados",
    "de_bsc_4con.productos_cheques_dim_usuarios",
    "de_bsc_4con.productos_cliente_dim_cuenta",
    "de_bsc_4con.productos_contabilidad_dim_comisiones",
    "de_bsc_4con.productos_contabilidad_dim_maestro_causales",
    "de_bsc_4con.productos_contabilidad_dim_maestro_equivalencias_contables",
    "de_bsc_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "de_bsc_4con.productos_contabilidad_dim_maestro_tareas_cierre",
    "de_bsc_4con.productos_contabilidad_dim_minuta",
    "de_bsc_4con.productos_contabilidad_dim_renglon_minuta",
    "de_bsc_4con.productos_cta_corriente_dim_embargos",
    "de_bsc_4con.productos_cta_corriente_dim_maestro",
    "de_bsc_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "de_bsc_4con.productos_cta_corriente_ft_maestro_historico",
    "de_bsc_4con.productos_cta_corriente_movimientos_dim",
    "de_bsc_4con.productos_cta_corriente_param_dim_relacion_titularidad",
    "de_bsc_4con.productos_dep_val_cheques_ft_empresa",
    "de_bsc_4con.productos_dim_maestro_chequeras",
    "de_bsc_4con.productos_dim_maestro_valores_cesion",
    "de_bsc_4con.productos_dim_maestro_valores_sesion",
    "de_bsc_4con.productos_garantias_dim_maestro",
    "de_bsc_4con.productos_garantias_rel_operaciones",
    "de_bsc_4con.productos_haberes_cargas_masivas_ft",
    "de_bsc_4con.productos_haberes_dim_abt_empresas",
    "de_bsc_4con.productos_haberes_dim_convenios",
    "de_bsc_4con.productos_haberes_dim_cuenta_sueldo",
    "de_bsc_4con.productos_haberes_empresas_clientes_ft",
    "de_bsc_4con.productos_haberes_empresas_dim",
    "de_bsc_4con.productos_haberes_ft_adelanto",
    "de_bsc_4con.productos_haberes_ft_convenios",
    "de_bsc_4con.productos_haberes_ft_convenioslkp",
    "de_bsc_4con.productos_lineas_especiales_dim",
    "de_bsc_4con.productos_maestro_causales",
    "de_bsc_4con.productos_monedaextranjera_ft_compraventa",
    "de_bsc_4con.productos_paquetes_dim",
    "de_bsc_4con.productos_paquetes_dim_abt_empresas",
    "de_bsc_4con.productos_paquetes_dim_empleados",
    "de_bsc_4con.productos_paquetes_dim_estado_solicitud",
    "de_bsc_4con.productos_paquetes_ft_movimientos_pagos",
    "de_bsc_4con.productos_paquetes_ft_solicitud",
    "de_bsc_4con.productos_paquetes_ft_solicitud_ca",
    "de_bsc_4con.productos_paquetes_ft_solicitud_cliente",
    "de_bsc_4con.productos_paquetes_ft_solicitud_historico",
    "de_bsc_4con.productos_paquetes_ft_solicitud_paquete",
    "de_bsc_4con.productos_paquetes_rel_paq_cc_ca",
    "de_bsc_4con.productos_paquetes_rel_vinculacion_cuentas",
    "de_bsc_4con.productos_parametria_dim_acordante",
    "de_bsc_4con.productos_parametria_dim_atrib_cont_bcra",
    "de_bsc_4con.productos_parametria_dim_codigos_tasa",
    "de_bsc_4con.productos_parametria_dim_condicion_iva",
    "de_bsc_4con.productos_parametria_dim_destino_econom",
    "de_bsc_4con.productos_parametria_dim_divisas",
    "de_bsc_4con.productos_parametria_dim_estado_cuenta",
    "de_bsc_4con.productos_parametria_dim_estado_ppmap",
    "de_bsc_4con.productos_parametria_dim_general_bancos",
    "de_bsc_4con.productos_parametria_dim_lim",
    "de_bsc_4con.productos_parametria_dim_manual",
    "de_bsc_4con.productos_parametria_dim_moneda",
    "de_bsc_4con.productos_parametria_dim_moneda_refactor",
    "de_bsc_4con.productos_parametria_dim_motivos_cierres",
    "de_bsc_4con.productos_parametria_dim_nivel",
    "de_bsc_4con.productos_parametria_dim_operativa_contable",
    "de_bsc_4con.productos_parametria_dim_origen_fondos",
    "de_bsc_4con.productos_parametria_dim_paquetes",
    "de_bsc_4con.productos_parametria_dim_periodocpa",
    "de_bsc_4con.productos_parametria_dim_plazo_fijo",
    "de_bsc_4con.productos_parametria_dim_productos",
    "de_bsc_4con.productos_parametria_dim_punto_vta",
    "de_bsc_4con.productos_parametria_dim_rechazo",
    "de_bsc_4con.productos_parametria_dim_relacion_cliente_cuenta",
    "de_bsc_4con.productos_parametria_dim_relacion_portafolio_cuentas",
    "de_bsc_4con.productos_parametria_dim_relacion_titularidad",
    "de_bsc_4con.productos_parametria_dim_relacion_titularidad_refactor",
    "de_bsc_4con.productos_parametria_dim_sector_residencia",
    "de_bsc_4con.productos_parametria_dim_sist_amort",
    "de_bsc_4con.productos_parametria_dim_sublim",
    "de_bsc_4con.productos_parametria_dim_sucursales_provincia",
    "de_bsc_4con.productos_parametria_dim_tipo_boleta",
    "de_bsc_4con.productos_parametria_dim_tipo_embargos",
    "de_bsc_4con.productos_parametria_dim_tipo_empresa",
    "de_bsc_4con.productos_parametria_dim_tipo_paquete",
    "de_bsc_4con.productos_parametria_dim_tipo_servicio",
    "de_bsc_4con.productos_parametria_dim_tipo_tasa",
    "de_bsc_4con.productos_parametria_dim_toma_disp_fondo",
    "de_bsc_4con.productos_parametria_dim_zonas",
    "de_bsc_4con.productos_parametria_ft_calendario_saldo",
    "de_bsc_4con.productos_parametria_tarjeta_debito",
    "de_bsc_4con.productos_parametrias_dim_concepto",
    "de_bsc_4con.productos_pf_dim_abt_empresas",
    "de_bsc_4con.productos_pf_ft",
    "de_bsc_4con.productos_pf_ft_certificados",
    "de_bsc_4con.productos_pf_maestro_cuentas_inversoras",
    "de_bsc_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "de_bsc_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras_refactor",
    "de_bsc_4con.productos_plazo_fijo_ft_certificados",
    "de_bsc_4con.productos_plazo_fijo_promedios_certificados",
    "de_bsc_4con.productos_plazo_fijos_dim_parametros",
    "de_bsc_4con.productos_prestamo_transacciones",
    "de_bsc_4con.productos_prestamos_dim_abt_empresas",
    "de_bsc_4con.productos_prestamos_dim_cuotas_generadas",
    "de_bsc_4con.productos_prestamos_dim_maestro",
    "de_bsc_4con.productos_prestamos_dim_maestro_cuotas",
    "de_bsc_4con.productos_prestamos_dim_maestro_vendedores",
    "de_bsc_4con.productos_prestamos_ft",
    "de_bsc_4con.productos_prestamos_ft_gastos_cuotas",
    "de_bsc_4con.productos_prestamos_ft_movimientos_historico",
    "de_bsc_4con.productos_prestamos_ft_residuales",
    "de_bsc_4con.productos_prestamos_ft_residuales_nueva",
    "de_bsc_4con.productos_prestamos_ft_residuales_nueva2",
    "de_bsc_4con.productos_prestamos_rel_carpeta_cliente",
    "de_bsc_4con.productos_prestamos_rel_prefinanciados_productos",
    "de_bsc_4con.productos_recaudaciones_dim_maestro_entes",
    "de_bsc_4con.productos_recaudaciones_dim_tasas_interes",
    "de_bsc_4con.productos_recaudaciones_ft_historico",
    "de_bsc_4con.productos_recaudaciones_ft_maestro",
    "de_bsc_4con.productos_request_tracking",
    "de_bsc_4con.productos_seguros_dim_maestro",
    "de_bsc_4con.productos_seguros_dim_qualia",
    "de_bsc_4con.productos_seguros_ft",
    "de_bsc_4con.productos_seguros_ft_solicitud_baja",
    "de_bsc_4con.productos_tarjetas_debito_dim_maestro",
    "de_bsc_4con.productos_tarjetas_debito_ft_cierres",
    "de_bsc_4con.productos_tarjetas_debito_movimientos",
    "de_bsc_4con.productos_tarjetas_promocion_individuos",
    "de_bsc_4con.productos_ttcc_dim_abt_empresas",
    "de_bsc_4con.productos_ttcc_dim_maestro",
    "de_bsc_4con.productos_ttcc_dim_plasticos",
    "de_bsc_4con.productos_ttcc_ft_mov_cred",
    "de_bsc_4con.productos_ttcc_ft_mov_prisma",
    "de_bsc_4con.productos_ttdd_dim",
    "de_bsc_4con.productos_ttdd_dim_maestro",
    "de_bsc_4con.productos_vendedores_dim_maestro",
    "de_bsc_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "de_bsc_4con.riesgos_adm_crediticia_balance",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_afip",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "de_bsc_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_bsc_4con.riesgos_adm_crediticia_datos_adicionales",
    "de_bsc_4con.riesgos_adm_crediticia_datos_impositivos",
    "de_bsc_4con.riesgos_adm_crediticia_datos_personales",
    "de_bsc_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "de_bsc_4con.riesgos_adm_crediticia_dim_lim",
    "de_bsc_4con.riesgos_adm_crediticia_dim_no_clientes",
    "de_bsc_4con.riesgos_adm_crediticia_dim_plafond",
    "de_bsc_4con.riesgos_adm_crediticia_dim_sublim",
    "de_bsc_4con.riesgos_adm_crediticia_dim_workflow",
    "de_bsc_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_bsc_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_bsc_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "de_bsc_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_bsc_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_bsc_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_bsc_4con.riesgos_adm_crediticia_eva_score",
    "de_bsc_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "de_bsc_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_bsc_4con.riesgos_adm_crediticia_eva_script",
    "de_bsc_4con.riesgos_adm_crediticia_ft_calificador_lim",
    "de_bsc_4con.riesgos_adm_crediticia_ft_individuos_mab",
    "de_bsc_4con.riesgos_adm_crediticia_ft_link",
    "de_bsc_4con.riesgos_adm_crediticia_ft_sin_haberes",
    "de_bsc_4con.riesgos_adm_crediticia_home_banking",
    "de_bsc_4con.riesgos_adm_crediticia_limites_y_garantias",
    "de_bsc_4con.riesgos_adm_crediticia_mora",
    "de_bsc_4con.riesgos_adm_crediticia_of_calculosfinales",
    "de_bsc_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "de_bsc_4con.riesgos_adm_crediticia_of_decisionfinal",
    "de_bsc_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "de_bsc_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_bsc_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "de_bsc_4con.riesgos_adm_crediticia_of_niveldefirma",
    "de_bsc_4con.riesgos_adm_crediticia_of_postburo",
    "de_bsc_4con.riesgos_adm_crediticia_of_reclasificacion",
    "de_bsc_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "de_bsc_4con.riesgos_adm_crediticia_of_score",
    "de_bsc_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "de_bsc_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_bsc_4con.riesgos_adm_crediticia_of_topedecliente",
    "de_bsc_4con.riesgos_adm_crediticia_of_tramites",
    "de_bsc_4con.riesgos_adm_crediticia_of_verificaciones",
    "de_bsc_4con.riesgos_adm_crediticia_of_vigencias",
    "de_bsc_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "de_bsc_4con.riesgos_adm_crediticia_perfil_tecnico",
    "de_bsc_4con.riesgos_adm_crediticia_prestamos",
    "de_bsc_4con.riesgos_adm_crediticia_sucursales",
    "de_bsc_4con.riesgos_adm_crediticia_tarjetas",
    "de_bsc_4con.riesgos_calificacion_prestamos_tarjetas",
    "de_bsc_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_bsc_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "de_bsc_4con.riesgos_recupero_dim_cartera_diaria_morosa",
    "de_bsc_4con.riesgos_recupero_ft_gestiones",
    "de_bsc_4con.rrhh_perfil_colaborador_dim_empleado",
    "de_bsc_4con.tabla_temporal_con",
    "de_bsc_4con.test_hdfs",
    "de_bsc_4con.test_hdfs_v123",
    "de_bsc_4con.test_hdfs_v2",
    "de_bsc_4con.test_hdfs_v3",
    "de_bsc_4con.test_hdfs_v4",
    "de_bsc_4con.vn_productos_parametria_dim_relacion_titularidad",
    "de_bsc_4con.vw_caja_ahorro_cuentas_contables",
    "de_bsc_4con.vw_caja_ahorro_cuentas_contables_comisiones",
    "de_bsc_4con.vw_caja_ahorro_datos_basicos",
    "de_bsc_4con.vw_caja_ahorro_embargos",
    "de_bsc_4con.vw_caja_ahorro_movimientos",
    "de_bsc_4con.vw_caja_ahorro_saldos",
    "de_bsc_4con.vw_caja_ahorro_tarjetas_debito",
    "de_bsc_4con.vw_caja_ahorro_titularidad_relacion",
    "de_bsc_4con.vw_caja_ahorro_transacciones_habilitadas",
    "de_bsc_4con.vw_cheques_chequeras",
    "de_bsc_4con.vw_cheques_convenios",
    "de_bsc_4con.vw_clientes_rel_vn",
    "de_bsc_4con.vw_clientes_rel_vn_bsc",
    "de_bsc_4con.vw_cuenta_corriente_acuerdos",
    "de_bsc_4con.vw_cuenta_corriente_cuenta_portafolio",
    "de_bsc_4con.vw_cuenta_corriente_datos_basicos",
    "de_bsc_4con.vw_cuenta_corriente_embargos",
    "de_bsc_4con.vw_cuenta_corriente_garantias",
    "de_bsc_4con.vw_cuenta_corriente_maestro_historico",
    "de_bsc_4con.vw_cuenta_corriente_titularidad_relacion",
    "de_bsc_4con.vw_maestro_vn",
    "de_bsc_4con.vw_prestamos_cobranzas_movimientos",
    "de_bsc_4con.vw_prod_vn_cheques",
    "de_bsc_4con.vw_productos_paquetes_datos_basicos",
    "de_bsc_4con.vw_productos_parametria_dim_relacion_titularidad",
    "de_bsc_4con.vw_productos_pf_dim_maestro_cuentas_inversoras",
    "de_bsc_4con.vw_productos_plazo_fijo_ft_certificados",
    "de_bsc_4con.vw_productos_prestamos_dim_maestro",
    "de_bsc_4con.vw_riesgos_adm_crediticia_dim_lim",
    "de_bsc_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "de_bsc_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "de_bsf_4con.beneficios_tienda_clic_ft_compra",
    "de_bsf_4con.can_gen_empleadores_sector_publico",
    "de_bsf_4con.can_ges_atm_ft_extract_link",
    "de_bsf_4con.can_ges_atm_ft_ingresos_pf",
    "de_bsf_4con.can_ges_caja_presencial_dim",
    "de_bsf_4con.can_ges_campania_ft_respuesta",
    "de_bsf_4con.can_ges_campanias_dim_engage_lista",
    "de_bsf_4con.can_ges_campanias_ft_codlista",
    "de_bsf_4con.can_ges_campanias_ft_micrositio_4u",
    "de_bsf_4con.can_ges_campanias_ft_micrositio_empresa",
    "de_bsf_4con.can_ges_campanias_ft_micrositio_misolucion",
    "de_bsf_4con.can_ges_campanias_ft_micrositio_tcma",
    "de_bsf_4con.can_ges_campanias_ft_respuesta_contratacion_producto",
    "de_bsf_4con.can_ges_campanias_ft_respuesta_icommkt",
    "de_bsf_4con.can_ges_campanias_ft_respuesta_notificacion_oferta",
    "de_bsf_4con.can_ges_contact_center_ft",
    "de_bsf_4con.can_ges_hb_empresas_ft_auditoria_errores",
    "de_bsf_4con.can_ges_hb_empresas_parametria_actividades",
    "de_bsf_4con.can_ges_hb_ft_auditoria_errores",
    "de_bsf_4con.can_ges_hb_ft_login",
    "de_bsf_4con.can_ges_hb_ft_transacciones",
    "de_bsf_4con.can_ges_hb_parametria_actividades",
    "de_bsf_4con.can_ges_homebanking_dim_abt_empresa",
    "de_bsf_4con.can_ges_homebanking_dim_abt_empresas",
    "de_bsf_4con.can_ges_homebanking_empresas_ft_login",
    "de_bsf_4con.can_ges_homebanking_empresas_transacciones",
    "de_bsf_4con.can_ges_parametria_dim_oficiales",
    "de_bsf_4con.can_ges_parametria_dim_oficiales_cuenta",
    "de_bsf_4con.can_ges_parametria_dim_sucursal",
    "de_bsf_4con.can_ges_parametria_dim_sucursal_cg",
    "de_bsf_4con.can_ges_parametria_dim_sucursal_meta4",
    "de_bsf_4con.can_ges_parametria_dim_sucursales",
    "de_bsf_4con.can_ges_parametria_ft_metas_grupales",
    "de_bsf_4con.can_ges_parametria_ft_metas_individuales",
    "de_bsf_4con.can_ges_parametria_ft_uptime_atm",
    "de_bsf_4con.can_ges_parametria_rel_carterizacion",
    "de_bsf_4con.can_ges_turnero_ft_turnos_engage",
    "de_bsf_4con.can_ges_workflow_ft_mesa_entrada",
    "de_bsf_4con.can_ges_workflow_ft_tramites",
    "de_bsf_4con.can_ges_workflow_rel_soli_relacion_persona",
    "de_bsf_4con.clientes_contactabilidad_direccion_dim",
    "de_bsf_4con.clientes_contactabilidad_mail_dim",
    "de_bsf_4con.clientes_contactabilidad_telefono_dim",
    "de_bsf_4con.clientes_datos_adicionales_dim_abt_empresa",
    "de_bsf_4con.clientes_datos_adicionales_dim_abt_empresas",
    "de_bsf_4con.clientes_datos_identificatorios_dim",
    "de_bsf_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "de_bsf_4con.clientes_datos_identificatorios_dim_ampp",
    "de_bsf_4con.clientes_datos_identificatorios_dim_data_gp",
    "de_bsf_4con.clientes_datos_identificatorios_dim_temp",
    "de_bsf_4con.clientes_datos_identificatorios_rel_documentos",
    "de_bsf_4con.clientes_datos_impositivos_dim",
    "de_bsf_4con.clientes_datos_impositivos_dim_abt_empresas",
    "de_bsf_4con.clientes_legajo_digital_dim_abt_empresa",
    "de_bsf_4con.clientes_legajo_digital_dim_abt_empresas",
    "de_bsf_4con.clientes_perfil_comercial_dim",
    "de_bsf_4con.clientes_perfil_comercial_dim_abt_empresas",
    "de_bsf_4con.clientes_perfil_comercial_dim_manual_carterizacion_oficiales",
    "de_bsf_4con.clientes_perfil_comercial_dim_manual_segmento_instituciones",
    "de_bsf_4con.clientes_productos_dim_activos",
    "de_bsf_4con.contabilidad_balance_dim_abt_empresas",
    "de_bsf_4con.contabilidad_cuentas_contables",
    "de_bsf_4con.contabilidad_importes_cuentas_contables",
    "de_bsf_4con.contabilidad_mov_contables_dim_abt_empresas",
    "de_bsf_4con.contabilidad_mov_contables_dim_plan_cuentas",
    "de_bsf_4con.contabilidad_mov_contables_ft_imputaciones",
    "de_bsf_4con.contabilidad_pf_datos_certificados",
    "de_bsf_4con.contabilidad_pf_devengamientos",
    "de_bsf_4con.contabilidad_pf_ft_montos_uva",
    "de_bsf_4con.eva_calculosiniciales",
    "de_bsf_4con.exp_cliente_nps_ft_encuesta",
    "de_bsf_4con.finanzas_cot_indices_ft_cotizaciones",
    "de_bsf_4con.ft_precalificados",
    "de_bsf_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "de_bsf_4con.legales_denuncias_dim_abt_empresas",
    "de_bsf_4con.legales_mora_judicial_dim_abt_empresas",
    "de_bsf_4con.legales_mora_judicial_ft_mail",
    "de_bsf_4con.legales_mora_judicial_ft_sms",
    "de_bsf_4con.parametria_datos_generales_demograficos",
    "de_bsf_4con.party_status_hist",
    "de_bsf_4con.productos_ca_dim",
    "de_bsf_4con.productos_ca_dim_tasas_interes",
    "de_bsf_4con.productos_ca_ft",
    "de_bsf_4con.productos_caja_ahorro_dim_maestro",
    "de_bsf_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "de_bsf_4con.productos_caja_de_ahorro_ft_maestro_historico_bis",
    "de_bsf_4con.productos_caja_de_ahorro_ft_maestro_historico_tres",
    "de_bsf_4con.productos_cajas_segurdidad_dim_titular",
    "de_bsf_4con.productos_cajas_seguridad_dim_caja",
    "de_bsf_4con.productos_cajas_seguridad_dim_cta_contable",
    "de_bsf_4con.productos_cajas_seguridad_dim_cuenta_debito",
    "de_bsf_4con.productos_cajas_seguridad_dim_modelo",
    "de_bsf_4con.productos_cajas_seguridad_dim_tipo_contrato",
    "de_bsf_4con.productos_cajas_seguridad_ft_asiento",
    "de_bsf_4con.productos_cajas_seguridad_ft_contrato",
    "de_bsf_4con.productos_cajas_seguridad_ft_factura",
    "de_bsf_4con.productos_cajas_seguridad_ft_moviento_factura",
    "de_bsf_4con.productos_cajas_seguridad_ft_recibo",
    "de_bsf_4con.productos_cantidad_activos",
    "de_bsf_4con.productos_cc_dim",
    "de_bsf_4con.productos_cc_ft_movimiento",
    "de_bsf_4con.productos_cc_ft_saldo",
    "de_bsf_4con.productos_cheques_dim_convenio_cliente",
    "de_bsf_4con.productos_cheques_dim_convenios",
    "de_bsf_4con.productos_cheques_dim_convenios_depositos",
    "de_bsf_4con.productos_cheques_dim_depositos",
    "de_bsf_4con.productos_cheques_dim_echeq_librados",
    "de_bsf_4con.productos_cheques_dim_empresas",
    "de_bsf_4con.productos_cheques_dim_firmantes",
    "de_bsf_4con.productos_cheques_dim_negociados",
    "de_bsf_4con.productos_cheques_dim_usuarios",
    "de_bsf_4con.productos_contabilidad_dim_imputaciones_contables",
    "de_bsf_4con.productos_contabilidad_dim_imputaciones_contables_refactor",
    "de_bsf_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "de_bsf_4con.productos_contabilidad_dim_plan_cuentas",
    "de_bsf_4con.productos_cta_corriente_dim_maestro",
    "de_bsf_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "de_bsf_4con.productos_cta_corriente_ft_historico_acuerdos",
    "de_bsf_4con.productos_cta_corriente_ft_maestro_historico",
    "de_bsf_4con.productos_cuentas_negocio_ft",
    "de_bsf_4con.productos_dep_val_cheques_ft_empresa",
    "de_bsf_4con.productos_dim_maestro_chequeras",
    "de_bsf_4con.productos_dim_transaccion_permitida",
    "de_bsf_4con.productos_garantias_dim_maestro",
    "de_bsf_4con.productos_haberes_bolsa_movimientos_ft",
    "de_bsf_4con.productos_haberes_cargas_masivas_ft",
    "de_bsf_4con.productos_haberes_convenios_dim",
    "de_bsf_4con.productos_haberes_dim_abt_empresas",
    "de_bsf_4con.productos_haberes_dim_convenios",
    "de_bsf_4con.productos_haberes_dim_cuenta_sueldo",
    "de_bsf_4con.productos_haberes_empresas_convenios_dim",
    "de_bsf_4con.productos_haberes_empresas_maestro_dim",
    "de_bsf_4con.productos_haberes_ft_adelanto",
    "de_bsf_4con.productos_haberes_ft_convenios",
    "de_bsf_4con.productos_haberes_ft_convenioslkp",
    "de_bsf_4con.productos_maestro_operaciones_ft",
    "de_bsf_4con.productos_maestro_tipos_operaciones_dim",
    "de_bsf_4con.productos_monedaextranjera_dim_concepto",
    "de_bsf_4con.productos_monedaextranjera_ft_boletos",
    "de_bsf_4con.productos_monedaextranjera_ft_compraventa",
    "de_bsf_4con.productos_movimientos_detalle_dim",
    "de_bsf_4con.productos_operaciones_detalle_cuotas_dim",
    "de_bsf_4con.productos_paquetes_dim",
    "de_bsf_4con.productos_paquetes_dim_abt_empresa",
    "de_bsf_4con.productos_paquetes_dim_abt_empresas",
    "de_bsf_4con.productos_paquetes_dim_bajas",
    "de_bsf_4con.productos_paquetes_dim_mantenimiento_impuestos",
    "de_bsf_4con.productos_paquetes_dim_mantenimiento_tc",
    "de_bsf_4con.productos_paquetes_dim_paquetes_ca",
    "de_bsf_4con.productos_paquetes_dim_paquetes_cc",
    "de_bsf_4con.productos_paquetes_dim_paquetes_no_vista",
    "de_bsf_4con.productos_paquetes_ft_paquetes",
    "de_bsf_4con.productos_parametria_dim_acordante",
    "de_bsf_4con.productos_parametria_dim_aplica_comision",
    "de_bsf_4con.productos_parametria_dim_aplica_empresa",
    "de_bsf_4con.productos_parametria_dim_atrib_cont_bcra",
    "de_bsf_4con.productos_parametria_dim_cod_aliados",
    "de_bsf_4con.productos_parametria_dim_fondos_destino",
    "de_bsf_4con.productos_parametria_dim_lim",
    "de_bsf_4con.productos_parametria_dim_manual",
    "de_bsf_4con.productos_parametria_dim_moneda",
    "de_bsf_4con.productos_parametria_dim_moneda_refactor",
    "de_bsf_4con.productos_parametria_dim_nivel",
    "de_bsf_4con.productos_parametria_dim_operativa_contable",
    "de_bsf_4con.productos_parametria_dim_paquetes",
    "de_bsf_4con.productos_parametria_dim_productos",
    "de_bsf_4con.productos_parametria_dim_provincias",
    "de_bsf_4con.productos_parametria_dim_punto_vta",
    "de_bsf_4con.productos_parametria_dim_rechazo",
    "de_bsf_4con.productos_parametria_dim_relacion_titularidad",
    "de_bsf_4con.productos_parametria_dim_relacion_titularidad_refactor",
    "de_bsf_4con.productos_parametria_dim_sec_residencia",
    "de_bsf_4con.productos_parametria_dim_sector_residencia",
    "de_bsf_4con.productos_parametria_dim_servicios",
    "de_bsf_4con.productos_parametria_dim_sublim",
    "de_bsf_4con.productos_parametria_dim_tipo_boleta",
    "de_bsf_4con.productos_parametria_dim_tipo_comision",
    "de_bsf_4con.productos_parametria_dim_tipo_fondos",
    "de_bsf_4con.productos_parametria_ft_calendario_saldo",
    "de_bsf_4con.productos_parametria_ft_codigos_base",
    "de_bsf_4con.productos_pf_dim_abt_empresas",
    "de_bsf_4con.productos_pf_ft",
    "de_bsf_4con.productos_pf_ft_certificados",
    "de_bsf_4con.productos_pf_maestro_cuentas_inversoras",
    "de_bsf_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "de_bsf_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras_refactor",
    "de_bsf_4con.productos_plazo_fijo_ft_certificados",
    "de_bsf_4con.productos_plazo_fijo_ft_montos_uva",
    "de_bsf_4con.productos_plazo_fijos_dim_parametros",
    "de_bsf_4con.productos_prestamos_cuentas_negocio",
    "de_bsf_4con.productos_prestamos_dim_abt_empresas",
    "de_bsf_4con.productos_prestamos_dim_cuotas_generadas",
    "de_bsf_4con.productos_prestamos_dim_maestro",
    "de_bsf_4con.productos_prestamos_dim_maestro_cuotas",
    "de_bsf_4con.productos_prestamos_ft",
    "de_bsf_4con.productos_prestamos_ft_residuales",
    "de_bsf_4con.productos_prestamos_gestion_mora",
    "de_bsf_4con.productos_prestamos_rel_garantia_prestamo",
    "de_bsf_4con.productos_previsiones_minimas",
    "de_bsf_4con.productos_previsiones_modulocomp",
    "de_bsf_4con.productos_previsiones_parametros",
    "de_bsf_4con.productos_recaudaciones_dim_api_comision_param",
    "de_bsf_4con.productos_recaudaciones_dim_api_impuesto_param",
    "de_bsf_4con.productos_recaudaciones_dim_boca_param",
    "de_bsf_4con.productos_recaudaciones_dim_ente_param",
    "de_bsf_4con.productos_recaudaciones_dim_formulario_impuesto",
    "de_bsf_4con.productos_recaudaciones_dim_osiris_comision",
    "de_bsf_4con.productos_recaudaciones_dim_osiris_formulario",
    "de_bsf_4con.productos_recaudaciones_dim_osiris_impuesto",
    "de_bsf_4con.productos_recaudaciones_dim_vigencia_impuesto",
    "de_bsf_4con.productos_recaudaciones_ft_osiris_historico",
    "de_bsf_4con.productos_recaudaciones_ft_osiris_transaccion",
    "de_bsf_4con.productos_recaudaciones_ft_pdc_movimiento",
    "de_bsf_4con.productos_recaudaciones_ft_transaccion_ente",
    "de_bsf_4con.productos_request_tracking",
    "de_bsf_4con.productos_saldos_diarios_ft",
    "de_bsf_4con.productos_saldos_prestamos",
    "de_bsf_4con.productos_seguros_dim_maestro",
    "de_bsf_4con.productos_seguros_dim_qualia",
    "de_bsf_4con.productos_seguros_ft",
    "de_bsf_4con.productos_seguros_ft_solicitud_baja",
    "de_bsf_4con.productos_tarjeta_credito_dim_comisiones",
    "de_bsf_4con.productos_tarjetas_debito_dim_maestro",
    "de_bsf_4con.productos_tarjetas_debito_movimientos",
    "de_bsf_4con.productos_tarjetas_debito_seguimiento",
    "de_bsf_4con.productos_tarjetas_promocion_individuos",
    "de_bsf_4con.productos_ttcc_dim_abt_empresas",
    "de_bsf_4con.productos_ttcc_dim_maestro",
    "de_bsf_4con.productos_ttcc_dim_plasticos",
    "de_bsf_4con.productos_ttcc_ft_mov_cred",
    "de_bsf_4con.productos_ttcc_ft_mov_prisma",
    "de_bsf_4con.productos_ttdd_dim",
    "de_bsf_4con.productos_ttdd_dim_maestro",
    "de_bsf_4con.prueba2",
    "de_bsf_4con.prueba3",
    "de_bsf_4con.prueba4",
    "de_bsf_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "de_bsf_4con.riesgos_adm_crediticia_balance",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_afip",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "de_bsf_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_bsf_4con.riesgos_adm_crediticia_datos_adicionales",
    "de_bsf_4con.riesgos_adm_crediticia_datos_impositivos",
    "de_bsf_4con.riesgos_adm_crediticia_datos_personales",
    "de_bsf_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "de_bsf_4con.riesgos_adm_crediticia_dim_lim",
    "de_bsf_4con.riesgos_adm_crediticia_dim_linea",
    "de_bsf_4con.riesgos_adm_crediticia_dim_linea_deuda",
    "de_bsf_4con.riesgos_adm_crediticia_dim_no_clientes",
    "de_bsf_4con.riesgos_adm_crediticia_dim_plafond",
    "de_bsf_4con.riesgos_adm_crediticia_dim_sublim",
    "de_bsf_4con.riesgos_adm_crediticia_dim_workflow",
    "de_bsf_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_bsf_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_bsf_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "de_bsf_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_bsf_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_bsf_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_bsf_4con.riesgos_adm_crediticia_eva_score",
    "de_bsf_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "de_bsf_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_bsf_4con.riesgos_adm_crediticia_eva_script",
    "de_bsf_4con.riesgos_adm_crediticia_ft_calificador_lim",
    "de_bsf_4con.riesgos_adm_crediticia_ft_link",
    "de_bsf_4con.riesgos_adm_crediticia_ft_sin_haberes",
    "de_bsf_4con.riesgos_adm_crediticia_home_banking",
    "de_bsf_4con.riesgos_adm_crediticia_limites_y_garantias",
    "de_bsf_4con.riesgos_adm_crediticia_mora",
    "de_bsf_4con.riesgos_adm_crediticia_of_calculosfinales",
    "de_bsf_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "de_bsf_4con.riesgos_adm_crediticia_of_decisionfinal",
    "de_bsf_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "de_bsf_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_bsf_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "de_bsf_4con.riesgos_adm_crediticia_of_niveldefirma",
    "de_bsf_4con.riesgos_adm_crediticia_of_postburo",
    "de_bsf_4con.riesgos_adm_crediticia_of_reclasificacion",
    "de_bsf_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "de_bsf_4con.riesgos_adm_crediticia_of_score",
    "de_bsf_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "de_bsf_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_bsf_4con.riesgos_adm_crediticia_of_topedecliente",
    "de_bsf_4con.riesgos_adm_crediticia_of_tramites",
    "de_bsf_4con.riesgos_adm_crediticia_of_verificaciones",
    "de_bsf_4con.riesgos_adm_crediticia_of_vigencias",
    "de_bsf_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "de_bsf_4con.riesgos_adm_crediticia_perfil_tecnico",
    "de_bsf_4con.riesgos_adm_crediticia_prestamos",
    "de_bsf_4con.riesgos_adm_crediticia_sucursales",
    "de_bsf_4con.riesgos_adm_crediticia_tarjetas",
    "de_bsf_4con.riesgos_calificacion_prestamos_tarjetas",
    "de_bsf_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_bsf_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "de_bsf_4con.riesgos_recupero_dim_cartera_diaria_morosa",
    "de_bsf_4con.riesgos_recupero_ft_gestiones",
    "de_bsf_4con.rrhh_perfil_colaborador_dim_empleado",
    "de_bsf_4con.vw_caja_ahorro_cuentas_contables",
    "de_bsf_4con.vw_caja_ahorro_datos_basicos",
    "de_bsf_4con.vw_caja_ahorro_embargos",
    "de_bsf_4con.vw_caja_ahorro_movimientos",
    "de_bsf_4con.vw_caja_ahorro_movimientos_ccc",
    "de_bsf_4con.vw_caja_ahorro_saldos",
    "de_bsf_4con.vw_caja_ahorro_saldos_test",
    "de_bsf_4con.vw_caja_ahorro_tarjetas_debito",
    "de_bsf_4con.vw_caja_ahorro_titularidad_relacion",
    "de_bsf_4con.vw_caja_ahorro_transacciones_habilitadas",
    "de_bsf_4con.vw_cheques_chequeras",
    "de_bsf_4con.vw_cheques_convenios",
    "de_bsf_4con.vw_clientes_rel_vn",
    "de_bsf_4con.vw_clientes_rel_vn_bsf",
    "de_bsf_4con.vw_cuenta_corriente_acuerdos",
    "de_bsf_4con.vw_cuenta_corriente_datos_basicos",
    "de_bsf_4con.vw_cuenta_corriente_datos_basicos_rm",
    "de_bsf_4con.vw_cuenta_corriente_datos_basicos_test",
    "de_bsf_4con.vw_cuenta_corriente_embargos",
    "de_bsf_4con.vw_cuenta_corriente_garantias",
    "de_bsf_4con.vw_cuenta_corriente_maestro_historico",
    "de_bsf_4con.vw_cuenta_corriente_titularidad_relacion",
    "de_bsf_4con.vw_maestro_vn",
    "de_bsf_4con.vw_prestamos_cobranzas_movimientos",
    "de_bsf_4con.vw_prod_vn_cheques",
    "de_bsf_4con.vw_productos_paquetes_datos_basicos",
    "de_bsf_4con.vw_productos_parametria_dim_relacion_titularidad",
    "de_bsf_4con.vw_productos_pf_dim_maestro_cuentas_inversoras",
    "de_bsf_4con.vw_productos_plazo_fijo_ft_certificados",
    "de_bsf_4con.vw_productos_prestamos_dim_maestro",
    "de_bsf_4con.vw_riesgos_adm_crediticia_dim_lim",
    "de_bsf_4con.vw_riesgos_adm_crediticia_dim_linea",
    "de_bsf_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "de_bsf_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "de_bsj_4con.beneficios_tienda_clic_ft_compra",
    "de_bsj_4con.can_gen_empleadores_sector_publico",
    "de_bsj_4con.can_ges_caja_presencial_dim",
    "de_bsj_4con.can_ges_campania_ft_respuesta",
    "de_bsj_4con.can_ges_campanias_dim_engage_lista",
    "de_bsj_4con.can_ges_campanias_ft_codlista",
    "de_bsj_4con.can_ges_campanias_ft_micrositio_4u",
    "de_bsj_4con.can_ges_campanias_ft_micrositio_empresa",
    "de_bsj_4con.can_ges_campanias_ft_micrositio_misolucion",
    "de_bsj_4con.can_ges_campanias_ft_micrositio_tcma",
    "de_bsj_4con.can_ges_campanias_ft_respuesta_contratacion_producto",
    "de_bsj_4con.can_ges_campanias_ft_respuesta_icommkt",
    "de_bsj_4con.can_ges_campanias_ft_respuesta_notificacion_oferta",
    "de_bsj_4con.can_ges_contact_center_ft",
    "de_bsj_4con.can_ges_hb_ft_auditoria_errores",
    "de_bsj_4con.can_ges_hb_ft_login",
    "de_bsj_4con.can_ges_hb_ft_transacciones",
    "de_bsj_4con.can_ges_hb_parametria_actividades",
    "de_bsj_4con.can_ges_homebanking_dim_abt_empresa",
    "de_bsj_4con.can_ges_homebanking_dim_abt_empresas",
    "de_bsj_4con.can_ges_parametria_dim_oficiales",
    "de_bsj_4con.can_ges_parametria_dim_sucursal",
    "de_bsj_4con.can_ges_parametria_dim_sucursal_cg",
    "de_bsj_4con.can_ges_parametria_dim_sucursal_meta4",
    "de_bsj_4con.can_ges_parametria_dim_sucursales",
    "de_bsj_4con.can_ges_parametria_ft_metas_grupales",
    "de_bsj_4con.can_ges_parametria_ft_metas_individuales",
    "de_bsj_4con.can_ges_parametria_ft_uptime_atm",
    "de_bsj_4con.can_ges_parametria_rel_carterizacion",
    "de_bsj_4con.can_ges_turnero_ft_turnos_engage",
    "de_bsj_4con.can_ges_workflow_ft_mesa_entrada",
    "de_bsj_4con.can_ges_workflow_rel_soli_relacion_persona",
    "de_bsj_4con.clientes_afip_dim",
    "de_bsj_4con.clientes_contactabilidad_direccion_dim",
    "de_bsj_4con.clientes_contactabilidad_mail_dim",
    "de_bsj_4con.clientes_contactabilidad_telefono_dim",
    "de_bsj_4con.clientes_datos_adicionales_dim_abt_empresa",
    "de_bsj_4con.clientes_datos_adicionales_dim_abt_empresas",
    "de_bsj_4con.clientes_datos_identificatorios_dim",
    "de_bsj_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "de_bsj_4con.clientes_datos_identificatorios_dim_ampp",
    "de_bsj_4con.clientes_datos_identificatorios_dim_datagp",
    "de_bsj_4con.clientes_datos_identificatorios_dim_temp",
    "de_bsj_4con.clientes_datos_identificatorios_rel_documentos",
    "de_bsj_4con.clientes_datos_impositivos_dim",
    "de_bsj_4con.clientes_datos_impositivos_dim_abt_empresas",
    "de_bsj_4con.clientes_documentos_dim",
    "de_bsj_4con.clientes_legajo_digital_dim_abt_empresa",
    "de_bsj_4con.clientes_legajo_digital_dim_abt_empresas",
    "de_bsj_4con.clientes_perfil_comercial_dim",
    "de_bsj_4con.clientes_perfil_comercial_dim_abt_empresas",
    "de_bsj_4con.clientes_perfil_comercial_dim_manual_carterizacion_oficiales",
    "de_bsj_4con.clientes_perfil_comercial_dim_manual_segmento_instituciones",
    "de_bsj_4con.clientes_productos_dim_activos",
    "de_bsj_4con.contabilidad_balance_dim_abt_empresas",
    "de_bsj_4con.contabilidad_mov_contables_dim_abt_empresas",
    "de_bsj_4con.dt_productos_prestamos_dim_cuotas_procesadas",
    "de_bsj_4con.exp_cliente_nps_ft_encuesta",
    "de_bsj_4con.finanzas_cot_indices_ft_cotizaciones",
    "de_bsj_4con.ft_precalificados",
    "de_bsj_4con.inventario_acuerdos_cobros",
    "de_bsj_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "de_bsj_4con.legales_denuncias_dim_abt_empresas",
    "de_bsj_4con.legales_mora_judicial_dim_abt_empresas",
    "de_bsj_4con.legales_mora_judicial_ft_mail",
    "de_bsj_4con.legales_mora_judicial_ft_sms",
    "de_bsj_4con.parametria_datos_generales_demograficos",
    "de_bsj_4con.parametria_datos_generales_provincias_dim",
    "de_bsj_4con.productos_ca_dim",
    "de_bsj_4con.productos_ca_dim_tasas_interes",
    "de_bsj_4con.productos_ca_ft",
    "de_bsj_4con.productos_ca_ft_prueba",
    "de_bsj_4con.productos_caja_ahorro_dim_maestro",
    "de_bsj_4con.productos_caja_ahorro_movimientos_dim",
    "de_bsj_4con.productos_caja_de_ahorro_dim_embargos",
    "de_bsj_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "de_bsj_4con.productos_caja_de_ahorro_transaccion_permitida",
    "de_bsj_4con.productos_cajas_seguridad_alta_contratos",
    "de_bsj_4con.productos_cajas_seguridad_dim_cotitulares",
    "de_bsj_4con.productos_cajas_seguridad_dim_param_estados",
    "de_bsj_4con.productos_cajas_seguridad_dim_provincia",
    "de_bsj_4con.productos_cajas_seguridad_dim_sucursal",
    "de_bsj_4con.productos_cajas_seguridad_dim_tamanio_cajas",
    "de_bsj_4con.productos_cajas_seguridad_ft_bajas_alquileres",
    "de_bsj_4con.productos_cajas_seguridad_ft_cta_cte",
    "de_bsj_4con.productos_cajas_seguridad_ft_estados",
    "de_bsj_4con.productos_cajas_seguridad_ft_personas_autorizadas",
    "de_bsj_4con.productos_can_ges_parametria_tasas_pasivas",
    "de_bsj_4con.productos_cc_dim",
    "de_bsj_4con.productos_cc_ft_movimiento",
    "de_bsj_4con.productos_cc_ft_saldo",
    "de_bsj_4con.productos_cheques_dim_convenio_cliente",
    "de_bsj_4con.productos_cheques_dim_convenios",
    "de_bsj_4con.productos_cheques_dim_convenios_depositos",
    "de_bsj_4con.productos_cheques_dim_datos_identificatorios_clientes",
    "de_bsj_4con.productos_cheques_dim_depositos",
    "de_bsj_4con.productos_cheques_dim_echeq_librados",
    "de_bsj_4con.productos_cheques_dim_empresas",
    "de_bsj_4con.productos_cheques_dim_maestro_bancos",
    "de_bsj_4con.productos_cheques_dim_maestro_codigos_postales",
    "de_bsj_4con.productos_cheques_dim_maestro_plazas",
    "de_bsj_4con.productos_cheques_dim_negociados",
    "de_bsj_4con.productos_cheques_dim_usuarios",
    "de_bsj_4con.productos_cliente_dim_cuenta",
    "de_bsj_4con.productos_contabilidad_dim_comisiones",
    "de_bsj_4con.productos_contabilidad_dim_maestro_causales",
    "de_bsj_4con.productos_contabilidad_dim_maestro_equivalencias_contables",
    "de_bsj_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "de_bsj_4con.productos_contabilidad_dim_maestro_tareas_cierre",
    "de_bsj_4con.productos_contabilidad_dim_minuta",
    "de_bsj_4con.productos_contabilidad_dim_renglon_minuta",
    "de_bsj_4con.productos_cta_corriente_dim_embargos",
    "de_bsj_4con.productos_cta_corriente_dim_maestro",
    "de_bsj_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "de_bsj_4con.productos_cta_corriente_ft_maestro_historico",
    "de_bsj_4con.productos_cta_corriente_movimientos_dim",
    "de_bsj_4con.productos_cta_corriente_param_dim_relacion_titularidad",
    "de_bsj_4con.productos_dep_val_cheques_ft_empresa",
    "de_bsj_4con.productos_dim_maestro_chequeras",
    "de_bsj_4con.productos_dim_maestro_valores_cesion",
    "de_bsj_4con.productos_dim_maestro_valores_sesion",
    "de_bsj_4con.productos_ft_certificados",
    "de_bsj_4con.productos_garantias_dim_maestro",
    "de_bsj_4con.productos_garantias_rel_operaciones",
    "de_bsj_4con.productos_haberes_cargas_masivas_ft",
    "de_bsj_4con.productos_haberes_dim_abt_empresas",
    "de_bsj_4con.productos_haberes_dim_convenios",
    "de_bsj_4con.productos_haberes_dim_cuenta_sueldo",
    "de_bsj_4con.productos_haberes_empresas_clientes_ft",
    "de_bsj_4con.productos_haberes_empresas_dim",
    "de_bsj_4con.productos_haberes_ft_adelanto",
    "de_bsj_4con.productos_haberes_ft_convenios",
    "de_bsj_4con.productos_haberes_ft_convenioslkp",
    "de_bsj_4con.productos_lineas_especiales_dim",
    "de_bsj_4con.productos_maestro_causales",
    "de_bsj_4con.productos_monedaextranjera_ft_compraventa",
    "de_bsj_4con.productos_paquetes_dim",
    "de_bsj_4con.productos_paquetes_dim_abt_empresa",
    "de_bsj_4con.productos_paquetes_dim_abt_empresas",
    "de_bsj_4con.productos_paquetes_dim_parametros_affinity",
    "de_bsj_4con.productos_paquetes_ft_movimientos_pagos",
    "de_bsj_4con.productos_paquetes_rel_paq_cc_ca",
    "de_bsj_4con.productos_paquetes_rel_pqtca_comisiones",
    "de_bsj_4con.productos_paquetes_rel_vinculacion_cuentas",
    "de_bsj_4con.productos_parametria_dim_acordante",
    "de_bsj_4con.productos_parametria_dim_atrib_cont_bcra",
    "de_bsj_4con.productos_parametria_dim_codigos_tasa",
    "de_bsj_4con.productos_parametria_dim_condicion_iva",
    "de_bsj_4con.productos_parametria_dim_destino_econom",
    "de_bsj_4con.productos_parametria_dim_divisas",
    "de_bsj_4con.productos_parametria_dim_estado_cuenta",
    "de_bsj_4con.productos_parametria_dim_estado_ppmap",
    "de_bsj_4con.productos_parametria_dim_general_bancos",
    "de_bsj_4con.productos_parametria_dim_lim",
    "de_bsj_4con.productos_parametria_dim_manual",
    "de_bsj_4con.productos_parametria_dim_moneda",
    "de_bsj_4con.productos_parametria_dim_moneda_refactor",
    "de_bsj_4con.productos_parametria_dim_motivos_cierres",
    "de_bsj_4con.productos_parametria_dim_nivel",
    "de_bsj_4con.productos_parametria_dim_operativa_contable",
    "de_bsj_4con.productos_parametria_dim_origen_fondos",
    "de_bsj_4con.productos_parametria_dim_paquetes",
    "de_bsj_4con.productos_parametria_dim_periodocpa",
    "de_bsj_4con.productos_parametria_dim_plazo_fijo",
    "de_bsj_4con.productos_parametria_dim_productos",
    "de_bsj_4con.productos_parametria_dim_punto_vta",
    "de_bsj_4con.productos_parametria_dim_rechazo",
    "de_bsj_4con.productos_parametria_dim_relacion_cliente_cuenta",
    "de_bsj_4con.productos_parametria_dim_relacion_portafolio_cuentas",
    "de_bsj_4con.productos_parametria_dim_relacion_titularidad",
    "de_bsj_4con.productos_parametria_dim_relacion_titularidad_refactor",
    "de_bsj_4con.productos_parametria_dim_sector_residencia",
    "de_bsj_4con.productos_parametria_dim_sist_amort",
    "de_bsj_4con.productos_parametria_dim_sublim",
    "de_bsj_4con.productos_parametria_dim_sucursales_provincia",
    "de_bsj_4con.productos_parametria_dim_tipo_boleta",
    "de_bsj_4con.productos_parametria_dim_tipo_embargos",
    "de_bsj_4con.productos_parametria_dim_tipo_empresa",
    "de_bsj_4con.productos_parametria_dim_tipo_servicio",
    "de_bsj_4con.productos_parametria_dim_tipo_tasa",
    "de_bsj_4con.productos_parametria_dim_toma_disp_fondo",
    "de_bsj_4con.productos_parametria_dim_zonas",
    "de_bsj_4con.productos_parametria_ft_calendario_saldo",
    "de_bsj_4con.productos_parametria_tarjeta_debito",
    "de_bsj_4con.productos_parametrias_dim_concepto",
    "de_bsj_4con.productos_pf_dim_abt_empresas",
    "de_bsj_4con.productos_pf_ft",
    "de_bsj_4con.productos_pf_ft_certificados",
    "de_bsj_4con.productos_pf_maestro_cuentas_inversoras",
    "de_bsj_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "de_bsj_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras_refactor",
    "de_bsj_4con.productos_plazo_fijo_ft_certificados",
    "de_bsj_4con.productos_plazo_fijos_dim_parametros",
    "de_bsj_4con.productos_prestamo_transacciones",
    "de_bsj_4con.productos_prestamos_dim_abt_empresas",
    "de_bsj_4con.productos_prestamos_dim_cuotas_generadas",
    "de_bsj_4con.productos_prestamos_dim_maestro",
    "de_bsj_4con.productos_prestamos_dim_maestro_cuotas",
    "de_bsj_4con.productos_prestamos_dim_maestro_vendedores",
    "de_bsj_4con.productos_prestamos_ft",
    "de_bsj_4con.productos_prestamos_ft_gastos_cuotas",
    "de_bsj_4con.productos_prestamos_ft_movimientos_historico",
    "de_bsj_4con.productos_prestamos_ft_residuales",
    "de_bsj_4con.productos_prestamos_ft_residuales_nueva",
    "de_bsj_4con.productos_prestamos_ft_residuales_nueva2",
    "de_bsj_4con.productos_prestamos_rel_carpeta_cliente",
    "de_bsj_4con.productos_prestamos_rel_prefinanciados_productos",
    "de_bsj_4con.productos_recaudaciones_dim_maestro_entes",
    "de_bsj_4con.productos_recaudaciones_dim_parametria_entes",
    "de_bsj_4con.productos_recaudaciones_dim_tasas_interes",
    "de_bsj_4con.productos_recaudaciones_ft_boletas",
    "de_bsj_4con.productos_recaudaciones_ft_historico",
    "de_bsj_4con.productos_recaudaciones_ft_maestro",
    "de_bsj_4con.productos_request_tracking",
    "de_bsj_4con.productos_seguros_dim_maestro",
    "de_bsj_4con.productos_seguros_dim_qualia",
    "de_bsj_4con.productos_seguros_ft",
    "de_bsj_4con.productos_seguros_ft_solicitud_baja",
    "de_bsj_4con.productos_tarjetas_debito_dim_maestro",
    "de_bsj_4con.productos_tarjetas_debito_ft_cierres",
    "de_bsj_4con.productos_tarjetas_debito_movimientos",
    "de_bsj_4con.productos_tarjetas_promocion_individuos",
    "de_bsj_4con.productos_ttcc_dim_abt_empresas",
    "de_bsj_4con.productos_ttcc_dim_maestro",
    "de_bsj_4con.productos_ttcc_dim_plasticos",
    "de_bsj_4con.productos_ttcc_ft_mov_cred",
    "de_bsj_4con.productos_ttcc_ft_mov_prisma",
    "de_bsj_4con.productos_ttdd_dim",
    "de_bsj_4con.productos_ttdd_dim_maestro",
    "de_bsj_4con.productos_vendedores_dim_maestro",
    "de_bsj_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "de_bsj_4con.riesgos_adm_crediticia_balance",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_afip",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "de_bsj_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_bsj_4con.riesgos_adm_crediticia_datos_adicionales",
    "de_bsj_4con.riesgos_adm_crediticia_datos_impositivos",
    "de_bsj_4con.riesgos_adm_crediticia_datos_personales",
    "de_bsj_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "de_bsj_4con.riesgos_adm_crediticia_dim_lim",
    "de_bsj_4con.riesgos_adm_crediticia_dim_no_clientes",
    "de_bsj_4con.riesgos_adm_crediticia_dim_plafond",
    "de_bsj_4con.riesgos_adm_crediticia_dim_sublim",
    "de_bsj_4con.riesgos_adm_crediticia_dim_workflow",
    "de_bsj_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_bsj_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_bsj_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "de_bsj_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_bsj_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_bsj_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_bsj_4con.riesgos_adm_crediticia_eva_score",
    "de_bsj_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "de_bsj_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_bsj_4con.riesgos_adm_crediticia_eva_script",
    "de_bsj_4con.riesgos_adm_crediticia_ft_calificador_lim",
    "de_bsj_4con.riesgos_adm_crediticia_ft_link",
    "de_bsj_4con.riesgos_adm_crediticia_ft_sin_haberes",
    "de_bsj_4con.riesgos_adm_crediticia_home_banking",
    "de_bsj_4con.riesgos_adm_crediticia_limites_y_garantias",
    "de_bsj_4con.riesgos_adm_crediticia_mora",
    "de_bsj_4con.riesgos_adm_crediticia_of_calculosfinales",
    "de_bsj_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "de_bsj_4con.riesgos_adm_crediticia_of_decisionfinal",
    "de_bsj_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "de_bsj_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_bsj_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "de_bsj_4con.riesgos_adm_crediticia_of_niveldefirma",
    "de_bsj_4con.riesgos_adm_crediticia_of_postburo",
    "de_bsj_4con.riesgos_adm_crediticia_of_reclasificacion",
    "de_bsj_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "de_bsj_4con.riesgos_adm_crediticia_of_score",
    "de_bsj_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "de_bsj_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_bsj_4con.riesgos_adm_crediticia_of_topedecliente",
    "de_bsj_4con.riesgos_adm_crediticia_of_tramites",
    "de_bsj_4con.riesgos_adm_crediticia_of_verificaciones",
    "de_bsj_4con.riesgos_adm_crediticia_of_vigencias",
    "de_bsj_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "de_bsj_4con.riesgos_adm_crediticia_perfil_tecnico",
    "de_bsj_4con.riesgos_adm_crediticia_prestamos",
    "de_bsj_4con.riesgos_adm_crediticia_sucursales",
    "de_bsj_4con.riesgos_adm_crediticia_tarjetas",
    "de_bsj_4con.riesgos_calificacion_prestamos_tarjetas",
    "de_bsj_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_bsj_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "de_bsj_4con.riesgos_recupero_dim_cartera_diaria_morosa",
    "de_bsj_4con.riesgos_recupero_ft_gestiones",
    "de_bsj_4con.rrhh_perfil_colaborador_dim_empleado",
    "de_bsj_4con.tabla_temporal_con",
    "de_bsj_4con.vn_productos_parametria_dim_relacion_titularidad",
    "de_bsj_4con.vw_caja_ahorro_cuentas_contables",
    "de_bsj_4con.vw_caja_ahorro_cuentas_contables_comisiones",
    "de_bsj_4con.vw_caja_ahorro_datos_basicos",
    "de_bsj_4con.vw_caja_ahorro_embargos",
    "de_bsj_4con.vw_caja_ahorro_movimientos",
    "de_bsj_4con.vw_caja_ahorro_saldos",
    "de_bsj_4con.vw_caja_ahorro_tarjetas_debito",
    "de_bsj_4con.vw_caja_ahorro_titularidad_relacion",
    "de_bsj_4con.vw_caja_ahorro_transacciones_habilitadas",
    "de_bsj_4con.vw_cheques_chequeras",
    "de_bsj_4con.vw_cheques_convenios",
    "de_bsj_4con.vw_clientes_rel_vn",
    "de_bsj_4con.vw_clientes_rel_vn_bsj",
    "de_bsj_4con.vw_cuenta_corriente_acuerdos",
    "de_bsj_4con.vw_cuenta_corriente_cuenta_portafolio",
    "de_bsj_4con.vw_cuenta_corriente_datos_basicos",
    "de_bsj_4con.vw_cuenta_corriente_embargos",
    "de_bsj_4con.vw_cuenta_corriente_garantias",
    "de_bsj_4con.vw_cuenta_corriente_maestro_historico",
    "de_bsj_4con.vw_cuenta_corriente_titularidad_relacion",
    "de_bsj_4con.vw_maestro_vn",
    "de_bsj_4con.vw_prestamos_cobranzas_movimientos",
    "de_bsj_4con.vw_prod_vn_cheques",
    "de_bsj_4con.vw_prod_vn_cheques_bsj",
    "de_bsj_4con.vw_productos_paquetes_datos_basicos",
    "de_bsj_4con.vw_productos_parametria_dim_relacion_titularidad",
    "de_bsj_4con.vw_productos_pf_dim_maestro_cuentas_inversoras",
    "de_bsj_4con.vw_productos_plazo_fijo_ft_certificados",
    "de_bsj_4con.vw_productos_prestamos_dim_maestro",
    "de_bsj_4con.vw_riesgos_adm_crediticia_dim_lim",
    "de_bsj_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "de_bsj_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "uat_ber_4con.can_ges_homebanking_dim_abt_empresas",
    "uat_ber_4con.can_ges_parametria_dim_sucursal",
    "uat_ber_4con.can_ges_parametria_dim_sucursal_cg",
    "uat_ber_4con.can_ges_parametria_dim_sucursales",
    "uat_ber_4con.clientes_datos_adicionales_dim_abt_empresas",
    "uat_ber_4con.clientes_datos_identificatorios_dim",
    "uat_ber_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_ber_4con.clientes_datos_identificatorios_rel_documentos",
    "uat_ber_4con.clientes_datos_impositivos_dim",
    "uat_ber_4con.clientes_datos_impositivos_dim_abt_empresas",
    "uat_ber_4con.clientes_legajo_digital_dim_abt_empresas",
    "uat_ber_4con.clientes_perfil_comercial_dim_abt_empresas",
    "uat_ber_4con.clientes_relacion_prestamos",
    "uat_ber_4con.clientes_relacion_valores_negociados",
    "uat_ber_4con.contabilidad_balance_dim_abt_empresas",
    "uat_ber_4con.contabilidad_mov_contables_dim_abt_empresas",
    "uat_ber_4con.ejemplo_external_table",
    "uat_ber_4con.finanzas_cot_indices_ft_cotizaciones",
    "uat_ber_4con.inventario_acuerdos_cobros",
    "uat_ber_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "uat_ber_4con.legales_denuncias_dim_abt_empresas",
    "uat_ber_4con.legales_mora_judicial_dim_abt_empresas",
    "uat_ber_4con.parametria_datos_generales_provincias_dim",
    "uat_ber_4con.prestamos_cuotas",
    "uat_ber_4con.prestamos_garantias",
    "uat_ber_4con.prestamos_relacion_garantias",
    "uat_ber_4con.productos_ca_dim_tasas_interes",
    "uat_ber_4con.productos_caja_ahorro_dim_maestro",
    "uat_ber_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "uat_ber_4con.productos_caja_de_ahorro_transaccion_permitida",
    "uat_ber_4con.productos_can_ges_parametria_tasas_pasivas",
    "uat_ber_4con.productos_cheques_dim_convenios",
    "uat_ber_4con.productos_contabilidad_dim_comisiones",
    "uat_ber_4con.productos_contabilidad_dim_maestro_causales",
    "uat_ber_4con.productos_contabilidad_dim_maestro_equivalencias_contables",
    "uat_ber_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "uat_ber_4con.productos_contabilidad_dim_maestro_tareas_cierre",
    "uat_ber_4con.productos_contabilidad_dim_minuta",
    "uat_ber_4con.productos_cta_corriente_dim_embargos",
    "uat_ber_4con.productos_cta_corriente_dim_maestro",
    "uat_ber_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "uat_ber_4con.productos_cta_corriente_ft_maestro_historico",
    "uat_ber_4con.productos_cta_corriente_param_dim_relacion_titularidad",
    "uat_ber_4con.productos_dim_maestro_chequeras",
    "uat_ber_4con.productos_garantias_dim_maestro",
    "uat_ber_4con.productos_haberes_dim_abt_empresas",
    "uat_ber_4con.productos_paquetes_dim_abt_empresas",
    "uat_ber_4con.productos_parametria_dim_acordante",
    "uat_ber_4con.productos_parametria_dim_estado_cuenta",
    "uat_ber_4con.productos_parametria_dim_lim",
    "uat_ber_4con.productos_parametria_dim_moneda",
    "uat_ber_4con.productos_parametria_dim_motivos_cierres",
    "uat_ber_4con.productos_parametria_dim_nivel",
    "uat_ber_4con.productos_parametria_dim_operativa_contable",
    "uat_ber_4con.productos_parametria_dim_paquetes",
    "uat_ber_4con.productos_parametria_dim_relacion_portafolio_cuentas",
    "uat_ber_4con.productos_parametria_dim_sublim",
    "uat_ber_4con.productos_parametria_dim_sucursal_provincia",
    "uat_ber_4con.productos_parametria_dim_sucursales_provincia",
    "uat_ber_4con.productos_parametria_dim_tipo_embargos",
    "uat_ber_4con.productos_parametria_ft_calendario_saldo",
    "uat_ber_4con.productos_parametrias_dim_concepto",
    "uat_ber_4con.productos_pf_dim_abt_empresas",
    "uat_ber_4con.productos_pf_ft_certificados",
    "uat_ber_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_ber_4con.productos_plazo_fijo_ft_certificados",
    "uat_ber_4con.productos_prestamos_dim_abt_empresas",
    "uat_ber_4con.productos_prestamos_dim_maestro",
    "uat_ber_4con.productos_prestamos_ft_movimientos_historico",
    "uat_ber_4con.productos_seguros_dim_maestro",
    "uat_ber_4con.productos_ttcc_dim_abt_empresas",
    "uat_ber_4con.productos_ttdd_dim_maestro",
    "uat_ber_4con.productos_valores_negociables_cheques",
    "uat_ber_4con.productos_valores_negociables_dim_maestro",
    "uat_ber_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_ber_4con.riesgos_adm_crediticia_balance",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_afip",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_ber_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_ber_4con.riesgos_adm_crediticia_datos_adicionales",
    "uat_ber_4con.riesgos_adm_crediticia_datos_impositivos",
    "uat_ber_4con.riesgos_adm_crediticia_datos_personales",
    "uat_ber_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "uat_ber_4con.riesgos_adm_crediticia_dim_lim",
    "uat_ber_4con.riesgos_adm_crediticia_dim_plafond",
    "uat_ber_4con.riesgos_adm_crediticia_dim_sublim",
    "uat_ber_4con.riesgos_adm_crediticia_dim_workflow",
    "uat_ber_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_ber_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_ber_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_ber_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_ber_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_ber_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_ber_4con.riesgos_adm_crediticia_eva_score",
    "uat_ber_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_ber_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_ber_4con.riesgos_adm_crediticia_eva_script",
    "uat_ber_4con.riesgos_adm_crediticia_home_banking",
    "uat_ber_4con.riesgos_adm_crediticia_limites_y_garantias",
    "uat_ber_4con.riesgos_adm_crediticia_mora",
    "uat_ber_4con.riesgos_adm_crediticia_of_calculosfinales",
    "uat_ber_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_ber_4con.riesgos_adm_crediticia_of_decisionfinal",
    "uat_ber_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_ber_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_ber_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_ber_4con.riesgos_adm_crediticia_of_niveldefirma",
    "uat_ber_4con.riesgos_adm_crediticia_of_postburo",
    "uat_ber_4con.riesgos_adm_crediticia_of_reclasificacion",
    "uat_ber_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_ber_4con.riesgos_adm_crediticia_of_score",
    "uat_ber_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_ber_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_ber_4con.riesgos_adm_crediticia_of_topedecliente",
    "uat_ber_4con.riesgos_adm_crediticia_of_tramites",
    "uat_ber_4con.riesgos_adm_crediticia_of_verificaciones",
    "uat_ber_4con.riesgos_adm_crediticia_of_vigencias",
    "uat_ber_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_ber_4con.riesgos_adm_crediticia_perfil_tecnico",
    "uat_ber_4con.riesgos_adm_crediticia_prestamos",
    "uat_ber_4con.riesgos_adm_crediticia_sucursales",
    "uat_ber_4con.riesgos_adm_crediticia_tarjetas",
    "uat_ber_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_ber_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "uat_ber_4con.vn_cheques",
    "uat_ber_4con.vn_relacion_clientes",
    "uat_ber_4con.vw_caja_ahorro_cuentas_contables",
    "uat_ber_4con.vw_caja_ahorro_cuentas_contables_comisiones",
    "uat_ber_4con.vw_caja_ahorro_datos_basicos",
    "uat_ber_4con.vw_caja_ahorro_embargos",
    "uat_ber_4con.vw_caja_ahorro_movimientos",
    "uat_ber_4con.vw_caja_ahorro_saldos",
    "uat_ber_4con.vw_caja_ahorro_tarjetas_debito",
    "uat_ber_4con.vw_caja_ahorro_titularidad_relacion",
    "uat_ber_4con.vw_caja_ahorro_transacciones_habilitadas",
    "uat_ber_4con.vw_cheques_chequeras",
    "uat_ber_4con.vw_cheques_convenios",
    "uat_ber_4con.vw_cuenta_corriente_acuerdos",
    "uat_ber_4con.vw_cuenta_corriente_cuenta_portafolio",
    "uat_ber_4con.vw_cuenta_corriente_datos_basicos",
    "uat_ber_4con.vw_cuenta_corriente_embargos",
    "uat_ber_4con.vw_cuenta_corriente_garantias",
    "uat_ber_4con.vw_cuenta_corriente_maestro_historico",
    "uat_ber_4con.vw_cuenta_corriente_titularidad_relacion",
    "uat_ber_4con.vw_productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_ber_4con.vw_productos_plazo_fijo_ft_certificados",
    "uat_ber_4con.vw_productos_prestamos_dim_maestro",
    "uat_ber_4con.vw_riesgos_adm_crediticia_dim_lim",
    "uat_ber_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "uat_ber_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "uat_bsc_4con.can_ges_homebanking_dim_abt_empresas",
    "uat_bsc_4con.can_ges_parametria_dim_sucursal_cg",
    "uat_bsc_4con.can_ges_parametria_dim_sucursales",
    "uat_bsc_4con.clientes_datos_adicionales_dim_abt_empresas",
    "uat_bsc_4con.clientes_datos_identificatorios_dim",
    "uat_bsc_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_bsc_4con.clientes_datos_identificatorios_rel_documentos",
    "uat_bsc_4con.clientes_datos_impositivos_dim",
    "uat_bsc_4con.clientes_datos_impositivos_dim_abt_empresas",
    "uat_bsc_4con.clientes_legajo_digital_dim_abt_empresa",
    "uat_bsc_4con.clientes_legajo_digital_dim_abt_empresas",
    "uat_bsc_4con.clientes_perfil_comercial_dim_abt_empresas",
    "uat_bsc_4con.clientes_relacion_prestamos",
    "uat_bsc_4con.clientes_relacion_valores_negociados",
    "uat_bsc_4con.contabilidad_balance_dim_abt_empresa",
    "uat_bsc_4con.contabilidad_balance_dim_abt_empresas",
    "uat_bsc_4con.contabilidad_mov_contables_dim_abt_empresa",
    "uat_bsc_4con.contabilidad_mov_contables_dim_abt_empresas",
    "uat_bsc_4con.finanzas_cot_indices_ft_cotizaciones",
    "uat_bsc_4con.inventario_acuerdos_cobros",
    "uat_bsc_4con.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "uat_bsc_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "uat_bsc_4con.legales_denuncias_dim_abt_empresa",
    "uat_bsc_4con.legales_denuncias_dim_abt_empresas",
    "uat_bsc_4con.legales_mora_judicial_dim_abt_empresa",
    "uat_bsc_4con.legales_mora_judicial_dim_abt_empresas",
    "uat_bsc_4con.parametria_datos_generales_provincias_dim",
    "uat_bsc_4con.prestamos_cuotas",
    "uat_bsc_4con.prestamos_garantias",
    "uat_bsc_4con.prestamos_relacion_garantias",
    "uat_bsc_4con.productos_ca_dim_tasas_interes",
    "uat_bsc_4con.productos_caja_ahorro_dim_maestro",
    "uat_bsc_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "uat_bsc_4con.productos_caja_de_ahorro_transaccion_permitida",
    "uat_bsc_4con.productos_can_ges_parametria_tasas_pasivas",
    "uat_bsc_4con.productos_cheques_dim_convenios",
    "uat_bsc_4con.productos_contabilidad_dim_comisiones",
    "uat_bsc_4con.productos_contabilidad_dim_maestro_causales",
    "uat_bsc_4con.productos_contabilidad_dim_maestro_equivalencias_contables",
    "uat_bsc_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "uat_bsc_4con.productos_contabilidad_dim_maestro_tareas_cierre",
    "uat_bsc_4con.productos_contabilidad_dim_minuta",
    "uat_bsc_4con.productos_cta_corriente_dim_embargos",
    "uat_bsc_4con.productos_cta_corriente_dim_maestro",
    "uat_bsc_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "uat_bsc_4con.productos_cta_corriente_ft_maestro_historico",
    "uat_bsc_4con.productos_cta_corriente_param_dim_relacion_titularidad",
    "uat_bsc_4con.productos_dim_maestro_chequeras",
    "uat_bsc_4con.productos_garantias_dim_maestro",
    "uat_bsc_4con.productos_haberes_dim_abt_empresa",
    "uat_bsc_4con.productos_haberes_dim_abt_empresas",
    "uat_bsc_4con.productos_paquetes_dim_abt_empresa",
    "uat_bsc_4con.productos_paquetes_dim_abt_empresas",
    "uat_bsc_4con.productos_parametria_dim_acordante",
    "uat_bsc_4con.productos_parametria_dim_estado_cuenta",
    "uat_bsc_4con.productos_parametria_dim_lim",
    "uat_bsc_4con.productos_parametria_dim_moneda",
    "uat_bsc_4con.productos_parametria_dim_motivos_cierres",
    "uat_bsc_4con.productos_parametria_dim_nivel",
    "uat_bsc_4con.productos_parametria_dim_operativa_contable",
    "uat_bsc_4con.productos_parametria_dim_paquetes",
    "uat_bsc_4con.productos_parametria_dim_relacion_portafolio_cuentas",
    "uat_bsc_4con.productos_parametria_dim_sublim",
    "uat_bsc_4con.productos_parametria_dim_sucursal_provincia",
    "uat_bsc_4con.productos_parametria_dim_sucursales_provincia",
    "uat_bsc_4con.productos_parametria_dim_tipo_embargos",
    "uat_bsc_4con.productos_parametria_ft_calendario_saldo",
    "uat_bsc_4con.productos_parametrias_dim_concepto",
    "uat_bsc_4con.productos_pf_dim_abt_empresa",
    "uat_bsc_4con.productos_pf_dim_abt_empresas",
    "uat_bsc_4con.productos_pf_ft_certificados",
    "uat_bsc_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_bsc_4con.productos_plazo_fijo_ft_certificados",
    "uat_bsc_4con.productos_prestamos_dim_abt_empresa",
    "uat_bsc_4con.productos_prestamos_dim_abt_empresas",
    "uat_bsc_4con.productos_prestamos_dim_maestro",
    "uat_bsc_4con.productos_prestamos_ft_movimientos_historico",
    "uat_bsc_4con.productos_seguros_dim_maestro",
    "uat_bsc_4con.productos_ttcc_dim_abt_empresa",
    "uat_bsc_4con.productos_ttcc_dim_abt_empresas",
    "uat_bsc_4con.productos_ttdd_dim_maestro",
    "uat_bsc_4con.productos_valores_negociables_cheques",
    "uat_bsc_4con.productos_valores_negociables_dim_maestro",
    "uat_bsc_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_bsc_4con.riesgos_adm_crediticia_balance",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_afip",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_bsc_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_bsc_4con.riesgos_adm_crediticia_datos_adicionales",
    "uat_bsc_4con.riesgos_adm_crediticia_datos_impositivos",
    "uat_bsc_4con.riesgos_adm_crediticia_datos_personales",
    "uat_bsc_4con.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_bsc_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "uat_bsc_4con.riesgos_adm_crediticia_dim_lim",
    "uat_bsc_4con.riesgos_adm_crediticia_dim_plafond",
    "uat_bsc_4con.riesgos_adm_crediticia_dim_sublim",
    "uat_bsc_4con.riesgos_adm_crediticia_dim_workflow",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_score",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_bsc_4con.riesgos_adm_crediticia_eva_script",
    "uat_bsc_4con.riesgos_adm_crediticia_home_banking",
    "uat_bsc_4con.riesgos_adm_crediticia_limites_y_garantias",
    "uat_bsc_4con.riesgos_adm_crediticia_mora",
    "uat_bsc_4con.riesgos_adm_crediticia_of_calculosfinales",
    "uat_bsc_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_bsc_4con.riesgos_adm_crediticia_of_decisionfinal",
    "uat_bsc_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_bsc_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_bsc_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_bsc_4con.riesgos_adm_crediticia_of_niveldefirma",
    "uat_bsc_4con.riesgos_adm_crediticia_of_postburo",
    "uat_bsc_4con.riesgos_adm_crediticia_of_reclasificacion",
    "uat_bsc_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_bsc_4con.riesgos_adm_crediticia_of_score",
    "uat_bsc_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_bsc_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_bsc_4con.riesgos_adm_crediticia_of_topedecliente",
    "uat_bsc_4con.riesgos_adm_crediticia_of_tramites",
    "uat_bsc_4con.riesgos_adm_crediticia_of_verificaciones",
    "uat_bsc_4con.riesgos_adm_crediticia_of_vigencias",
    "uat_bsc_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_bsc_4con.riesgos_adm_crediticia_perfil_tecnico",
    "uat_bsc_4con.riesgos_adm_crediticia_prestamos",
    "uat_bsc_4con.riesgos_adm_crediticia_sucursales",
    "uat_bsc_4con.riesgos_adm_crediticia_tarjetas",
    "uat_bsc_4con.riesgos_dep_val_cheques_dim_abt_empresa",
    "uat_bsc_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_bsc_4con.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_bsc_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "uat_bsc_4con.vn_cheques",
    "uat_bsc_4con.vn_relacion_clientes",
    "uat_bsc_4con.vw_caja_ahorro_cuentas_contables",
    "uat_bsc_4con.vw_caja_ahorro_cuentas_contables_comisiones",
    "uat_bsc_4con.vw_caja_ahorro_datos_basicos",
    "uat_bsc_4con.vw_caja_ahorro_embargos",
    "uat_bsc_4con.vw_caja_ahorro_movimientos",
    "uat_bsc_4con.vw_caja_ahorro_saldos",
    "uat_bsc_4con.vw_caja_ahorro_tarjetas_debito",
    "uat_bsc_4con.vw_caja_ahorro_titularidad_relacion",
    "uat_bsc_4con.vw_caja_ahorro_transacciones_habilitadas",
    "uat_bsc_4con.vw_cheques_chequeras",
    "uat_bsc_4con.vw_cheques_convenios",
    "uat_bsc_4con.vw_cuenta_corriente_acuerdos",
    "uat_bsc_4con.vw_cuenta_corriente_cuenta_portafolio",
    "uat_bsc_4con.vw_cuenta_corriente_datos_basicos",
    "uat_bsc_4con.vw_cuenta_corriente_embargos",
    "uat_bsc_4con.vw_cuenta_corriente_garantias",
    "uat_bsc_4con.vw_cuenta_corriente_maestro_historico",
    "uat_bsc_4con.vw_cuenta_corriente_titularidad_relacion",
    "uat_bsc_4con.vw_productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_bsc_4con.vw_productos_plazo_fijo_ft_certificados",
    "uat_bsc_4con.vw_productos_prestamos_dim_maestro",
    "uat_bsc_4con.vw_riesgos_adm_crediticia_dim_lim",
    "uat_bsc_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "uat_bsc_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "uat_bsf_4con.can_ges_atm_ft_extract_link",
    "uat_bsf_4con.can_ges_homebanking_dim_abt_empresas",
    "uat_bsf_4con.can_ges_parametria_dim_sucursal",
    "uat_bsf_4con.can_ges_parametria_dim_sucursal_cg",
    "uat_bsf_4con.clientes_datos_adicionales_dim_abt_empresas",
    "uat_bsf_4con.clientes_datos_identificatorios_dim",
    "uat_bsf_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_bsf_4con.clientes_datos_identificatorios_rel_documentos",
    "uat_bsf_4con.clientes_datos_impositivos_dim",
    "uat_bsf_4con.clientes_datos_impositivos_dim_abt_empresas",
    "uat_bsf_4con.clientes_legajo_digital_dim_abt_empresa",
    "uat_bsf_4con.clientes_legajo_digital_dim_abt_empresas",
    "uat_bsf_4con.clientes_perfil_comercial_dim_abt_empresas",
    "uat_bsf_4con.clientes_relacion_prestamos",
    "uat_bsf_4con.clientes_relacion_valores_negociados",
    "uat_bsf_4con.contabilidad_balance_dim_abt_empresa",
    "uat_bsf_4con.contabilidad_balance_dim_abt_empresas",
    "uat_bsf_4con.contabilidad_cuentas_contables",
    "uat_bsf_4con.contabilidad_mov_contables_dim_abt_empresa",
    "uat_bsf_4con.contabilidad_mov_contables_dim_abt_empresas",
    "uat_bsf_4con.finanzas_cot_indices_ft_cotizaciones",
    "uat_bsf_4con.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "uat_bsf_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "uat_bsf_4con.legales_denuncias_dim_abt_empresa",
    "uat_bsf_4con.legales_denuncias_dim_abt_empresas",
    "uat_bsf_4con.legales_mora_judicial_dim_abt_empresa",
    "uat_bsf_4con.legales_mora_judicial_dim_abt_empresas",
    "uat_bsf_4con.parametria_datos_generales_provincias_dim",
    "uat_bsf_4con.prestamos_cobranzas_movimientos",
    "uat_bsf_4con.prestamos_cuotas",
    "uat_bsf_4con.prestamos_garantias",
    "uat_bsf_4con.prestamos_relacion_garantias",
    "uat_bsf_4con.productos_ca_dim_tasas_interes",
    "uat_bsf_4con.productos_caja_ahorro_dim_maestro",
    "uat_bsf_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "uat_bsf_4con.productos_caja_de_ahorro_ft_maestro_historico_bis",
    "uat_bsf_4con.productos_cheques_dim_convenios",
    "uat_bsf_4con.productos_contabilidad_dim_imputaciones_contables",
    "uat_bsf_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "uat_bsf_4con.productos_contabilidad_dim_plan_cuentas",
    "uat_bsf_4con.productos_cta_corriente_dim_maestro",
    "uat_bsf_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "uat_bsf_4con.productos_cta_corriente_ft_historico_acuerdos",
    "uat_bsf_4con.productos_cta_corriente_ft_maestro_historico",
    "uat_bsf_4con.productos_cuentas_negocio_ft",
    "uat_bsf_4con.productos_dim_maestro_chequeras",
    "uat_bsf_4con.productos_dim_transaccion_permitida",
    "uat_bsf_4con.productos_garantias_dim_maestro",
    "uat_bsf_4con.productos_haberes_dim_abt_empresa",
    "uat_bsf_4con.productos_haberes_dim_abt_empresas",
    "uat_bsf_4con.productos_maestro_operaciones_ft",
    "uat_bsf_4con.productos_monedaextranjera_dim_concepto",
    "uat_bsf_4con.productos_monedaextranjera_ft_boletos",
    "uat_bsf_4con.productos_monedaextranjera_ft_compraventa",
    "uat_bsf_4con.productos_paquetes_dim_abt_empresa",
    "uat_bsf_4con.productos_paquetes_dim_abt_empresas",
    "uat_bsf_4con.productos_parametria_dim_acordante",
    "uat_bsf_4con.productos_parametria_dim_estado_cuenta",
    "uat_bsf_4con.productos_parametria_dim_lim",
    "uat_bsf_4con.productos_parametria_dim_moneda",
    "uat_bsf_4con.productos_parametria_dim_nivel",
    "uat_bsf_4con.productos_parametria_dim_operativa_contable",
    "uat_bsf_4con.productos_parametria_dim_paquetes",
    "uat_bsf_4con.productos_parametria_dim_relacion_titularidad",
    "uat_bsf_4con.productos_parametria_dim_sublim",
    "uat_bsf_4con.productos_parametria_dim_tipo_garantias",
    "uat_bsf_4con.productos_parametria_ft_calendario_saldo",
    "uat_bsf_4con.productos_pf_dim_abt_empresa",
    "uat_bsf_4con.productos_pf_dim_abt_empresas",
    "uat_bsf_4con.productos_pf_ft_certificados",
    "uat_bsf_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_bsf_4con.productos_plazo_fijo_ft_certificados",
    "uat_bsf_4con.productos_prestamos_dim_abt_empresa",
    "uat_bsf_4con.productos_prestamos_dim_abt_empresas",
    "uat_bsf_4con.productos_prestamos_dim_maestro",
    "uat_bsf_4con.productos_prestamos_rel_garantia_prestamo",
    "uat_bsf_4con.productos_seguros_dim_maestro",
    "uat_bsf_4con.productos_ttcc_dim_abt_empresa",
    "uat_bsf_4con.productos_ttcc_dim_abt_empresas",
    "uat_bsf_4con.productos_ttdd_dim_maestro",
    "uat_bsf_4con.productos_valores_negociables_cheques",
    "uat_bsf_4con.productos_valores_negociables_dim_maestro",
    "uat_bsf_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_bsf_4con.riesgos_adm_crediticia_balance",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_afip",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_bsf_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_bsf_4con.riesgos_adm_crediticia_datos_adicionales",
    "uat_bsf_4con.riesgos_adm_crediticia_datos_impositivos",
    "uat_bsf_4con.riesgos_adm_crediticia_datos_personales",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_lim",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_linea",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_linea_deuda",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_plafond",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_sublim",
    "uat_bsf_4con.riesgos_adm_crediticia_dim_workflow",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_score",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_bsf_4con.riesgos_adm_crediticia_eva_script",
    "uat_bsf_4con.riesgos_adm_crediticia_home_banking",
    "uat_bsf_4con.riesgos_adm_crediticia_limites_y_garantias",
    "uat_bsf_4con.riesgos_adm_crediticia_mora",
    "uat_bsf_4con.riesgos_adm_crediticia_of_calculosfinales",
    "uat_bsf_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_bsf_4con.riesgos_adm_crediticia_of_decisionfinal",
    "uat_bsf_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_bsf_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_bsf_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_bsf_4con.riesgos_adm_crediticia_of_niveldefirma",
    "uat_bsf_4con.riesgos_adm_crediticia_of_postburo",
    "uat_bsf_4con.riesgos_adm_crediticia_of_reclasificacion",
    "uat_bsf_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_bsf_4con.riesgos_adm_crediticia_of_score",
    "uat_bsf_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_bsf_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_bsf_4con.riesgos_adm_crediticia_of_topedecliente",
    "uat_bsf_4con.riesgos_adm_crediticia_of_tramites",
    "uat_bsf_4con.riesgos_adm_crediticia_of_verificaciones",
    "uat_bsf_4con.riesgos_adm_crediticia_of_vigencias",
    "uat_bsf_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_bsf_4con.riesgos_adm_crediticia_perfil_tecnico",
    "uat_bsf_4con.riesgos_adm_crediticia_prestamos",
    "uat_bsf_4con.riesgos_adm_crediticia_sucursales",
    "uat_bsf_4con.riesgos_adm_crediticia_tarjetas",
    "uat_bsf_4con.riesgos_dep_val_cheques_dim_abt_empresa",
    "uat_bsf_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_bsf_4con.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_bsf_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "uat_bsf_4con.vn_cheques",
    "uat_bsf_4con.vn_relacion_clientes",
    "uat_bsf_4con.vw_caja_ahorro_cuentas_contables",
    "uat_bsf_4con.vw_caja_ahorro_datos_basicos",
    "uat_bsf_4con.vw_caja_ahorro_embargos",
    "uat_bsf_4con.vw_caja_ahorro_movimientos",
    "uat_bsf_4con.vw_caja_ahorro_saldos",
    "uat_bsf_4con.vw_caja_ahorro_tarjetas_debito",
    "uat_bsf_4con.vw_caja_ahorro_titularidad_relacion",
    "uat_bsf_4con.vw_caja_ahorro_transacciones_habilitadas",
    "uat_bsf_4con.vw_cheques_chequeras",
    "uat_bsf_4con.vw_cheques_convenios",
    "uat_bsf_4con.vw_cuenta_corriente_acuerdos",
    "uat_bsf_4con.vw_cuenta_corriente_datos_basicos",
    "uat_bsf_4con.vw_cuenta_corriente_embargos",
    "uat_bsf_4con.vw_cuenta_corriente_garantias",
    "uat_bsf_4con.vw_cuenta_corriente_maestro_historico",
    "uat_bsf_4con.vw_cuenta_corriente_titularidad_relacion",
    "uat_bsf_4con.vw_productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_bsf_4con.vw_productos_plazo_fijo_ft_certificados",
    "uat_bsf_4con.vw_productos_prestamos_dim_maestro",
    "uat_bsf_4con.vw_riesgos_adm_crediticia_dim_lim",
    "uat_bsf_4con.vw_riesgos_adm_crediticia_dim_linea",
    "uat_bsf_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "uat_bsf_4con.vw_riesgos_adm_crediticia_dim_sublim",
    "uat_bsj_4con.can_ges_homebanking_dim_abt_empresas",
    "uat_bsj_4con.can_ges_parametria_dim_sucursal",
    "uat_bsj_4con.can_ges_parametria_dim_sucursal_cg",
    "uat_bsj_4con.can_ges_parametria_dim_sucursales",
    "uat_bsj_4con.clientes_datos_adicionales_dim_abt_empresas",
    "uat_bsj_4con.clientes_datos_identificatorios_dim",
    "uat_bsj_4con.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_bsj_4con.clientes_datos_identificatorios_rel_documentos",
    "uat_bsj_4con.clientes_datos_impositivos_dim",
    "uat_bsj_4con.clientes_datos_impositivos_dim_abt_empresas",
    "uat_bsj_4con.clientes_legajo_digital_dim_abt_empresa",
    "uat_bsj_4con.clientes_legajo_digital_dim_abt_empresas",
    "uat_bsj_4con.clientes_perfil_comercial_dim_abt_empresas",
    "uat_bsj_4con.clientes_relacion_prestamos",
    "uat_bsj_4con.clientes_relacion_valores_negociados",
    "uat_bsj_4con.contabilidad_balance_dim_abt_empresa",
    "uat_bsj_4con.contabilidad_balance_dim_abt_empresas",
    "uat_bsj_4con.contabilidad_mov_contables_dim_abt_empresa",
    "uat_bsj_4con.contabilidad_mov_contables_dim_abt_empresas",
    "uat_bsj_4con.finanzas_cot_indices_ft_cotizaciones",
    "uat_bsj_4con.inventario_acuerdos_cobros",
    "uat_bsj_4con.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "uat_bsj_4con.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "uat_bsj_4con.legales_denuncias_dim_abt_empresa",
    "uat_bsj_4con.legales_denuncias_dim_abt_empresas",
    "uat_bsj_4con.legales_mora_judicial_dim_abt_empresa",
    "uat_bsj_4con.legales_mora_judicial_dim_abt_empresas",
    "uat_bsj_4con.parametria_datos_generales_provincias_dim",
    "uat_bsj_4con.prestamos_cuotas",
    "uat_bsj_4con.prestamos_garantias",
    "uat_bsj_4con.prestamos_relacion_garantias",
    "uat_bsj_4con.productos_ca_dim_tasas_interes",
    "uat_bsj_4con.productos_caja_ahorro_dim_maestro",
    "uat_bsj_4con.productos_caja_de_ahorro_ft_maestro_historico",
    "uat_bsj_4con.productos_caja_de_ahorro_transaccion_permitida",
    "uat_bsj_4con.productos_can_ges_parametria_tasas_pasivas",
    "uat_bsj_4con.productos_cheques_dim_convenios",
    "uat_bsj_4con.productos_contabilidad_dim_comisiones",
    "uat_bsj_4con.productos_contabilidad_dim_maestro_causales",
    "uat_bsj_4con.productos_contabilidad_dim_maestro_equivalencias_contables",
    "uat_bsj_4con.productos_contabilidad_dim_maestro_plan_cuentas",
    "uat_bsj_4con.productos_contabilidad_dim_maestro_tareas_cierre",
    "uat_bsj_4con.productos_contabilidad_dim_minuta",
    "uat_bsj_4con.productos_cta_corriente_dim_embargos",
    "uat_bsj_4con.productos_cta_corriente_dim_maestro",
    "uat_bsj_4con.productos_cta_corriente_dim_maestro_acuerdos",
    "uat_bsj_4con.productos_cta_corriente_ft_maestro_historico",
    "uat_bsj_4con.productos_cta_corriente_param_dim_relacion_titularidad",
    "uat_bsj_4con.productos_dim_maestro_chequeras",
    "uat_bsj_4con.productos_garantias_dim_maestro",
    "uat_bsj_4con.productos_haberes_dim_abt_empresa",
    "uat_bsj_4con.productos_haberes_dim_abt_empresas",
    "uat_bsj_4con.productos_paquetes_dim_abt_empresa",
    "uat_bsj_4con.productos_paquetes_dim_abt_empresas",
    "uat_bsj_4con.productos_parametria_dim_acordante",
    "uat_bsj_4con.productos_parametria_dim_estado_cuenta",
    "uat_bsj_4con.productos_parametria_dim_lim",
    "uat_bsj_4con.productos_parametria_dim_moneda",
    "uat_bsj_4con.productos_parametria_dim_motivos_cierres",
    "uat_bsj_4con.productos_parametria_dim_nivel",
    "uat_bsj_4con.productos_parametria_dim_operativa_contable",
    "uat_bsj_4con.productos_parametria_dim_paquetes",
    "uat_bsj_4con.productos_parametria_dim_relacion_portafolio_cuentas",
    "uat_bsj_4con.productos_parametria_dim_sublim",
    "uat_bsj_4con.productos_parametria_dim_sucursal_provincia",
    "uat_bsj_4con.productos_parametria_dim_sucursales_provincia",
    "uat_bsj_4con.productos_parametria_dim_tipo_embargos",
    "uat_bsj_4con.productos_parametria_ft_calendario_saldo",
    "uat_bsj_4con.productos_parametrias_dim_concepto",
    "uat_bsj_4con.productos_pf_dim_abt_empresa",
    "uat_bsj_4con.productos_pf_dim_abt_empresas",
    "uat_bsj_4con.productos_pf_ft_certificados",
    "uat_bsj_4con.productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_bsj_4con.productos_plazo_fijo_ft_certificados",
    "uat_bsj_4con.productos_prestamos_dim_abt_empresa",
    "uat_bsj_4con.productos_prestamos_dim_abt_empresas",
    "uat_bsj_4con.productos_prestamos_dim_maestro",
    "uat_bsj_4con.productos_prestamos_ft_movimientos_historico",
    "uat_bsj_4con.productos_seguros_dim_maestro",
    "uat_bsj_4con.productos_ttcc_dim_abt_empresa",
    "uat_bsj_4con.productos_ttcc_dim_abt_empresas",
    "uat_bsj_4con.productos_ttdd_dim_maestro",
    "uat_bsj_4con.productos_valores_negociables_cheques",
    "uat_bsj_4con.productos_valores_negociables_dim_maestro",
    "uat_bsj_4con.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_bsj_4con.riesgos_adm_crediticia_balance",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_afip",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_bsj_4con.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_bsj_4con.riesgos_adm_crediticia_datos_adicionales",
    "uat_bsj_4con.riesgos_adm_crediticia_datos_impositivos",
    "uat_bsj_4con.riesgos_adm_crediticia_datos_personales",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_abt_empresas",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_lim",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_linea",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_plafond",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_sublim",
    "uat_bsj_4con.riesgos_adm_crediticia_dim_workflow",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_score",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_bsj_4con.riesgos_adm_crediticia_eva_script",
    "uat_bsj_4con.riesgos_adm_crediticia_home_banking",
    "uat_bsj_4con.riesgos_adm_crediticia_limites_y_garantias",
    "uat_bsj_4con.riesgos_adm_crediticia_mora",
    "uat_bsj_4con.riesgos_adm_crediticia_of_calculosfinales",
    "uat_bsj_4con.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_bsj_4con.riesgos_adm_crediticia_of_decisionfinal",
    "uat_bsj_4con.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_bsj_4con.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_bsj_4con.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_bsj_4con.riesgos_adm_crediticia_of_niveldefirma",
    "uat_bsj_4con.riesgos_adm_crediticia_of_postburo",
    "uat_bsj_4con.riesgos_adm_crediticia_of_reclasificacion",
    "uat_bsj_4con.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_bsj_4con.riesgos_adm_crediticia_of_score",
    "uat_bsj_4con.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_bsj_4con.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_bsj_4con.riesgos_adm_crediticia_of_topedecliente",
    "uat_bsj_4con.riesgos_adm_crediticia_of_tramites",
    "uat_bsj_4con.riesgos_adm_crediticia_of_verificaciones",
    "uat_bsj_4con.riesgos_adm_crediticia_of_vigencias",
    "uat_bsj_4con.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_bsj_4con.riesgos_adm_crediticia_perfil_tecnico",
    "uat_bsj_4con.riesgos_adm_crediticia_prestamos",
    "uat_bsj_4con.riesgos_adm_crediticia_sucursales",
    "uat_bsj_4con.riesgos_adm_crediticia_tarjetas",
    "uat_bsj_4con.riesgos_dep_val_cheques_dim_abt_empresa",
    "uat_bsj_4con.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_bsj_4con.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_bsj_4con.riesgos_perfil_crediticio_dim_abt_empresas",
    "uat_bsj_4con.vn_cheques",
    "uat_bsj_4con.vn_relacion_clientes",
    "uat_bsj_4con.vw_caja_ahorro_cuentas_contables",
    "uat_bsj_4con.vw_caja_ahorro_cuentas_contables_comisiones",
    "uat_bsj_4con.vw_caja_ahorro_datos_basicos",
    "uat_bsj_4con.vw_caja_ahorro_embargos",
    "uat_bsj_4con.vw_caja_ahorro_movimientos",
    "uat_bsj_4con.vw_caja_ahorro_saldos",
    "uat_bsj_4con.vw_caja_ahorro_tarjetas_debito",
    "uat_bsj_4con.vw_caja_ahorro_titularidad_relacion",
    "uat_bsj_4con.vw_caja_ahorro_transacciones_habilitadas",
    "uat_bsj_4con.vw_cheques_chequeras",
    "uat_bsj_4con.vw_cheques_convenios",
    "uat_bsj_4con.vw_cuenta_corriente_acuerdos",
    "uat_bsj_4con.vw_cuenta_corriente_cuenta_portafolio",
    "uat_bsj_4con.vw_cuenta_corriente_datos_basicos",
    "uat_bsj_4con.vw_cuenta_corriente_embargos",
    "uat_bsj_4con.vw_cuenta_corriente_garantias",
    "uat_bsj_4con.vw_cuenta_corriente_maestro_historico",
    "uat_bsj_4con.vw_cuenta_corriente_titularidad_relacion",
    "uat_bsj_4con.vw_productos_plazo_fijo_dim_maestro_cuentas_inversoras",
    "uat_bsj_4con.vw_productos_plazo_fijo_ft_certificados",
    "uat_bsj_4con.vw_productos_prestamos_dim_maestro",
    "uat_bsj_4con.vw_riesgos_adm_crediticia_dim_lim",
    "uat_bsj_4con.vw_riesgos_adm_crediticia_dim_plafon",
    "uat_bsj_4con.vw_riesgos_adm_crediticia_dim_sublim"
  ],
  "DATAMART": [
    "de_ber_datamart_campaigns.adobe_calificacion_empresa",
    "de_ber_datamart_campaigns.adobe_calificacion_individuos",
    "de_ber_datamart_campaigns.adobe_catalogo_productos",
    "de_ber_datamart_campaigns.adobe_contactabilidad",
    "de_ber_datamart_campaigns.adobe_engage_campanias",
    "de_ber_datamart_campaigns.adobe_engage_listado_carteras",
    "de_ber_datamart_campaigns.adobe_engage_respuesta",
    "de_ber_datamart_campaigns.adobe_feedback_card_hm_ms_sms",
    "de_ber_datamart_campaigns.adobe_ft_haberes_convenios",
    "de_ber_datamart_campaigns.adobe_ft_productos_ca_cc",
    "de_ber_datamart_campaigns.adobe_ft_resp_camp_atm_hbmb",
    "de_ber_datamart_campaigns.adobe_ft_seguros_qualia",
    "de_ber_datamart_campaigns.adobe_ft_tarjetas_credito_maestro",
    "de_ber_datamart_campaigns.adobe_meta4_empleados",
    "de_ber_datamart_campaigns.adobe_mora_mail",
    "de_ber_datamart_campaigns.adobe_mora_sms",
    "de_ber_datamart_campaigns.adobe_productos_caja_ahorro",
    "de_ber_datamart_campaigns.adobe_productos_cuenta_corriente",
    "de_ber_datamart_campaigns.adobe_productos_paquetes",
    "de_ber_datamart_campaigns.adobe_productos_prestamos_ft",
    "de_ber_datamart_campaigns.adobe_productos_qualia",
    "de_ber_datamart_campaigns.adobe_productos_tarjetas_credito",
    "de_ber_datamart_campaigns.adobe_productos_tracking",
    "de_ber_datamart_campaigns.adobe_productos_ttcc_ft_mov_cred",
    "de_ber_datamart_campaigns.adobe_productos_ttcc_ft_mov_prisma",
    "de_ber_datamart_campaigns.adobe_productos_ttdd_dim",
    "de_ber_datamart_campaigns.adobe_sucursales",
    "de_ber_datamart_campaigns.adobe_valores_negociados",
    "de_ber_datamart_comercial.can_ges_campanias_ft_easy_call",
    "de_ber_datamart_comercial.can_ges_campanias_ft_engage",
    "de_ber_datamart_comercial.cart_min_cartera_clientes",
    "de_ber_datamart_comercial.cart_min_carterizacion_minorista",
    "de_ber_datamart_comercial.cart_minorista_abt_suc_operativa",
    "de_ber_datamart_comercial.cart_minorista_suc_operativa",
    "de_ber_datamart_comercial.carterizacion_bmay_error",
    "de_ber_datamart_comercial.carterizacion_empresas",
    "de_ber_datamart_comercial.clientes_consolidado_hist",
    "de_ber_datamart_comercial.clientes_consolidado_snap",
    "de_ber_datamart_comercial.cotizacion_dolar",
    "de_ber_datamart_comercial.dim_clientes",
    "de_ber_datamart_comercial.dim_moneda",
    "de_ber_datamart_comercial.dim_monedas",
    "de_ber_datamart_comercial.dim_oficiales",
    "de_ber_datamart_comercial.dim_productos",
    "de_ber_datamart_comercial.dim_segmentacion_clientes",
    "de_ber_datamart_comercial.dim_segmentacion_clientes_detalle",
    "de_ber_datamart_comercial.dim_segmentacion_gpn",
    "de_ber_datamart_comercial.dim_sucursales",
    "de_ber_datamart_comercial.ft_base_precalificados_mercado_abierto",
    "de_ber_datamart_comercial.ft_cajas_de_ahorro",
    "de_ber_datamart_comercial.ft_calificaciones",
    "de_ber_datamart_comercial.ft_cheques",
    "de_ber_datamart_comercial.ft_cuentas_corrientes",
    "de_ber_datamart_comercial.ft_cuentas_mov",
    "de_ber_datamart_comercial.ft_engage",
    "de_ber_datamart_comercial.ft_estados_productos_hist",
    "de_ber_datamart_comercial.ft_feedback_engage",
    "de_ber_datamart_comercial.ft_haberes_capitas",
    "de_ber_datamart_comercial.ft_homebanking_link_extractprima_ind",
    "de_ber_datamart_comercial.ft_homebanking_link_transacciones",
    "de_ber_datamart_comercial.ft_metas_grupales",
    "de_ber_datamart_comercial.ft_metas_individuales",
    "de_ber_datamart_comercial.ft_nps",
    "de_ber_datamart_comercial.ft_paquetes",
    "de_ber_datamart_comercial.ft_plazo_fijo",
    "de_ber_datamart_comercial.ft_prestamos",
    "de_ber_datamart_comercial.ft_productos_x_mes",
    "de_ber_datamart_comercial.ft_seguros",
    "de_ber_datamart_comercial.ft_tarjeta_de_credito",
    "de_ber_datamart_comercial.ft_tarjeta_de_credito_mov",
    "de_ber_datamart_comercial.ft_turnos_engage",
    "de_ber_datamart_comercial.ft_uptime_atm",
    "de_ber_datamart_comercial.ft_ventas",
    "de_ber_datamart_comercial.producto_estado_actual",
    "de_ber_datamart_comercial.rel_carterizacion",
    "de_ber_datamart_comercial.segmentacion_abt_clientes",
    "de_ber_datamart_comercial.segmentacion_parametria_modelo_atencion",
    "de_ber_datamart_comercial.segmentacion_parametria_reglas",
    "de_ber_datamart_comercial.segmentacion_parametros_rangos",
    "de_ber_datamart_control_gestion.can_ges_parametria_dim_sucursales",
    "de_ber_datamart_control_gestion.clientes_datos_identificatorios_dim",
    "de_ber_datamart_control_gestion.clientes_relacion_prestamos",
    "de_ber_datamart_control_gestion.clientes_relacion_valores_negociados",
    "de_ber_datamart_control_gestion.comision_cajas_seguridad",
    "de_ber_datamart_control_gestion.cuentas_relacionadas",
    "de_ber_datamart_control_gestion.datos_basicos",
    "de_ber_datamart_control_gestion.datos_basicos_caja_seguridad",
    "de_ber_datamart_control_gestion.dim_cheques_depositos",
    "de_ber_datamart_control_gestion.haberes_acreditaciones",
    "de_ber_datamart_control_gestion.limites_dim_limites",
    "de_ber_datamart_control_gestion.limites_dim_plafon",
    "de_ber_datamart_control_gestion.limites_dim_sublimites",
    "de_ber_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "de_ber_datamart_control_gestion.prestamos_cuotas",
    "de_ber_datamart_control_gestion.prestamos_garantias",
    "de_ber_datamart_control_gestion.prestamos_relacion_garantias",
    "de_ber_datamart_control_gestion.productos_cheques_convenios",
    "de_ber_datamart_control_gestion.productos_cheques_librados",
    "de_ber_datamart_control_gestion.productos_cheques_negociados",
    "de_ber_datamart_control_gestion.productos_cta_corriente_dim_maestro",
    "de_ber_datamart_control_gestion.productos_haberes_datos_basicos",
    "de_ber_datamart_control_gestion.productos_lineas_especiales_dim",
    "de_ber_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "de_ber_datamart_control_gestion.productos_paquetes_comisiones",
    "de_ber_datamart_control_gestion.productos_paquetes_datos_basicos",
    "de_ber_datamart_control_gestion.productos_paquetes_productos",
    "de_ber_datamart_control_gestion.productos_parametria_dim_acordante",
    "de_ber_datamart_control_gestion.productos_parametria_dim_atrib_cont_bcra",
    "de_ber_datamart_control_gestion.productos_parametria_dim_codigos_tasa",
    "de_ber_datamart_control_gestion.productos_parametria_dim_destino_econom",
    "de_ber_datamart_control_gestion.productos_parametria_dim_estado_ppmap",
    "de_ber_datamart_control_gestion.productos_parametria_dim_moneda",
    "de_ber_datamart_control_gestion.productos_parametria_dim_origen_fondos",
    "de_ber_datamart_control_gestion.productos_parametria_dim_periodocpa",
    "de_ber_datamart_control_gestion.productos_parametria_dim_productos",
    "de_ber_datamart_control_gestion.productos_parametria_dim_relacion_titularidad",
    "de_ber_datamart_control_gestion.productos_parametria_dim_sist_amort",
    "de_ber_datamart_control_gestion.productos_parametria_dim_tipo_tasa",
    "de_ber_datamart_control_gestion.productos_prestamos_dim_cuotas_generadas",
    "de_ber_datamart_control_gestion.productos_prestamos_dim_maestro",
    "de_ber_datamart_control_gestion.productos_prestamos_rel_prefinanciados_productos",
    "de_ber_datamart_control_gestion.productos_seguros_dim_maestro",
    "de_ber_datamart_control_gestion.productos_seguros_gestion_cobros",
    "de_ber_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "de_ber_datamart_control_gestion.productos_td_stock_y_movimientos",
    "de_ber_datamart_control_gestion.productos_valores_negociables_cheques",
    "de_ber_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "de_ber_datamart_control_gestion.productos_valores_negociables_ft_movimientos",
    "de_ber_datamart_control_gestion.seguimiento_td",
    "de_ber_datamart_control_gestion.vw_clientes_relacion_prestamos",
    "de_ber_datamart_control_gestion.vw_productos_prestamos_dim_maestros",
    "de_ber_datamart_control_gestion.vw_productos_prestamos_ft_movimientos_historico",
    "de_ber_datamart_control_gestion.vw_productos_valores_negociables_ft_movimientos",
    "de_ber_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "de_ber_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "de_ber_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "de_ber_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "de_ber_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "de_ber_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "de_ber_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "de_ber_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "de_ber_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "de_ber_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "de_ber_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "de_ber_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "de_ber_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "de_ber_datamart_riesgos.productos_pf_dim_abt_empresas",
    "de_ber_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "de_ber_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_balance",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_mora",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "de_ber_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "de_ber_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_ber_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "de_bsc_datamart_campaigns.adobe_calificacion_empresa",
    "de_bsc_datamart_campaigns.adobe_calificacion_individuos",
    "de_bsc_datamart_campaigns.adobe_catalogo_productos",
    "de_bsc_datamart_campaigns.adobe_contactabilidad",
    "de_bsc_datamart_campaigns.adobe_engage_campanias",
    "de_bsc_datamart_campaigns.adobe_engage_listado_carteras",
    "de_bsc_datamart_campaigns.adobe_engage_respuesta",
    "de_bsc_datamart_campaigns.adobe_feedback_card_hm_ms_sms",
    "de_bsc_datamart_campaigns.adobe_ft_haberes_convenios",
    "de_bsc_datamart_campaigns.adobe_ft_productos_ca_cc",
    "de_bsc_datamart_campaigns.adobe_ft_resp_camp_atm_hbmb",
    "de_bsc_datamart_campaigns.adobe_ft_seguros_qualia",
    "de_bsc_datamart_campaigns.adobe_ft_tarjetas_credito_maestro",
    "de_bsc_datamart_campaigns.adobe_meta4_empleados",
    "de_bsc_datamart_campaigns.adobe_mora_mail",
    "de_bsc_datamart_campaigns.adobe_mora_sms",
    "de_bsc_datamart_campaigns.adobe_productos_caja_ahorro",
    "de_bsc_datamart_campaigns.adobe_productos_cuenta_corriente",
    "de_bsc_datamart_campaigns.adobe_productos_paquetes",
    "de_bsc_datamart_campaigns.adobe_productos_prestamos_ft",
    "de_bsc_datamart_campaigns.adobe_productos_qualia",
    "de_bsc_datamart_campaigns.adobe_productos_tarjetas_credito",
    "de_bsc_datamart_campaigns.adobe_productos_tracking",
    "de_bsc_datamart_campaigns.adobe_productos_ttcc_ft_mov_cred",
    "de_bsc_datamart_campaigns.adobe_productos_ttcc_ft_mov_prisma",
    "de_bsc_datamart_campaigns.adobe_productos_ttdd_dim",
    "de_bsc_datamart_campaigns.adobe_sucursales",
    "de_bsc_datamart_campaigns.adobe_valores_negociados",
    "de_bsc_datamart_comercial.adobe_calificacion_individuos",
    "de_bsc_datamart_comercial.can_ges_campanias_ft_easy_call",
    "de_bsc_datamart_comercial.can_ges_campanias_ft_engage",
    "de_bsc_datamart_comercial.cart_min_cartera_clientes",
    "de_bsc_datamart_comercial.cart_min_carterizacion_minorista",
    "de_bsc_datamart_comercial.cart_minorista_abt_suc_operativa",
    "de_bsc_datamart_comercial.cart_minorista_suc_operativa",
    "de_bsc_datamart_comercial.carterizacion_bmay_error",
    "de_bsc_datamart_comercial.carterizacion_empresas",
    "de_bsc_datamart_comercial.clientes_consolidado_hist",
    "de_bsc_datamart_comercial.clientes_consolidado_snap",
    "de_bsc_datamart_comercial.cotizacion_dolar",
    "de_bsc_datamart_comercial.dim_clientes",
    "de_bsc_datamart_comercial.dim_moneda",
    "de_bsc_datamart_comercial.dim_monedas",
    "de_bsc_datamart_comercial.dim_oficiales",
    "de_bsc_datamart_comercial.dim_productos",
    "de_bsc_datamart_comercial.dim_segmentacion_clientes",
    "de_bsc_datamart_comercial.dim_segmentacion_clientes_detalle",
    "de_bsc_datamart_comercial.dim_segmentacion_gpn",
    "de_bsc_datamart_comercial.dim_sucursales",
    "de_bsc_datamart_comercial.ft_base_precalificados_mercado_abierto",
    "de_bsc_datamart_comercial.ft_cajas_de_ahorro",
    "de_bsc_datamart_comercial.ft_calificaciones",
    "de_bsc_datamart_comercial.ft_cheques",
    "de_bsc_datamart_comercial.ft_cuentas_corrientes",
    "de_bsc_datamart_comercial.ft_cuentas_mov",
    "de_bsc_datamart_comercial.ft_engage",
    "de_bsc_datamart_comercial.ft_estados_productos_hist",
    "de_bsc_datamart_comercial.ft_feedback_engage",
    "de_bsc_datamart_comercial.ft_haberes_capitas",
    "de_bsc_datamart_comercial.ft_homebanking_link_extractprima_ind",
    "de_bsc_datamart_comercial.ft_homebanking_link_transacciones",
    "de_bsc_datamart_comercial.ft_metas_grupales",
    "de_bsc_datamart_comercial.ft_metas_individuales",
    "de_bsc_datamart_comercial.ft_nps",
    "de_bsc_datamart_comercial.ft_paquetes",
    "de_bsc_datamart_comercial.ft_plazo_fijo",
    "de_bsc_datamart_comercial.ft_prestamos",
    "de_bsc_datamart_comercial.ft_seguros",
    "de_bsc_datamart_comercial.ft_stock_caja_ahorro",
    "de_bsc_datamart_comercial.ft_stock_cheques",
    "de_bsc_datamart_comercial.ft_stock_cuentas_corrientes",
    "de_bsc_datamart_comercial.ft_stock_haberes",
    "de_bsc_datamart_comercial.ft_stock_paquetes",
    "de_bsc_datamart_comercial.ft_stock_plazo_fijo",
    "de_bsc_datamart_comercial.ft_stock_prestamos",
    "de_bsc_datamart_comercial.ft_stock_seguros",
    "de_bsc_datamart_comercial.ft_stock_tarjeta_credito",
    "de_bsc_datamart_comercial.ft_tarjeta_de_credito",
    "de_bsc_datamart_comercial.ft_tarjeta_de_credito_mov",
    "de_bsc_datamart_comercial.ft_turnos_engage",
    "de_bsc_datamart_comercial.ft_uptime_atm",
    "de_bsc_datamart_comercial.ft_ventas",
    "de_bsc_datamart_comercial.producto_estado_actual",
    "de_bsc_datamart_comercial.rel_carterizacion",
    "de_bsc_datamart_comercial.segmentacion_abt_clientes",
    "de_bsc_datamart_comercial.segmentacion_parametria_reglas",
    "de_bsc_datamart_control_gestion.can_ges_parametria_dim_sucursales",
    "de_bsc_datamart_control_gestion.clientes_datos_identificatorios_dim",
    "de_bsc_datamart_control_gestion.clientes_relacion_prestamos",
    "de_bsc_datamart_control_gestion.clientes_relacion_valores_negociados",
    "de_bsc_datamart_control_gestion.comision_cajas_seguridad",
    "de_bsc_datamart_control_gestion.cuentas_relacionadas",
    "de_bsc_datamart_control_gestion.datos_basicos",
    "de_bsc_datamart_control_gestion.datos_basicos_caja_seguridad",
    "de_bsc_datamart_control_gestion.dim_cheques_depositos",
    "de_bsc_datamart_control_gestion.haberes_acreditaciones",
    "de_bsc_datamart_control_gestion.limites_dim_limites",
    "de_bsc_datamart_control_gestion.limites_dim_plafon",
    "de_bsc_datamart_control_gestion.limites_dim_sublimites",
    "de_bsc_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "de_bsc_datamart_control_gestion.prestamos_cuotas",
    "de_bsc_datamart_control_gestion.prestamos_cuotas_prueba",
    "de_bsc_datamart_control_gestion.prestamos_garantias",
    "de_bsc_datamart_control_gestion.prestamos_relacion_garantias",
    "de_bsc_datamart_control_gestion.productos_cheques_convenios",
    "de_bsc_datamart_control_gestion.productos_cheques_librados",
    "de_bsc_datamart_control_gestion.productos_cheques_negociados",
    "de_bsc_datamart_control_gestion.productos_cta_corriente_dim_maestro",
    "de_bsc_datamart_control_gestion.productos_haberes_datos_basicos",
    "de_bsc_datamart_control_gestion.productos_lineas_especiales_dim",
    "de_bsc_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "de_bsc_datamart_control_gestion.productos_paquetes_comisiones",
    "de_bsc_datamart_control_gestion.productos_paquetes_datos_basicos",
    "de_bsc_datamart_control_gestion.productos_paquetes_productos",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_acordante",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_atrib_cont_bcra",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_codigos_tasa",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_destino_econom",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_estado_ppmap",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_moneda",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_origen_fondos",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_periodocpa",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_productos",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_relacion_titularidad",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_sist_amort",
    "de_bsc_datamart_control_gestion.productos_parametria_dim_tipo_tasa",
    "de_bsc_datamart_control_gestion.productos_prestamos_dim_cuotas_generadas",
    "de_bsc_datamart_control_gestion.productos_prestamos_dim_maestro",
    "de_bsc_datamart_control_gestion.productos_prestamos_rel_prefinanciados_productos",
    "de_bsc_datamart_control_gestion.productos_seguros_dim_maestro",
    "de_bsc_datamart_control_gestion.productos_seguros_gestion_cobros",
    "de_bsc_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "de_bsc_datamart_control_gestion.productos_td_stock_y_movimientos",
    "de_bsc_datamart_control_gestion.productos_valores_negociables_cheques",
    "de_bsc_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "de_bsc_datamart_control_gestion.productos_valores_negociables_ft_movimientos",
    "de_bsc_datamart_control_gestion.seguimiento_td",
    "de_bsc_datamart_control_gestion.vw_clientes_relacion_prestamos",
    "de_bsc_datamart_control_gestion.vw_productos_prestamos_dim_maestro",
    "de_bsc_datamart_control_gestion.vw_productos_valores_negociables_ft_movimientos",
    "de_bsc_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "de_bsc_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "de_bsc_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "de_bsc_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "de_bsc_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "de_bsc_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "de_bsc_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "de_bsc_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "de_bsc_datamart_riesgos.eva_clasificacionempresayrelacionado",
    "de_bsc_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "de_bsc_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "de_bsc_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "de_bsc_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "de_bsc_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "de_bsc_datamart_riesgos.productos_pf_dim_abt_empresas",
    "de_bsc_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "de_bsc_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_balance",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_mora",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "de_bsc_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "de_bsc_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_bsc_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "de_bsf_datamart_campaigns.adobe_calificacion_empresa",
    "de_bsf_datamart_campaigns.adobe_calificacion_individuos",
    "de_bsf_datamart_campaigns.adobe_catalogo_productos",
    "de_bsf_datamart_campaigns.adobe_contactabilidad",
    "de_bsf_datamart_campaigns.adobe_engage_campanias",
    "de_bsf_datamart_campaigns.adobe_engage_listado_carteras",
    "de_bsf_datamart_campaigns.adobe_engage_respuesta",
    "de_bsf_datamart_campaigns.adobe_feedback_card_hm_ms_sms",
    "de_bsf_datamart_campaigns.adobe_ft_haberes_convenios",
    "de_bsf_datamart_campaigns.adobe_ft_productos_ca_cc",
    "de_bsf_datamart_campaigns.adobe_ft_resp_camp_atm_hbmb",
    "de_bsf_datamart_campaigns.adobe_ft_seguros_qualia",
    "de_bsf_datamart_campaigns.adobe_ft_tarjetas_credito_maestro",
    "de_bsf_datamart_campaigns.adobe_meta4_empleados",
    "de_bsf_datamart_campaigns.adobe_mora_mail",
    "de_bsf_datamart_campaigns.adobe_mora_sms",
    "de_bsf_datamart_campaigns.adobe_productos_caja_ahorro",
    "de_bsf_datamart_campaigns.adobe_productos_cuenta_corriente",
    "de_bsf_datamart_campaigns.adobe_productos_paquetes",
    "de_bsf_datamart_campaigns.adobe_productos_prestamos_ft",
    "de_bsf_datamart_campaigns.adobe_productos_qualia",
    "de_bsf_datamart_campaigns.adobe_productos_tarjetas_credito",
    "de_bsf_datamart_campaigns.adobe_productos_tracking",
    "de_bsf_datamart_campaigns.adobe_productos_ttcc_ft_mov_cred",
    "de_bsf_datamart_campaigns.adobe_productos_ttcc_ft_mov_prisma",
    "de_bsf_datamart_campaigns.adobe_productos_ttdd_dim",
    "de_bsf_datamart_campaigns.adobe_sucursales",
    "de_bsf_datamart_campaigns.adobe_valores_negociados",
    "de_bsf_datamart_comercial.can_ges_campanias_ft_easy_call",
    "de_bsf_datamart_comercial.can_ges_campanias_ft_engage",
    "de_bsf_datamart_comercial.cart_min_cartera_clientes",
    "de_bsf_datamart_comercial.cart_min_carterizacion_minorista",
    "de_bsf_datamart_comercial.cart_minorista_abt_suc_operativa",
    "de_bsf_datamart_comercial.cart_minorista_suc_operativa",
    "de_bsf_datamart_comercial.carterizacion_bmay_error",
    "de_bsf_datamart_comercial.carterizacion_empresas",
    "de_bsf_datamart_comercial.clientes_consolidado_hist",
    "de_bsf_datamart_comercial.clientes_consolidado_snap",
    "de_bsf_datamart_comercial.cotizacion_dolar",
    "de_bsf_datamart_comercial.dim_clientes",
    "de_bsf_datamart_comercial.dim_moneda",
    "de_bsf_datamart_comercial.dim_oficiales",
    "de_bsf_datamart_comercial.dim_productos",
    "de_bsf_datamart_comercial.dim_segmentacion_clientes",
    "de_bsf_datamart_comercial.dim_segmentacion_clientes_detalle",
    "de_bsf_datamart_comercial.dim_segmentacion_gpn",
    "de_bsf_datamart_comercial.dim_sucursales",
    "de_bsf_datamart_comercial.ft_base_precalificados_mercado_abierto",
    "de_bsf_datamart_comercial.ft_cajas_de_ahorro",
    "de_bsf_datamart_comercial.ft_calificaciones",
    "de_bsf_datamart_comercial.ft_cheques",
    "de_bsf_datamart_comercial.ft_cuentas_corrientes",
    "de_bsf_datamart_comercial.ft_cuentas_mov",
    "de_bsf_datamart_comercial.ft_engage",
    "de_bsf_datamart_comercial.ft_estados_productos_hist",
    "de_bsf_datamart_comercial.ft_feedback_engage",
    "de_bsf_datamart_comercial.ft_haberes_capitas",
    "de_bsf_datamart_comercial.ft_homebanking_link_extractprima_ind",
    "de_bsf_datamart_comercial.ft_homebanking_link_transacciones",
    "de_bsf_datamart_comercial.ft_metas_grupales",
    "de_bsf_datamart_comercial.ft_metas_individuales",
    "de_bsf_datamart_comercial.ft_nps",
    "de_bsf_datamart_comercial.ft_paquetes",
    "de_bsf_datamart_comercial.ft_plazo_fijo",
    "de_bsf_datamart_comercial.ft_prestamos",
    "de_bsf_datamart_comercial.ft_seguros",
    "de_bsf_datamart_comercial.ft_tarjeta_de_credito",
    "de_bsf_datamart_comercial.ft_tarjeta_de_credito_mov",
    "de_bsf_datamart_comercial.ft_turnos_engage",
    "de_bsf_datamart_comercial.ft_uptime_atm",
    "de_bsf_datamart_comercial.ft_ventas",
    "de_bsf_datamart_comercial.producto_estado_actual",
    "de_bsf_datamart_comercial.productos_adquirencia_ft_liquidaciones_comercios",
    "de_bsf_datamart_comercial.rel_carterizacion",
    "de_bsf_datamart_comercial.segmentacion_abt_clientes",
    "de_bsf_datamart_comercial.segmentacion_parametria_reglas",
    "de_bsf_datamart_control_gestion.clientes_relacion_prestamos",
    "de_bsf_datamart_control_gestion.clientes_relacion_valores_negociados",
    "de_bsf_datamart_control_gestion.comision_cajas_seguridad",
    "de_bsf_datamart_control_gestion.cuentas_relacionadas",
    "de_bsf_datamart_control_gestion.datos_basicos",
    "de_bsf_datamart_control_gestion.datos_basicos_caja_seguridad",
    "de_bsf_datamart_control_gestion.dim_cheques_custodia",
    "de_bsf_datamart_control_gestion.dim_cheques_depositos",
    "de_bsf_datamart_control_gestion.haberes_acreditaciones",
    "de_bsf_datamart_control_gestion.limites_dim_limites",
    "de_bsf_datamart_control_gestion.limites_dim_lineas",
    "de_bsf_datamart_control_gestion.limites_dim_plafon",
    "de_bsf_datamart_control_gestion.limites_dim_sublimites",
    "de_bsf_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "de_bsf_datamart_control_gestion.prestamos_cuotas",
    "de_bsf_datamart_control_gestion.prestamos_garantias",
    "de_bsf_datamart_control_gestion.prestamos_relacion_garantias",
    "de_bsf_datamart_control_gestion.productos_cheques_convenios",
    "de_bsf_datamart_control_gestion.productos_cheques_librados",
    "de_bsf_datamart_control_gestion.productos_cheques_negociados",
    "de_bsf_datamart_control_gestion.productos_haberes_datos_basicos",
    "de_bsf_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "de_bsf_datamart_control_gestion.productos_paquetes_comisiones",
    "de_bsf_datamart_control_gestion.productos_paquetes_datos_basicos",
    "de_bsf_datamart_control_gestion.productos_paquetes_productos",
    "de_bsf_datamart_control_gestion.productos_parametria_dim_relacion_titularidad",
    "de_bsf_datamart_control_gestion.productos_prestamos_dim_maestro",
    "de_bsf_datamart_control_gestion.productos_seguros_dim_maestro",
    "de_bsf_datamart_control_gestion.productos_seguros_gestion_cobros",
    "de_bsf_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "de_bsf_datamart_control_gestion.productos_td_stock_y_movimientos",
    "de_bsf_datamart_control_gestion.productos_valores_negociables_cheques",
    "de_bsf_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "de_bsf_datamart_control_gestion.productos_valores_negociables_dim_maestro_prueba",
    "de_bsf_datamart_control_gestion.seguimiento_td",
    "de_bsf_datamart_control_gestion.vw_clientes_relacion_prestamos",
    "de_bsf_datamart_control_gestion.vw_productos_prestamos_dim_maestros",
    "de_bsf_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "de_bsf_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "de_bsf_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "de_bsf_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "de_bsf_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "de_bsf_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "de_bsf_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "de_bsf_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "de_bsf_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "de_bsf_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "de_bsf_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "de_bsf_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "de_bsf_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "de_bsf_datamart_riesgos.productos_pf_dim_abt_empresas",
    "de_bsf_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "de_bsf_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_balance",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_mora",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "de_bsf_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "de_bsf_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_bsf_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "de_bsj_datamart_campaigns.adobe_calificacion_empresa",
    "de_bsj_datamart_campaigns.adobe_calificacion_individuos",
    "de_bsj_datamart_campaigns.adobe_catalogo_productos",
    "de_bsj_datamart_campaigns.adobe_contactabilidad",
    "de_bsj_datamart_campaigns.adobe_engage_campanias",
    "de_bsj_datamart_campaigns.adobe_engage_listado_carteras",
    "de_bsj_datamart_campaigns.adobe_engage_respuesta",
    "de_bsj_datamart_campaigns.adobe_feedback_card_hm_ms_sms",
    "de_bsj_datamart_campaigns.adobe_ft_haberes_convenios",
    "de_bsj_datamart_campaigns.adobe_ft_productos_ca_cc",
    "de_bsj_datamart_campaigns.adobe_ft_resp_camp_atm_hbmb",
    "de_bsj_datamart_campaigns.adobe_ft_seguros_qualia",
    "de_bsj_datamart_campaigns.adobe_ft_tarjetas_credito_maestro",
    "de_bsj_datamart_campaigns.adobe_meta4_empleados",
    "de_bsj_datamart_campaigns.adobe_mora_mail",
    "de_bsj_datamart_campaigns.adobe_mora_sms",
    "de_bsj_datamart_campaigns.adobe_productos_caja_ahorro",
    "de_bsj_datamart_campaigns.adobe_productos_cuenta_corriente",
    "de_bsj_datamart_campaigns.adobe_productos_paquetes",
    "de_bsj_datamart_campaigns.adobe_productos_prestamos_ft",
    "de_bsj_datamart_campaigns.adobe_productos_qualia",
    "de_bsj_datamart_campaigns.adobe_productos_tarjetas_credito",
    "de_bsj_datamart_campaigns.adobe_productos_tracking",
    "de_bsj_datamart_campaigns.adobe_productos_ttcc_ft_mov_cred",
    "de_bsj_datamart_campaigns.adobe_productos_ttcc_ft_mov_prisma",
    "de_bsj_datamart_campaigns.adobe_productos_ttdd_dim",
    "de_bsj_datamart_campaigns.adobe_sucursales",
    "de_bsj_datamart_campaigns.adobe_valores_negociados",
    "de_bsj_datamart_comercial.can_ges_campanias_ft_easy_call",
    "de_bsj_datamart_comercial.can_ges_campanias_ft_engage",
    "de_bsj_datamart_comercial.cart_min_cartera_clientes",
    "de_bsj_datamart_comercial.cart_min_carterizacion_minorista",
    "de_bsj_datamart_comercial.cart_minorista_abt_suc_operativa",
    "de_bsj_datamart_comercial.cart_minorista_suc_operativa",
    "de_bsj_datamart_comercial.carterizacion_bmay_error",
    "de_bsj_datamart_comercial.carterizacion_empresas",
    "de_bsj_datamart_comercial.clientes_consolidado_hist",
    "de_bsj_datamart_comercial.clientes_consolidado_snap",
    "de_bsj_datamart_comercial.cotizacion_dolar",
    "de_bsj_datamart_comercial.dim_clientes",
    "de_bsj_datamart_comercial.dim_moneda",
    "de_bsj_datamart_comercial.dim_monedas",
    "de_bsj_datamart_comercial.dim_oficiales",
    "de_bsj_datamart_comercial.dim_productos",
    "de_bsj_datamart_comercial.dim_segmentacion_clientes",
    "de_bsj_datamart_comercial.dim_segmentacion_clientes_detalle",
    "de_bsj_datamart_comercial.dim_segmentacion_gpn",
    "de_bsj_datamart_comercial.dim_sucursales",
    "de_bsj_datamart_comercial.ft_base_precalificados_mercado_abierto",
    "de_bsj_datamart_comercial.ft_cajas_de_ahorro",
    "de_bsj_datamart_comercial.ft_calificaciones",
    "de_bsj_datamart_comercial.ft_cheques",
    "de_bsj_datamart_comercial.ft_cuentas_corrientes",
    "de_bsj_datamart_comercial.ft_cuentas_mov",
    "de_bsj_datamart_comercial.ft_engage",
    "de_bsj_datamart_comercial.ft_estados_productos_hist",
    "de_bsj_datamart_comercial.ft_feedback_engage",
    "de_bsj_datamart_comercial.ft_haberes_capitas",
    "de_bsj_datamart_comercial.ft_homebanking_link_extractprima_ind",
    "de_bsj_datamart_comercial.ft_homebanking_link_transacciones",
    "de_bsj_datamart_comercial.ft_metas_grupales",
    "de_bsj_datamart_comercial.ft_metas_individuales",
    "de_bsj_datamart_comercial.ft_nps",
    "de_bsj_datamart_comercial.ft_paquetes",
    "de_bsj_datamart_comercial.ft_plazo_fijo",
    "de_bsj_datamart_comercial.ft_prestamos",
    "de_bsj_datamart_comercial.ft_seguros",
    "de_bsj_datamart_comercial.ft_stock_caja_ahorro",
    "de_bsj_datamart_comercial.ft_stock_cheques",
    "de_bsj_datamart_comercial.ft_stock_cuentas_corrientes",
    "de_bsj_datamart_comercial.ft_stock_haberes",
    "de_bsj_datamart_comercial.ft_stock_paquetes",
    "de_bsj_datamart_comercial.ft_stock_plazo_fijo",
    "de_bsj_datamart_comercial.ft_stock_prestamos",
    "de_bsj_datamart_comercial.ft_stock_seguros",
    "de_bsj_datamart_comercial.ft_tarjeta_de_credito",
    "de_bsj_datamart_comercial.ft_tarjeta_de_credito_mov",
    "de_bsj_datamart_comercial.ft_turnos_engage",
    "de_bsj_datamart_comercial.ft_uptime_atm",
    "de_bsj_datamart_comercial.ft_ventas",
    "de_bsj_datamart_comercial.producto_estado_actual",
    "de_bsj_datamart_comercial.prueba_borrar",
    "de_bsj_datamart_comercial.rel_carterizacion",
    "de_bsj_datamart_comercial.segmentacion_abt_clientes",
    "de_bsj_datamart_comercial.segmentacion_parametria_reglas",
    "de_bsj_datamart_control_gestion.can_ges_parametria_dim_sucursales",
    "de_bsj_datamart_control_gestion.clientes_datos_identificatorios_dim",
    "de_bsj_datamart_control_gestion.clientes_relacion_prestamos",
    "de_bsj_datamart_control_gestion.clientes_relacion_valores_negociados",
    "de_bsj_datamart_control_gestion.comision_cajas_seguridad",
    "de_bsj_datamart_control_gestion.cuentas_relacionadas",
    "de_bsj_datamart_control_gestion.datos_basicos",
    "de_bsj_datamart_control_gestion.datos_basicos_caja_seguridad",
    "de_bsj_datamart_control_gestion.dim_cheques_depositos",
    "de_bsj_datamart_control_gestion.haberes_acreditaciones",
    "de_bsj_datamart_control_gestion.limites_dim_limites",
    "de_bsj_datamart_control_gestion.limites_dim_plafon",
    "de_bsj_datamart_control_gestion.limites_dim_sublimites",
    "de_bsj_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "de_bsj_datamart_control_gestion.prestamos_cuotas",
    "de_bsj_datamart_control_gestion.prestamos_garantias",
    "de_bsj_datamart_control_gestion.prestamos_relacion_garantias",
    "de_bsj_datamart_control_gestion.productos_cheques_convenios",
    "de_bsj_datamart_control_gestion.productos_cheques_librados",
    "de_bsj_datamart_control_gestion.productos_cheques_negociados",
    "de_bsj_datamart_control_gestion.productos_cta_corriente_dim_maestro",
    "de_bsj_datamart_control_gestion.productos_haberes_datos_basicos",
    "de_bsj_datamart_control_gestion.productos_lineas_especiales_dim",
    "de_bsj_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "de_bsj_datamart_control_gestion.productos_paquetes_comisiones",
    "de_bsj_datamart_control_gestion.productos_paquetes_datos_basicos",
    "de_bsj_datamart_control_gestion.productos_paquetes_productos",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_acordante",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_atrib_cont_bcra",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_codigos_tasa",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_destino_econom",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_estado_ppmap",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_moneda",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_origen_fondos",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_periodocpa",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_productos",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_relacion_titularidad",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_sist_amort",
    "de_bsj_datamart_control_gestion.productos_parametria_dim_tipo_tasa",
    "de_bsj_datamart_control_gestion.productos_prestamos_dim_cuotas_generadas",
    "de_bsj_datamart_control_gestion.productos_prestamos_dim_maestro",
    "de_bsj_datamart_control_gestion.productos_prestamos_rel_prefinanciados_productos",
    "de_bsj_datamart_control_gestion.productos_seguros_dim_maestro",
    "de_bsj_datamart_control_gestion.productos_seguros_gestion_cobros",
    "de_bsj_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "de_bsj_datamart_control_gestion.productos_td_stock_y_movimientos",
    "de_bsj_datamart_control_gestion.productos_valores_negociables_cheques",
    "de_bsj_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "de_bsj_datamart_control_gestion.productos_valores_negociables_ft_movimientos",
    "de_bsj_datamart_control_gestion.seguimiento_td",
    "de_bsj_datamart_control_gestion.vw_clientes_relacion_prestamos",
    "de_bsj_datamart_control_gestion.vw_productos_prestamos_dim_maestros",
    "de_bsj_datamart_control_gestion.vw_productos_valores_negociables_ft_movimientos",
    "de_bsj_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "de_bsj_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "de_bsj_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "de_bsj_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "de_bsj_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "de_bsj_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "de_bsj_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "de_bsj_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "de_bsj_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "de_bsj_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "de_bsj_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "de_bsj_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "de_bsj_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "de_bsj_datamart_riesgos.productos_pf_dim_abt_empresas",
    "de_bsj_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "de_bsj_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_balance",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_mora",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "de_bsj_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "de_bsj_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "de_bsj_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_ber_datamart_control_gestion.clientes_relacion_prestamos",
    "uat_ber_datamart_control_gestion.clientes_relacion_valores_negociados",
    "uat_ber_datamart_control_gestion.comision_cajas_seguridad",
    "uat_ber_datamart_control_gestion.cuentas_relacionadas",
    "uat_ber_datamart_control_gestion.datos_basicos",
    "uat_ber_datamart_control_gestion.datos_basicos_caja_seguridad",
    "uat_ber_datamart_control_gestion.dim_cheques_depositos",
    "uat_ber_datamart_control_gestion.haberes_acreditaciones",
    "uat_ber_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "uat_ber_datamart_control_gestion.prestamos_cuotas",
    "uat_ber_datamart_control_gestion.prestamos_garantias",
    "uat_ber_datamart_control_gestion.prestamos_relacion_garantias",
    "uat_ber_datamart_control_gestion.productos_cheques_convenios",
    "uat_ber_datamart_control_gestion.productos_cheques_librados",
    "uat_ber_datamart_control_gestion.productos_cheques_negociados",
    "uat_ber_datamart_control_gestion.productos_haberes_datos_basicos",
    "uat_ber_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "uat_ber_datamart_control_gestion.productos_paquetes_comisiones",
    "uat_ber_datamart_control_gestion.productos_paquetes_datos_basicos",
    "uat_ber_datamart_control_gestion.productos_paquetes_productos",
    "uat_ber_datamart_control_gestion.productos_prestamos_dim_maestro",
    "uat_ber_datamart_control_gestion.productos_seguros_dim_maestro",
    "uat_ber_datamart_control_gestion.productos_seguros_gestion_cobros",
    "uat_ber_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "uat_ber_datamart_control_gestion.productos_td_stock_y_movimientos",
    "uat_ber_datamart_control_gestion.productos_valores_negociables_cheques",
    "uat_ber_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "uat_ber_datamart_control_gestion.productos_valores_negociables_ft_movimientos",
    "uat_ber_datamart_control_gestion.seguimiento_td",
    "uat_ber_datamart_control_gestion.vn_cheques",
    "uat_ber_datamart_control_gestion.vn_relacion_clientes",
    "uat_ber_datamart_control_gestion.vw_clientes_rel_vn",
    "uat_ber_datamart_control_gestion.vw_maestro_vn",
    "uat_ber_datamart_control_gestion.vw_prod_vn_cheques",
    "uat_ber_datamart_control_gestion.vw_productos_valores_negociables_ft_movimientos",
    "uat_ber_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "uat_ber_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "uat_ber_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_ber_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "uat_ber_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "uat_ber_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "uat_ber_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "uat_ber_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "uat_ber_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresas",
    "uat_ber_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "uat_ber_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "uat_ber_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "uat_ber_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "uat_ber_datamart_riesgos.productos_pf_dim_abt_empresas",
    "uat_ber_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "uat_ber_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_balance",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_mora",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "uat_ber_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "uat_ber_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_ber_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_bsc_datamart_control_gestion.clientes_relacion_prestamos",
    "uat_bsc_datamart_control_gestion.clientes_relacion_valores_negociados",
    "uat_bsc_datamart_control_gestion.comision_cajas_seguridad",
    "uat_bsc_datamart_control_gestion.cuentas_relacionadas",
    "uat_bsc_datamart_control_gestion.datos_basicos",
    "uat_bsc_datamart_control_gestion.datos_basicos_caja_seguridad",
    "uat_bsc_datamart_control_gestion.dim_cheques_depositos",
    "uat_bsc_datamart_control_gestion.haberes_acreditaciones",
    "uat_bsc_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "uat_bsc_datamart_control_gestion.prestamos_cuotas",
    "uat_bsc_datamart_control_gestion.prestamos_garantias",
    "uat_bsc_datamart_control_gestion.prestamos_relacion_garantias",
    "uat_bsc_datamart_control_gestion.productos_cheques_convenios",
    "uat_bsc_datamart_control_gestion.productos_cheques_librados",
    "uat_bsc_datamart_control_gestion.productos_cheques_negociados",
    "uat_bsc_datamart_control_gestion.productos_haberes_datos_basicos",
    "uat_bsc_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "uat_bsc_datamart_control_gestion.productos_paquetes_comisiones",
    "uat_bsc_datamart_control_gestion.productos_paquetes_datos_basicos",
    "uat_bsc_datamart_control_gestion.productos_paquetes_productos",
    "uat_bsc_datamart_control_gestion.productos_prestamos_dim_maestro",
    "uat_bsc_datamart_control_gestion.productos_seguros_dim_maestro",
    "uat_bsc_datamart_control_gestion.productos_seguros_gestion_cobros",
    "uat_bsc_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "uat_bsc_datamart_control_gestion.productos_td_stock_y_movimientos",
    "uat_bsc_datamart_control_gestion.productos_valores_negociables_cheques",
    "uat_bsc_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "uat_bsc_datamart_control_gestion.productos_valores_negociables_ft_movimientos",
    "uat_bsc_datamart_control_gestion.seguimiento_td",
    "uat_bsc_datamart_control_gestion.vn_cheques",
    "uat_bsc_datamart_control_gestion.vn_relacion_clientes",
    "uat_bsc_datamart_control_gestion.vw_clientes_rel_vn",
    "uat_bsc_datamart_control_gestion.vw_maestro_vn",
    "uat_bsc_datamart_control_gestion.vw_prod_vn_cheques",
    "uat_bsc_datamart_control_gestion.vw_productos_valores_negociables_ft_movimientos",
    "uat_bsc_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "uat_bsc_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.productos_pf_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_balance",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_mora",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "uat_bsc_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "uat_bsc_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_bsc_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_bsf_datamart_control_gestion.clientes_relacion_prestamos",
    "uat_bsf_datamart_control_gestion.clientes_relacion_valores_negociados",
    "uat_bsf_datamart_control_gestion.comision_cajas_seguridad",
    "uat_bsf_datamart_control_gestion.cuentas_relacionadas",
    "uat_bsf_datamart_control_gestion.datos_basicos",
    "uat_bsf_datamart_control_gestion.datos_basicos_caja_seguridad",
    "uat_bsf_datamart_control_gestion.dim_cheques_custodia",
    "uat_bsf_datamart_control_gestion.dim_cheques_depositos",
    "uat_bsf_datamart_control_gestion.haberes_acreditaciones",
    "uat_bsf_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "uat_bsf_datamart_control_gestion.prestamos_cuotas",
    "uat_bsf_datamart_control_gestion.prestamos_garantias",
    "uat_bsf_datamart_control_gestion.prestamos_relacion_garantias",
    "uat_bsf_datamart_control_gestion.productos_cheques_convenios",
    "uat_bsf_datamart_control_gestion.productos_cheques_librados",
    "uat_bsf_datamart_control_gestion.productos_cheques_negociados",
    "uat_bsf_datamart_control_gestion.productos_haberes_datos_basicos",
    "uat_bsf_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "uat_bsf_datamart_control_gestion.productos_paquetes_comisiones",
    "uat_bsf_datamart_control_gestion.productos_paquetes_datos_basicos",
    "uat_bsf_datamart_control_gestion.productos_paquetes_productos",
    "uat_bsf_datamart_control_gestion.productos_prestamos_dim_maestro",
    "uat_bsf_datamart_control_gestion.productos_seguros_dim_maestro",
    "uat_bsf_datamart_control_gestion.productos_seguros_gestion_cobros",
    "uat_bsf_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "uat_bsf_datamart_control_gestion.productos_td_stock_y_movimientos",
    "uat_bsf_datamart_control_gestion.productos_valores_negociables_cheques",
    "uat_bsf_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "uat_bsf_datamart_control_gestion.seguimiento_td",
    "uat_bsf_datamart_control_gestion.vw_clientes_rel_vn",
    "uat_bsf_datamart_control_gestion.vw_maestro_vn",
    "uat_bsf_datamart_control_gestion.vw_prod_vn_cheques",
    "uat_bsf_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "uat_bsf_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.productos_pf_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_balance",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_mora",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "uat_bsf_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "uat_bsf_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_bsf_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa",
    "uat_bsj_datamart_control_gestion.clientes_relacion_prestamos",
    "uat_bsj_datamart_control_gestion.clientes_relacion_valores_negociados",
    "uat_bsj_datamart_control_gestion.comision_cajas_seguridad",
    "uat_bsj_datamart_control_gestion.cuentas_relacionadas",
    "uat_bsj_datamart_control_gestion.datos_basicos",
    "uat_bsj_datamart_control_gestion.datos_basicos_caja_seguridad",
    "uat_bsj_datamart_control_gestion.dim_cheques_depositos",
    "uat_bsj_datamart_control_gestion.haberes_acreditaciones",
    "uat_bsj_datamart_control_gestion.prestamos_cobranzas_movimientos",
    "uat_bsj_datamart_control_gestion.prestamos_cuotas",
    "uat_bsj_datamart_control_gestion.prestamos_garantias",
    "uat_bsj_datamart_control_gestion.prestamos_relacion_garantias",
    "uat_bsj_datamart_control_gestion.productos_cheques_convenios",
    "uat_bsj_datamart_control_gestion.productos_cheques_librados",
    "uat_bsj_datamart_control_gestion.productos_cheques_negociados",
    "uat_bsj_datamart_control_gestion.productos_haberes_datos_basicos",
    "uat_bsj_datamart_control_gestion.productos_monedaextranjera_dim_compraventa",
    "uat_bsj_datamart_control_gestion.productos_paquetes_comisiones",
    "uat_bsj_datamart_control_gestion.productos_paquetes_datos_basicos",
    "uat_bsj_datamart_control_gestion.productos_paquetes_productos",
    "uat_bsj_datamart_control_gestion.productos_prestamos_dim_maestro",
    "uat_bsj_datamart_control_gestion.productos_seguros_dim_maestro",
    "uat_bsj_datamart_control_gestion.productos_seguros_gestion_cobros",
    "uat_bsj_datamart_control_gestion.productos_seguros_solicitud_baja_poliza",
    "uat_bsj_datamart_control_gestion.productos_td_stock_y_movimientos",
    "uat_bsj_datamart_control_gestion.productos_valores_negociables_cheques",
    "uat_bsj_datamart_control_gestion.productos_valores_negociables_dim_maestro",
    "uat_bsj_datamart_control_gestion.productos_valores_negociables_ft_movimientos",
    "uat_bsj_datamart_control_gestion.seguimiento_td",
    "uat_bsj_datamart_control_gestion.vn_cheques",
    "uat_bsj_datamart_control_gestion.vn_relacion_clientes",
    "uat_bsj_datamart_control_gestion.vw_clientes_rel_vn",
    "uat_bsj_datamart_control_gestion.vw_maestro_vn",
    "uat_bsj_datamart_control_gestion.vw_prod_vn_cheques",
    "uat_bsj_datamart_control_gestion.vw_productos_valores_negociables_ft_movimientos",
    "uat_bsj_datamart_riesgos.can_ges_homebanking_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.clientes_datos_adicionales_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.clientes_datos_identificatorios_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.clientes_datos_impositivos_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.clientes_legajo_digital_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.clientes_perfil_comercial_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.contabilidad_balance_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.contabilidad_mov_contables_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.legales_bastanteo_persona_juridica_dim_abt_empresa",
    "uat_bsj_datamart_riesgos.legales_denuncias_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.legales_mora_judicial_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.productos_haberes_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.productos_paquetes_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.productos_pf_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.productos_prestamos_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.productos_ttcc_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_antecedentes_negativos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_balance",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_afip",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_bcra",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_cheques",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_clientes",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_haberes",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_morosidad",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_nosis",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_bastanteo_tarjetas",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_datos_adicionales",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_datos_impositivos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_datos_personales",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_dim_abt_empresa",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_dim_workflow",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_calculosiniciales",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_clasificacionempresayrelacionado",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_filtrosduros",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_indexaciondedatos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosexternos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_requiereserviciosinternos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_score",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_scorepreburo",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_scorerelacionado",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_eva_script",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_home_banking",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_limites_y_garantias",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_mora",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_calculosfinales",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_calculosiniciales",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_decisionfinal",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_facturacioninferida",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_indexaciondedatos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_limitedegarantia",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_niveldefirma",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_postburo",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_reclasificacion",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_riesgocomputable",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_score",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_scorerelacionado",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_sublimitesdeproducto",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_topedecliente",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_tramites",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_verificaciones",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_of_vigencias",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_parametros_de_entrada",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_perfil_tecnico",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_prestamos",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_sucursales",
    "uat_bsj_datamart_riesgos.riesgos_adm_crediticia_tarjetas",
    "uat_bsj_datamart_riesgos.riesgos_dep_val_cheques_dim_abt_empresas",
    "uat_bsj_datamart_riesgos.riesgos_perfil_crediticio_dim_abt_empresa"
  ]
}

In [86]:
for k,v in json_consumo.items():
    not_uat_tables = [x for x in v if 'uat' not in x]
    json_consumo[k] = not_uat_tables

In [87]:
grouped_tables_by_zone.update(json_consumo)
print(grouped_tables_by_zone)

{'RAW': ['de_ber_1raw.acreditaciones_haberes', 'de_ber_1raw.adelanto_haberes', 'de_ber_1raw.anses_rud_beneficios', 'de_ber_1raw.archivo_segmentacion_bersa_1', 'de_ber_1raw.archivo_segmentacion_bersa_2', 'de_ber_1raw.archivo_segmentacion_bersa_3', 'de_ber_1raw.archivo_segmentacion_bersa_4', 'de_ber_1raw.ber_paq', 'de_ber_1raw.calificador_limites', 'de_ber_1raw.calificador_limites_deploy', 'de_ber_1raw.campania_mail_extrajudicial', 'de_ber_1raw.cant_atm_x_entidad', 'de_ber_1raw.captura_trx', 'de_ber_1raw.captura_trx_test2', 'de_ber_1raw.captura_trx_test3', 'de_ber_1raw.captura_trx_test4', 'de_ber_1raw.captura_trx_test5', 'de_ber_1raw.captura_trx_test6', 'de_ber_1raw.cierre_mensual_visa_mc', 'de_ber_1raw.cierres_tc_cart1_test', 'de_ber_1raw.cimfdbk_contratacionproducto', 'de_ber_1raw.cimfdbk_engage', 'de_ber_1raw.cimfdbk_icommkt', 'de_ber_1raw.cimfdbk_linkcli', 'de_ber_1raw.cimfdbk_notificacionoferta', 'de_ber_1raw.citasweb_appointment_client', 'de_ber_1raw.cliente_core', 'de_ber_1raw.cli

In [88]:
def translate_adj_list(adj_list, databases_dict, grouped_tables_by_zone):
    def find_tables_in_dict(grouped_tables_by_zone, table):
        zone, table_name = table.split('-')
        tables_for_zone = grouped_tables_by_zone.get(zone)
        if tables_for_zone:
            final_found_tables_list = list(filter(lambda x: table_name == x.split('.')[1], tables_for_zone))
            return final_found_tables_list
        else:
            return []
    #Check if tables exists in Hive for said zone and complete the adjacency list with the proper database.table name
    new_adj_list = {}
    for table in adj_list.keys():
        zone, table_name = table.split('-')
        #print ("table", table)
        proxy_dict = {}
        found_tables = find_tables_in_dict(grouped_tables_by_zone, table)
        for found_table in found_tables:
            entity = found_table.split('_')[1]
            proxy_dict[entity] = proxy_dict.setdefault(entity, []) + [found_table]
        affected_tables = adj_list[table]
        #print ("affected tables", affected_tables)
        for affected_table in affected_tables:
            found_tables = find_tables_in_dict(grouped_tables_by_zone, affected_table)
            for found_table in found_tables:
                entity = found_table.split('_')[1]
                proxy_dict[entity] = proxy_dict.setdefault(entity, []) + [found_table]
        for entity in proxy_dict.keys():
            root_table = proxy_dict[entity][0]
            if table.split('-')[1] == root_table.split('.')[1]:
                new_adj_list[proxy_dict[entity][0]] = proxy_dict[entity][1:]
    return new_adj_list

new_adj_list = translate_adj_list(table_adj_list, databases_dict, grouped_tables_by_zone)
print(json.dumps(new_adj_list, indent=2))

{
  "de_ber_4con.productos_parametria_dim_productos": [
    "de_ber_datamart_control_gestion.productos_prestamos_dim_maestro"
  ],
  "de_bsc_4con.productos_parametria_dim_productos": [
    "de_bsc_datamart_control_gestion.productos_prestamos_dim_maestro"
  ],
  "de_bsf_4con.productos_parametria_dim_productos": [
    "de_bsf_datamart_control_gestion.productos_prestamos_dim_maestro"
  ],
  "de_bsj_4con.productos_parametria_dim_productos": [
    "de_bsj_datamart_control_gestion.productos_prestamos_dim_maestro"
  ],
  "de_ber_3ref.productos_parametria_dim_productos": [
    "de_ber_4con.productos_parametria_dim_productos"
  ],
  "de_bsc_3ref.productos_parametria_dim_productos": [
    "de_bsc_4con.productos_parametria_dim_productos"
  ],
  "de_bsf_3ref.productos_parametria_dim_productos": [
    "de_bsf_4con.productos_parametria_dim_productos"
  ],
  "de_bsj_3ref.productos_parametria_dim_productos": [
    "de_bsj_4con.productos_parametria_dim_productos"
  ],
  "de_ber_2cur.productos_aampr": [

In [89]:
def find_database_zone(database):
    return ''.join([i for i in database.split('_')[2] if not i.isdigit()])

def find_entity(database):
    return database.split('_')[1]

def find_env(database):
    return database.split('_')[0]

In [ ]:
def get_final_data_recovery(adj_list, zone_table_dict):
    final_recovery_list = {}
    for table, affected_tables in new_adj_list.items():
        database, table_name = table.split('.')
        zone = find_database_zone(database)
        if 'bsf' in database:
            entity_type = 'bsf'
        else:
            entity_type = 'unisys'

        table_info = zone_table_dict.get(zone+';'+table_name+';'+entity_type)
        if not table_info:
            table_info = zone_table_dict.get(zone+';'+table_name+';'+'any')

        if table_info:
            if table_info.get('query'):
                query = table_info.get('query')\
                        .replace('$SUBENTORNO', find_env(database))\
                        .replace('$ENTIDAD', find_entity(database))
            else:
                query = None
            final_recovery_list[table] = {
                'database': database,
                'table_name': table_name,
                'create_table': "",
                'associated_term': table_info.get('associated_term'),
                'loading_query': query,
                'affected_tables': affected_tables
            }
    return final_recovery_list

final_recovery_list = get_final_data_recovery(new_adj_list, zone_table_dict)




In [97]:
print(json.dumps(final_recovery_list, indent=2))

{
  "de_ber_4con.productos_parametria_dim_productos": {
    "database": "de_ber_4con",
    "table_name": "productos_parametria_dim_productos",
    "create_table": "",
    "associated_term": "productos_parametria_dim_productos_unisys",
    "loading_query": "SELECT id_concepto AS id_concepto, cod_producto AS cod_producto, id_moneda AS id_moneda, fecha_proceso AS fecha_proceso, id_producto AS id_producto, marca_sfb AS marca_sfb, marca_producto_cta_comitente AS marca_producto_cta_comitente, cast(fecha_vencimiento_producto as varchar(10)) AS fecha_vencimiento_producto, cast(fecha_vigencia_producto as varchar(10)) AS fecha_vigencia_producto, desc_producto AS desc_producto, nro_campo_c_467 AS nro_campo_c_467, nro_campo_garantia AS nro_campo_garantia, nro_campo_lisol AS nro_campo_lisol, factor_ponderacion AS factor_ponderacion, fecha_vencimiento_producto_rel AS fecha_vencimiento_producto_rel, fecha_vigencia_producto_rel AS fecha_vigencia_producto_rel, estado AS estado, marca_producto_privado A

In [95]:
import os

file_path = os.path.abspath("data/data.json")

In [96]:
# Specify the file path where you want to save the JSON file
file_path = "data/data.json"

# Open the file in write mode and use json.dump to write the data to the file
with open(file_path, 'w') as json_file:
    json.dump(final_recovery_list, json_file)

In [ ]:
final_recovery_list

In [150]:
len(final_recovery_list.keys())

717

In [ ]:
final_recovery_list

## Desde una query ver que tablas estan involucradas

## Que tablas no se están usando

## Que tabla son mas importantes (frecuencia de nombracion de cada tabla)

In [ ]:
from impala.dbapi import connect
from thrift.transport.TTransport import TTransportException
import json

# List all databases in Impala
impala_host = "172.30.213.211"
impala_port = "21050"
impala_user = "ediogo"

impala_conn_raw = connect(
    host=impala_host,
    port=impala_port,
    user = impala_user)

databases_dict = {}
grouped_tables_by_zone = {}

impala_cursor_raw = impala_conn_raw.cursor()
impala_cursor_raw.execute('SHOW DATABASES')
databases = list(map(lambda x: x[0], impala_cursor_raw.fetchall()))

# List tables in impala database
for database in databases:
    if 'con' in database or 'datamart' in database:
        if 'con' in database:
            zone = 'CON'
        if 'datamart' in database:
            zone = 'DATAMART'
        grouped_tables_by_zone.setdefault(zone, [])
        if 'ber' in database or 'bsf' in database or 'bsj' in database or 'bsc' in database:
            impala_conn_raw.close()
            impala_conn_raw = connect(host=impala_host, port=impala_port, user=impala_user, database=database)
            impala_cursor_raw = impala_conn_raw.cursor()
            impala_cursor_raw.execute('SHOW TABLES')
            tables_in_database = list(map(lambda x: x[0], impala_cursor_raw.fetchall()))
            databases_dict[database] = tables_in_database
            grouped_tables_by_zone[zone] = grouped_tables_by_zone[zone]+list(map(lambda x: database+'.'+x, tables_in_database))

print(json.dumps(grouped_tables_by_zone, indent=2))

In [ ]:
#INTENTAR DIBUJARLO

import networkx as nx
import matplotlib.pyplot as plt
from matplotlib import pylab
%matplotlib inline

G = nx.Graph()
G.add_nodes_from(table_adj_list.keys())
for k,v in table_adj_list.items():
    for node in v:
        G.add_edge(k, node)

plt.figure(figsize=(10,6))
#pos = nx.spring_layout(G, k=0.8)
nx.draw(G, with_labels = True, width=1, 
        node_color='lightblue', node_size=40)

In [ ]:
## Como seguirlo
